In [1]:
import pandas as pd
import numpy as np
from fuzzywuzzy import fuzz
from fuzzywuzzy import process

C:\Users\vigrose\AppData\Local\Continuum\anaconda3\lib\site-packages\fuzzywuzzy\fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [6]:
GOV_HOSPITAL = pd.read_csv('Gov_Hospitals.csv')
GOV_HOSPITAL=GOV_HOSPITAL[GOV_HOSPITAL.STATUS=='OPEN']
npi_hospitals = pd.read_csv('NPI_ATTEMPT.csv')

In [34]:
npi_with_taxes = npi_with_taxes.fillna('None')

In [38]:
npi_hospitals = pd.read_csv('NPI_HOSPITALS_2.csv')
npi_hospitals = npi_hospitals.fillna('None')

In [3]:
addr_translate = {
    'DR': 'DRIVE',
    'PKWY': 'PARKWAY',
    'RD': 'ROAD',
    'ST': 'STREET',
    'STE': 'SUITE',
    'N': 'NORTH',
    'S': 'SOUTH',
    'E': 'EAST',
    'W': 'WEST',
    'LN': 'LANE',
    'CTR': 'CENTER',
    'CT': 'COURT',
    'BLVD': 'BOULEVARD',
    'CIR': 'CIRCLE',
    'HTS': 'HEIGHTS',
    'AVE': 'AVENUE',
    'HWY': 'HIGHWAY',
    'JCT': 'JUNCTION',
    'LK': 'LAKE',
    'MTN': 'MTN',
    'APT': 'APARTMENT',
    'RM': 'ROOM',
    'PL': 'PLACE',
    'PLZ': 'PLACA',
    'RDG': 'RIDGE',
    'SQ': 'SQUARE',
    'STA': 'STATION',
    'TER': 'TERRACE',
    'TRL': 'TRAIL',
    'TPKE': 'TURNPIKE',
    'VLY': 'VALLEY',
    'IS': 'ISLAND'
}


def translate_addr(addr_string):
    addr_string = addr_string.replace('.','')
    addr_string = addr_string.upper()
    new_addr = []
    
    tokens = addr_string.split()
    
    for t in tokens:
        if t in addr_translate:
            new_addr.append(addr_translate[t])
        else:
            new_addr.append(t)
    
    return ' '.join(new_addr)

def get_numbers(add1, add2):
    num1 = add1.split(' ')[0]
    num2 = add2.split(' ')[0]
    if num1.isnumeric() and num2.isnumeric():
        add1 = add1.replace((num1 + ' '), '')
        add2 = add2.replace((num2 + ' '), '')
        return([num1, add1],[num2,add2])
    else:
        return(False)

In [4]:
def match_address(address_1, address_2):
    address_1 = translate_addr(address_1)
    address_2 = translate_addr(address_2)
    
    if get_numbers(address_1, address_2) != False:
        add1, add2 = get_numbers(address_1, address_2)
        if add1[0] ==add2[0] and add1[1] == add2[1]:
            return(True)
        if fuzz.ratio(add1[0],add2[0]) > 80 and fuzz.ratio(add1[1],add2[1]) > 80:
            return('Maybe')
    if fuzz.ratio(address_1,address_2) > 80:
        return('Maybe')
    return(False)

In [5]:
def match_address_2(address_1, address_2):
    address_1 = translate_addr(address_1)
    address_2 = translate_addr(address_2)
    
    if get_numbers(address_1, address_2) != False:
        add1, add2 = get_numbers(address_1, address_2)
        if add1[0] ==add2[0] and add1[1] == add2[1]:
            return(100)
        else:
            score = (fuzz.ratio(add1[0],add2[0]) + fuzz.ratio(add1[1],add2[1]))/2
            return(score)
    else:
        return(fuzz.ratio(address_1,address_2))

In [166]:
fuzz.ratio('10819 S. Drake','s drake ave')

40

In [164]:
match_address_2('10819 S. Drake','10819 s drake ave')

88.0

In [7]:
dict_list = []
matched_count = 0
unmatched_count = 0
UNMATCHED_LIST =[]
for row in GOV_HOSPITAL.itertuples():
    print(row.NAME)
    
    npi_match = 'None'

    new_df =  npi_hospitals[(npi_hospitals['LOCATION_CITY']==row.CITY) &(npi_hospitals['LOCATION_STATE']==row.STATE)].sort_values('LOCATION_ADDRESS_1')
    match = False

    for line in new_df.itertuples():
        if match_address(row.ADDRESS,line.LOCATION_ADDRESS_1) == True:
            print(f'{row.ADDRESS} matched to {line.LOCATION_ADDRESS_1}!')
            if fuzz.ratio(row.NAME,line.NAME)>65 or fuzz.ratio(row.NAME,line.OTHER_NAME)>65:
                print("**********")
                print(f'VERY LIKELY Match: {line.NAME} / {line.OTHER_NAME}') 
                print("**********")
                match = True
                break 
        elif match_address(row.ADDRESS,line.LOCATION_ADDRESS_1) == 'Maybe':
            print(f'{row.ADDRESS} matched to {line.LOCATION_ADDRESS_1}!')
            print(f'Potential Match: {line.NAME} / {line.OTHER_NAME}')    
            print('---')
            if fuzz.ratio(row.NAME,line.NAME)>80 or fuzz.ratio(row.NAME,line.OTHER_NAME)>80:
                print("**********")
                print(f'VERY LIKELY Match: {line.NAME} / {line.OTHER_NAME}') 
                print("**********")
                match = True
                break 
            
        
    if match == False:
        
        new_df =  npi_hospitals[npi_hospitals['LOCATION_STATE']==row.STATE]
        
        for line in new_df.itertuples():
            if match_address(row.ADDRESS,line.LOCATION_ADDRESS_1) == True:
                print(f'{row.ADDRESS} matched to {line.LOCATION_ADDRESS_1}!')
                if fuzz.ratio(row.NAME,line.NAME)>65 or fuzz.ratio(row.NAME,line.OTHER_NAME)>65:
                    print("**********")
                    print(f'VERY LIKELY Match: {line.NAME} / {line.OTHER_NAME}') 
                    print("**********")
                    match = True
                    break 
            elif match_address(row.ADDRESS,line.LOCATION_ADDRESS_1) == 'Maybe':
                print(f'{row.ADDRESS} matched to {line.LOCATION_ADDRESS_1}!')
                print(f'Potential Match: {line.NAME} / {line.OTHER_NAME}')    
                print('---')
                if fuzz.ratio(row.NAME,line.NAME)>80 or fuzz.ratio(row.NAME,line.OTHER_NAME)>80:
                    print("**********")
                    print(f'VERY LIKELY Match: {line.NAME} / {line.OTHER_NAME}') 
                    print("**********")
                    match = True
                    break 
            
                
    if match == True:
        matched_count += 1
        new_dict = {
            'ID': row.ID,
            'NPI': line.NPI
        }
        dict_list.append(new_dict)
    if match == False:
        print(f'{row.NAME} did not match :(')
        print(f'Address is {row.ADDRESS} in {row.CITY},{row.STATE}')
        unmatched_count += 1
        UNMATCHED_LIST.append(row.ID)
    print('')
    print('')

ADENA GREENFIELD MEDICAL CENTER
550 MIRABEAU STREET matched to 550 MIRABEAU ST!
**********
VERY LIKELY Match: GREENFIELD AREA MEDICAL CENTER / None
**********


POMERENE HOSPITAL
981 WOOSTER ROAD matched to 981 WOOSTER RD!
**********
VERY LIKELY Match: HOLMES COUNTY JOEL POMERENE MEMORIAL HOSPITAL / JOEL POMERENE MEMORIAL HOSPITAL
**********


LICKING MEMORIAL HOSPITAL
1320 WEST MAIN STREET matched to 1320 W MAIN ST!
**********
VERY LIKELY Match: LICKING MEMORIAL HOSPITAL / None
**********


MARY RUTAN HOSPITAL
205 PALMER AVENUE matched to 205 PALMER AVENUE!
**********
VERY LIKELY Match: MARY RUTAN HOSPITAL / None
**********


MERCY ALLEN HOSPITAL
200 WEST LORAIN STREET matched to 200 W LORAIN ST!
**********
VERY LIKELY Match: MERCY HEALTH-ALLEN HOSPITAL LLC / MERCY HEALTH ALLEN HOSPITAL
**********


NORTHSIDE MEDICAL CENTER
500 GYPSY LANE matched to 500 GYPSY LANE!
500 GYPSY LANE matched to 500 GYPSY LANE!
**********
VERY LIKELY Match: NORTHSIDE MEDICAL CENTER / None
**********


VALL

VA SOUTHERN NEVADA HEALTHCARE SYSTEM did not match :(
Address is 1700 VEGAS DRIVE in LAS VEGAS,NV


DOCTORS MEMORIAL HOSPITAL
2600 HOSPITAL DR matched to 2600 HOSPITAL DRIVE!
**********
VERY LIKELY Match: HOLMES COUNTY HOSPITAL CORPORATION / DOCTORS MEMORIAL HOSPITAL
**********


HEALTHSOUTH DEACONESS REHABILITATION HOSPITAL
4100 COVERT AVE matched to 4100 COVERT AVE!
**********
VERY LIKELY Match: ENCOMPASS HEALTH DEACONESS REHABILITATION HOSPITAL, LLC / ENCOMPASS HEALTH DEACONESS REHABILITATION HOSPITAL
**********


HARSHA BEHAVIORAL CENTER INC
HARSHA BEHAVIORAL CENTER INC did not match :(
Address is 1420 E CROSSING BLVD in TERRE HAUTE,IN


MERCY MEDICAL CENTER
1320 MERCY DRIVE NW matched to 1320 MERCY DR NW!
1320 MERCY DRIVE NW matched to 1320 MERCY DR NW!
**********
VERY LIKELY Match: MERCY MEDICAL CENTER, INC. / MERCY MEDICAL CENTER
**********


HIGHLAND RIDGE HOSPITAL
7309 SOUTH 180 WEST matched to 7309 S 180 W!
**********
VERY LIKELY Match: PHC OF UTAH, INC. / HIGHLAND RIDGE HOSP

MADISON COUNTY MEMORIAL HOSPITAL did not match :(
Address is 309 NE MARION ST in MADISON,FL


CHG HOSPITAL TUCSON, LLC
7220 EAST ROSEWOOD DR matched to 7220 E ROSEWOOD ST!
Potential Match: CHG HOSPITAL TUCSON, LLC / CORNERSTONE SPECIALTY HOSPITALS TUCSON
---
**********
VERY LIKELY Match: CHG HOSPITAL TUCSON, LLC / CORNERSTONE SPECIALTY HOSPITALS TUCSON
**********


ST VINCENT'S MEDICAL CENTER SOUTHSIDE
4201 BELFORT RD matched to 4201 BELFORT RD!
4201 BELFORT RD matched to 4205 BELFORT RD!
Potential Match: PEDIATRIX,INC / None
---
4201 BELFORT RD matched to 4205 BELFORT RD!
Potential Match: PEDIATRIX,INC / None
---
4201 BELFORT RD matched to 4201 BELFORT RD!
ST VINCENT'S MEDICAL CENTER SOUTHSIDE did not match :(
Address is 4201 BELFORT RD in JACKSONVILLE,FL


CAPITAL REGIONAL MEDICAL CENTER - GADSDEN MEMORIAL CAMPUS
23186 BLUE STAR HWY matched to 23186 BLUE STAR HIGHWAY!
23186 BLUE STAR HWY matched to 23186 BLUESTAR HIGHWAY!
Potential Match: ASHFORD HEALTHCARE SYSTEMS / GADSDEN COMMUNIT

5300 KIDSPEACE DRIVE matched to 5300 KIDSPEACE DR!
KIDSPEACE ORCHARD HILLS CAMPUS did not match :(
Address is 5300 KIDSPEACE DRIVE in OREFIELD,PA


LEBANON VETERANS AFFAIRS MEDICAL CENTER
1700 SOUTH LINCOLN AVENUE matched to 1700 LINCOLN AVE!
Potential Match: LEBANON VAMC / None
---
1700 SOUTH LINCOLN AVENUE matched to 1700 S LINCOLN AVE!
1700 SOUTH LINCOLN AVENUE matched to 1700 LINCOLN AVE!
Potential Match: LEBANON VAMC / None
---
1700 SOUTH LINCOLN AVENUE matched to 100 LINCOLN AVE!
Potential Match: MARIAN COMMUNITY HOSPITAL / None
---
1700 SOUTH LINCOLN AVENUE matched to 1700 S LINCOLN AVE!
LEBANON VETERANS AFFAIRS MEDICAL CENTER did not match :(
Address is 1700 SOUTH LINCOLN AVENUE in LEBANON,PA


MAIN LINE BRYN MAWR HOSPITAL
130 SOUTH BRYN MAWR AVENUE matched to 130 S BRYN MAWR AVE!
**********
VERY LIKELY Match: MAIN LINE HOSPITALS, INC. / BRYN MAWR HOSPITAL
**********


INDIANA REGIONAL MEDICAL CENTER
INDIANA REGIONAL MEDICAL CENTER did not match :(
Address is 835 HOSPITAL ROAD,

1625 E JEFFERSON BLVD matched to 7970 W JEFFERSON BLVD!
Potential Match: REHAB HOSPITAL OF FORT WAYNE GENERAL PARTNERSHIP / REHABILITATION HOSPITAL OF FORT WAYNE GENERAL PARTNERSHIP
---
1625 E JEFFERSON BLVD matched to 112 W JEFFERSON BLVD!
Potential Match: NEUROLOGY AND PAIN MANAGEMENT / None
---
1625 E JEFFERSON BLVD matched to 7952 W JEFFERSON BLVD!
Potential Match: LUTHERAN MUSCULOSKELETAL CENTER LLC / THE ORTHOPAEDIC HOSPITAL OF LUTHERAN HEALTH NETWORK
---
1625 E JEFFERSON BLVD matched to 7950 W JEFFERSON BLVD!
Potential Match: IOM HEALTH SYSTEM LP / LUTHERAN HOSPITAL OF INDIANA
---
1625 E JEFFERSON BLVD matched to 1625 E JEFFERSON BLVD!
MEDICAL BEHAVIORAL HOSPITAL - MISHAWAKA did not match :(
Address is 1625 E JEFFERSON BLVD in MISHAWAKA,IN


WOODLAWN HOSPITAL
1400 E 9TH ST matched to 1400 E 9TH ST!
**********
VERY LIKELY Match: WOODLAWN HOSPITAL / None
**********


SOUTHERN ARIZONA VA HEALTH CARE SYSTEM
3601 S 6TH AVE matched to 3601 S 6TH AVE!
3601 S 6TH AVE matched to 1201 S 7

...

88TH MEDICAL GROUP - WRIGHT-PATTERSON AIR FORCE BASE MEDICAL CENTER did not match :(
Address is 4881 SUGAR MAPLE DR in WRIGHT PATTERSON AFB,OH


FORT LEONARD WOOD ARMY COMMUNITY HOSPITAL
4430 MISSOURI AVE matched to 126 MISSOURI AVE!
Potential Match: GENERAL LEONARD WOOD ARMY COMMUNITY HOSPITAL / MEDDAC
---
**********
VERY LIKELY Match: GENERAL LEONARD WOOD ARMY COMMUNITY HOSPITAL / MEDDAC
**********


KINDRED HOSPITAL - TARRANT COUNTY
1000 NORTH COOPER STREET matched to 1000 N COOPER ST!
**********
VERY LIKELY Match: TRANSITIONAL HOSPITALS CORPORATION OF TEXAS, LLC / KINDRED HOSPITAL - TARRANT COUNTY
**********


ALASKA VA HEALTHCARE SYSTEM
1201 N MULDOON RD matched to 1201 N MULDOON RD!
1201 N MULDOON RD matched to 1201 N MULDOON RD!
ALASKA VA HEALTHCARE SYSTEM did not match :(
Address is 1201 N MULDOON RD in ANCHORAGE,AK


VA MEDICAL CENTER - NEWINGTON CAMPUS
555 WILLARD AVE matched to 555 WILLARD AVE!
**********
VERY LIKELY Match: DEPARTMENT OF VETERAN AFFAIRS / VA MEDICAL CENTER N

7601 FANNIN STREET matched to 6400 FANNIN ST!
Potential Match: DEERBROOK CARDIOLOGY, PLLC / None
---
7601 FANNIN STREET matched to 6400 FANNIN ST!
Potential Match: MEMORIAL HERMANN HOSPITAL SYSTEM / None
---
7601 FANNIN STREET matched to 6411 FANNIN ST!
Potential Match: MEMORIAL HERMANN HEALTH SYSTEM / MEMORIAL HERMANN HOSPITAL
---
7601 FANNIN STREET matched to 6411 FANNIN ST!
Potential Match: VA NORTH TEXAS HEALTH CARE SYSTEM / None
---
7601 FANNIN STREET matched to 6411 FANNIN ST!
Potential Match: UT HEALTH / None
---
7601 FANNIN STREET matched to 6411 FANNIN ST!
Potential Match: UNIVERSITY OF TEXAS HEALTH SCIENCE CENTER HOUSTON / None
---
7601 FANNIN STREET matched to 6431 FANNIN ST!
Potential Match: UNIVERSITY OF TEXAS MEDICAL FOUNDATION / None
---
7601 FANNIN STREET matched to 6501 FANNIN ST!
Potential Match: BAYLOR COLLEGE OF MEDICINE / None
---
7601 FANNIN STREET matched to 6550 FANNIN ST!
Potential Match: TMH PHYSICIAN ORGANIZATION / None
---
7601 FANNIN STREET matched to 6550 

PAM REHABILITATION HOSPITAL OF BEAUMONT did not match :(
Address is 3340 PLAZA 10 BOULEVARD in BEAUMONT,TX


HEALTHSOUTH REHABILITATION HOSPITAL OF THE MID-CITIES
2304 STATE HIGHWAY 121 matched to 2304 HIGHWAY 121!
Potential Match: ENCOMPASS REHABILITATION HOSPITAL OF THE MID-CITIES, LLC / ENCOMPASS HEALTH REHABILITATION HOSPITAL OF THE MID-CITIES
---
**********
VERY LIKELY Match: ENCOMPASS REHABILITATION HOSPITAL OF THE MID-CITIES, LLC / ENCOMPASS HEALTH REHABILITATION HOSPITAL OF THE MID-CITIES
**********


VIBRA REHABILITATION HOSPITAL OF AMARILLO
7200 WEST 9TH STREET matched to 1201 W 38TH ST!
Potential Match: PEDIATRIX MEDICAL GROUP / None
---
7200 WEST 9TH STREET matched to 1201 E 9TH ST!
Potential Match: VETERANS AFFAIRS HOSPITAL / SAM RAYBURN MEMORIAL MEDICAL CENTER
---
7200 WEST 9TH STREET matched to 1100 W 34TH ST!
Potential Match: BAYLOR COLLEGE OF MEDICINE / None
---
7200 WEST 9TH STREET matched to 1201 W 38TH ST!
Potential Match: SETON MEDICAL CENTER AUSTIN / None
---
7200

1815 SOUTH 31ST STREET matched to 2401 S 31ST ST!
Potential Match: SCOTT AND WHITE MEMORIAL HOSPITAL / None
---
1815 SOUTH 31ST STREET matched to 2401 S 31ST ST!
Potential Match: SCOTT AND WHITE HOSPITAL / None
---
1815 SOUTH 31ST STREET matched to 1901 S 1ST ST!
Potential Match: VETERANS ADMINISTRATION MEDICAL CENTER / None
---
1815 SOUTH 31ST STREET matched to 708 S 1ST ST!
Potential Match: MULESHOE AREA HOSPITAL DISTRICT / MULESHOE AREA MEDICAL CENTER
---
1815 SOUTH 31ST STREET matched to 2401 S 31ST ST!
Potential Match: SCOTT AND WHITE HEALTH PLAN / None
---
1815 SOUTH 31ST STREET matched to 2401 S 31ST ST!
Potential Match: SCOTT & WHITE HEALTHCARE / None
---
1815 SOUTH 31ST STREET matched to 2401 S 31ST ST!
Potential Match: SCOTT & WHITE HOSPITAL / None
---
1815 SOUTH 31ST STREET matched to 2401 S 31ST ST!
Potential Match: SCOTT AND WHITE / None
---
1815 SOUTH 31ST STREET matched to 2401 S 31ST ST!
Potential Match: SCOTT AND WHITE HEALTHCARE / None
---
1815 SOUTH 31ST STREET match

MIDTOWN OAKS POST-ACUTE did not match :(
Address is 2600 L STREET in SACRAMENTO,CA


PIKES PEAK REGIONAL HOSPITAL
16420 HIGHWAY 24 matched to 16420 WEST HIGHWAY 24!
Potential Match: UCHEALTH PIKES PEAK REGIONAL HOSPITAL / None
---
**********
VERY LIKELY Match: UCHEALTH PIKES PEAK REGIONAL HOSPITAL / None
**********


FAIRVIEW DEVELOPMENTAL CENTER
2501 HARBOR BOULEVARD matched to 2501 HARBOR BLVD!
**********
VERY LIKELY Match: STATE OF CALIFORNIA - DEPARTMENT OF DEVELOPMENTAL SERVICES / FAIRVIEW DEVELOPMENTAL CENTER
**********


CORNERSTONE MEDICAL CENTER
100 GROSS CRESCENT CIRCLE matched to 100 GROSS CRESCENT CIR!
**********
VERY LIKELY Match: CORNERSTONE MEDICAL CENTER, LLC / None
**********


SELECT SPECIALTY HOSPITAL - MIDTOWN ATLANTA
705 JUNIPER STREET NE matched to 705 JUNIPER ST NE!
**********
VERY LIKELY Match: SELECT SPECIALTY HOSPITAL - MIDTOWN ATLANTA, LLC / None
**********


PIEDMONT NEWTON HOSPITAL
5126 HOSPITAL DRIVE matched to 5126 HOSPITAL DR NE!
Potential Match: NEWTON 

In [12]:
new_match_df = pd.DataFrame(dict_list)
pd.merge(npi_hospitals, new_match_df, on='NPI')

NPI                    Taxonomies  \
0     1841237575                ['282N00000X']   
1     1144268723                ['282NR1301X']   
2     1952349870                ['284300000X']   
3     1205955747  ['207L00000X', '282N00000X']   
4     1124147277                ['282N00000X']   
...          ...                           ...   
5306  1619351160                ['282N00000X']   
5307  1730544313                ['282NR1301X']   
5308  1184802480  ['273Y00000X', '282N00000X']   
5309  1932109048                ['282NC0060X']   
5310  1467836841                ['282N00000X']   

                                          NAME  \
0                 LANE REGIONAL MEDICAL CENTER   
1                   LINDSAY MUNICIPAL HOSPITAL   
2                 ALLENTOWN SPECIALTY HOSPITAL   
3                       GIFFORD MEDICAL CENTER   
4                  THOMAS JEFFERSON UNIVERSITY   
...                                        ...   
5306               UCHEALTH GRANDVIEW HOSPITAL   
5307              RIDGECREST REGIONAL HOSPITAL   
5308                      KINGMAN HOSPITAL INC   
5309                  GUNNISON VALLEY HOSPITAL   
5310  PROVIDENCE HOSPITAL OF NORTH HOUSTON LLC   

                                             OTHER_NAME  \
0                                                  None   
1                                                  None   
2                      GOOD SHEPHERD SPECIALTY HOSPITAL   
3                                         ANSTHESIOLOGY   
4                                                  None   
...                                                 ...   
5306             UCHEALTH COLORADO SPRINGS HOSPITAL LLC   
5307                                               None   
5308  KINGMAN REGIONAL MEDICAL CENTER - HUALAPAI MOU...   
5309                                               None   
5310                                               None   

           MAILING_ADDRESS_1    MAILING_ADDRESS_2     MAILING_CITY  \
0           6300 MAIN STREET                 None          ZACHARY   
1                 PO BOX 888                 None          LINDSAY   
2               850 S 5TH ST  GOOD SHEPHERD PLAZA        ALLENTOWN   
3               44 S MAIN ST                 None         RANDOLPH   
4          329 SKIPPACK PIKE                 None  FORT WASHINGTON   
...                      ...                  ...              ...   
5306       7901 E LOWRY BLVD      F402, 3RD FLOOR           DENVER   
5307  1081 N CHINA LAKE BLVD                 None       RIDGECREST   
5308   3269 STOCKTON HILL RD                 None          KINGMAN   
5309         711 N TAYLOR ST                 None         GUNNISON   
5310        5037B FM 2920 RD                 None           SPRING   

     MAILING_STATE MAIING_ZIP MAILING_PHONE      LOCATION_ADDRESS_1  \
0               LA  707914099    2256584316        6300 MAIN STREET   
1               OK  730520888    4057561404      1305 W CHEROKEE ST   
2               PA  181033308    6107768303  2545 SCHOENERSVILLE RD   
3               VT  050601381    8027287000            44 S MAIN ST   
4               PA  190342011    2157934035           111 S 11TH ST   
...            ...        ...           ...                     ...   
5306            CO      80230    7205531700     5623 PULPIT PEAK VW   
5307            CA  935553130    7604993900  1011 N CHINA LAKE BLVD   
5308            AZ  864093619    9287570626      3801 SANTA ROSA DR   
5309            CO  812302296    9706411456         711 N TAYLOR ST   
5310            TX  773883114    2814537916     16750 RED OAK DRIVE   

         LOCATION_ADDRESS_2     LOCATION_CITY LOCATION_STATE LOCATION_ZIP  \
0                      None           ZACHARY             LA    707914099   
1                      None           LINDSAY             OK    730525042   
2     4TH FLOOR SOUTH TOWER         BETHLEHEM             PA    180177300   
3                      None          RANDOLPH             VT    050601381   
4                SUITE 

In [17]:
unmatched_still = GOV_HOSPITAL[GOV_HOSPITAL.ID.isin(UNMATCHED_LIST)]

In [84]:
def match_hospital_datasets(GOV_HOSPITAL, npi_hospitals):   
    dict_list = []
    matched_count = 0
    unmatched_count = 0
    UNMATCHED_LIST =[]
    for row in GOV_HOSPITAL.itertuples():
        print(row.NAME)
        print(F'Scanning city {row.CITY}...')
        print('')
        npi_match = 'None'

        new_df =  npi_hospitals[(npi_hospitals['LOCATION_CITY']==row.CITY) &(npi_hospitals['LOCATION_STATE']==row.STATE)].sort_values('LOCATION_ADDRESS_1')
        match = False
        
        best_name_score = 0
        npi_number = 'None'
        address_match =False
        
        for line in new_df.itertuples():
            if match_address(row.ADDRESS,line.LOCATION_ADDRESS_1) == True:
                print(f'{row.ADDRESS} matched to {line.LOCATION_ADDRESS_1}!')
                print(f'Potential Match: {line.NAME} / {line.OTHER_NAME}')
                print('---')
                if fuzz.ratio(row.NAME,line.NAME)>65 or fuzz.ratio(row.NAME,line.OTHER_NAME)>65:
                    print("**********")
                    print(f'VERY LIKELY Match: {line.NAME} / {line.OTHER_NAME}') 
                    print("**********")
                    match = True
                    break 
                elif fuzz.ratio(row.NAME,line.NAME)>best_name_score or fuzz.ratio(row.NAME,line.OTHER_NAME)>best_name_score:
                    best_name_score= max([fuzz.ratio(row.NAME,line.NAME),fuzz.ratio(row.NAME,line.OTHER_NAME)])
                    name = line.NAME
                    other_name = line.OTHER_NAME
                    npi_number = line.NPI
                    address_match = True
                    
            elif match_address(row.ADDRESS,line.LOCATION_ADDRESS_1) == 'Maybe':
                print(f'{row.ADDRESS} matched to {line.LOCATION_ADDRESS_1}!')
                print(f'Potential Match: {line.NAME} / {line.OTHER_NAME}')    
                print('---')
                if fuzz.ratio(row.NAME,line.NAME)>80 or fuzz.ratio(row.NAME,line.OTHER_NAME)>80:
                    print("**********")
                    print(f'VERY LIKELY Match: {line.NAME} / {line.OTHER_NAME}') 
                    print("**********")
                    match = True
                    break 


        if match == False:
            if address_match == True:
                match = True
                print(f'Best Match: {name} / {other_name}')
            if address_match == False:
                print(F'Scanning whole state {row.STATE}...')
                print('')
                new_df =  npi_hospitals[npi_hospitals['LOCATION_STATE']==row.STATE]

                for line in new_df.itertuples():
                    if match_address(row.ADDRESS,line.LOCATION_ADDRESS_1) == True:
                        print(f'{row.ADDRESS} matched to {line.LOCATION_ADDRESS_1}, {line.LOCATION_CITY}!')
                        print(f'Potential Match: {line.NAME} / {line.OTHER_NAME}') 
                        print('---')
                        if fuzz.ratio(row.NAME,line.NAME)>65 or fuzz.ratio(row.NAME,line.OTHER_NAME)>65:
                            print("**********")
                            print(f'VERY LIKELY Match: {line.NAME} / {line.OTHER_NAME}') 
                            print("**********")
                            match = True
                            break 
                    elif match_address(row.ADDRESS,line.LOCATION_ADDRESS_1) == 'Maybe':
                        print(f'{row.ADDRESS} matched to {line.LOCATION_ADDRESS_1}, {line.LOCATION_CITY}!')
                        print(f'Potential Match: {line.NAME} / {line.OTHER_NAME}')    
                        print('---')
                        if fuzz.ratio(row.NAME,line.NAME)>80 or fuzz.ratio(row.NAME,line.OTHER_NAME)>80:
                            print("**********")
                            print(f'VERY LIKELY Match: {line.NAME} / {line.OTHER_NAME}') 
                            print("**********")
                            match = True
                            break 


        if match == True:
            matched_count += 1
            if npi_number == 'None':
                npi_number = line.NPI
            new_dict = {
                'ID': row.ID,
                'NPI': npi_number
            }
            dict_list.append(new_dict)
        if match == False:
            print(f'{row.NAME} did not match :(')
            print(f'Address is {row.ADDRESS} in {row.CITY},{row.STATE}')
            unmatched_count += 1
            UNMATCHED_LIST.append(row.ID)
        print('')
        print('')
        
    return(dict_list, UNMATCHED_LIST, matched_count, unmatched_count)

In [85]:
new_dict_list, new_UNMATCHED_LIST, new_matched_count, new_unmatched_count = match_hospital_datasets(GOV_HOSPITAL[GOV_HOSPITAL.ID.isin(UNMATCHED_LIST)], npi_hospitals)

NORTHSIDE MEDICAL CENTER
Scanning city YOUNGSTOWN...

500 GYPSY LANE matched to 500 GYPSY LN!
Potential Match: WESTERN RESERVE CARE SYSTEM / None
---
500 GYPSY LANE matched to 510 GYPSY LN!
Potential Match: FORUM HEALTH / None
---
Best Match: WESTERN RESERVE CARE SYSTEM / None


VALLEY VIEW MEDICAL CENTER
Scanning city CEDAR CITY...

1303 NORTH MAIN STREET matched to 1303 N MAIN ST!
Potential Match: IHC HEALTH SERVICES INC / CEDAR CITY HOSPITAL
---
Best Match: IHC HEALTH SERVICES INC / CEDAR CITY HOSPITAL


GILA REGIONAL MEDICAL CENTER
Scanning city SILVER CITY...

Scanning whole state NM...

GILA REGIONAL MEDICAL CENTER did not match :(
Address is 1313 EAST 32ND STREET in SILVER CITY,NM


GLENWOOD STATE HOSPITAL SCHOOL
Scanning city GLENWOOD...

Scanning whole state IA...

711 SOUTH VINE STREET matched to 1316 S MAIN ST, CLARION!
Potential Match: IOWA SPECIALTY HOSPITAL-CLARION / None
---
711 SOUTH VINE STREET matched to 1316 S MAIN ST, CLARION!
Potential Match: IOWA SPECIALTY HOSPITA

145 NORTH 6TH STREET matched to 145 N 6TH ST!
Potential Match: ST. JOSEPH REGIONAL HEALTH NETWORK / ST. JOSEPH MEDICAL CENTER PARTIAL HOSPITALIZATION PR
---
Best Match: ST. JOSEPH REGIONAL HEALTH NETWORK / ST. JOSEPH MEDICAL CENTER PARTIAL HOSPITALIZATION PR


HANOVER HOSPITAL
Scanning city HANOVER...

300 HIGHLAND AVENUE matched to 300 HIGHLAND AVE!
Potential Match: UPMC HANOVER / UPMC PINNACLE HANOVER
---
Best Match: UPMC HANOVER / UPMC PINNACLE HANOVER


CHILDRENS HOME OF PITTSBURGH
Scanning city PITTSBURGH...

5324 PENN AVENUE matched to 225 PENN AVENUE!
Potential Match: LIFECARE HOSPITALS OF PITTSBURGH / None
---
5324 PENN AVENUE matched to 4401 PENN AVE!
Potential Match: UPMC CHILDREN'S HOSPITAL OF PITTSBURGH / None
---
Scanning whole state PA...

5324 PENN AVENUE matched to 225 PENN AVENUE, PITTSBURGH!
Potential Match: LIFECARE HOSPITALS OF PITTSBURGH / None
---
5324 PENN AVENUE matched to 401 PENN AVE, SCRANTON!
Potential Match: DEPARTMENT OF MILITARY COMMONWEALTH OF PENNSYLVAN

SOUTHWEST IDAHO ADVANCED CARE HOSPITAL did not match :(
Address is 6651 W. FRANKLIN ROAD in BOISE,ID


CHESAPEAKE REGIONAL MEDICAL CENTER
Scanning city CHESAPEAKE...

736 BATTLEFIELD BOULEVARD NORTH matched to 736 BATTLEFIELD BLVD N!
Potential Match: CHESAPEAKE HOSPITAL AUTHORITY / CHESAPEAKE GENERAL HOSPITAL
---
Best Match: CHESAPEAKE HOSPITAL AUTHORITY / CHESAPEAKE GENERAL HOSPITAL


INOVA ALEXANDRIA HOSPITAL
Scanning city ALEXANDRIA...

Scanning whole state VA...

INOVA ALEXANDRIA HOSPITAL did not match :(
Address is 4320 SEMINARY ROAD in ALEXANDRIA,VA


SAINT ALPHONSUS MEDICAL CENTER - NAMPA
Scanning city NAMPA...

Scanning whole state ID...

SAINT ALPHONSUS MEDICAL CENTER - NAMPA did not match :(
Address is 1512 12TH AVENUE ROAD in NAMPA,ID


VALLEY HEALTH WARREN MEMORIAL HOSPITAL
Scanning city FRONT ROYAL...

1000 SHENANDOAH AVENUE matched to 1000 NORTH SHENANDOAH AVE!
Potential Match: WARREN MEMORIAL HOSPITAL, INC. / None
---
Scanning whole state VA...

1000 SHENANDOAH AVENUE ma

10 NICHOLS ST matched to 10 NICHOLLS ST, DAVENPORT!
Potential Match: LINCOLN COUNTY HOSPITAL DISTRICT 3 / LINCOLN HOSPITAL SWING BED
---
LINCOLN HOSPITAL did not match :(
Address is 10 NICHOLS ST in DAVENPORT,WA


SHRINERS HOSPITALS FOR CHILDREN
Scanning city GALVESTON...

Scanning whole state TX...

SHRINERS HOSPITALS FOR CHILDREN did not match :(
Address is 815 MARKET STREET in GALVESTON,TX


TEXAS CHILDREN'S HOSPITAL WEST CAMPUS
Scanning city HOUSTON...

18200 KATY FREEWAY matched to 18400 KATY FWY!
Potential Match: FAMILY HEALTH CONSULTANTS P A / None
---
Scanning whole state TX...

18200 KATY FREEWAY matched to 18400 KATY FWY, HOUSTON!
Potential Match: FAMILY HEALTH CONSULTANTS P A / None
---
TEXAS CHILDREN'S HOSPITAL WEST CAMPUS did not match :(
Address is 18200 KATY FREEWAY in HOUSTON,TX


ST. ANTHONY HOSPITAL
Scanning city GIG HARBOR...

Scanning whole state WA...

ST. ANTHONY HOSPITAL did not match :(
Address is 11567 CANTERWOOD BLVD NW in GIG HARBOR,WA


NEWPORT HOSPITAL & HE

DEER'S HEAD CENTER did not match :(
Address is 315 DEER'S HEAD HOSPITAL ROAD in SALISBURY,MD


NEW YORK EYE AND EAR INFIRMARY
Scanning city NEW YORK...

310 E 14TH ST matched to 301 E 17TH ST!
Potential Match: NYU LANGONE HOSPITALS / None
---
Scanning whole state NY...

310 E 14TH ST matched to 301 E 17TH ST, NEW YORK!
Potential Match: NYU LANGONE HOSPITALS / None
---
NEW YORK EYE AND EAR INFIRMARY did not match :(
Address is 310 E 14TH ST in NEW YORK,NY


MEMORIAL HOSPITAL OF CARBONDALE
Scanning city CARBONDALE...

Scanning whole state IL...

MEMORIAL HOSPITAL OF CARBONDALE did not match :(
Address is 405 W JACKSON in CARBONDALE,IL


IROQUOIS MEMORIAL HOSPITAL
Scanning city WATSEKA...

Scanning whole state IL...

IROQUOIS MEMORIAL HOSPITAL did not match :(
Address is 200 FAIRMAN STREET in WATSEKA,IL


TRIGG COUNTY HOSPITAL INC.
Scanning city CADIZ...

Scanning whole state KY...

254 MAIN STREET matched to 11203 MAIN ST, MARTIN!
Potential Match: SAINT JOSEPH HEALTH SYSTEM INC / None
--

...

Scanning whole state TX...

3535 SOUTH INTERSTATE 35 EAST matched to 3500 S INTERSTATE 35, BELTON!
Potential Match: HMIH CEDAR CREST, LLC / CEDAR CREST HOSPITAL & RTC
---
MEDICAL CITY DENTON did not match :(
Address is 3535 SOUTH INTERSTATE 35 EAST in DENTON,TX


THE FRIARY OF LAKEVIEW CENTER
Scanning city GULF BREEZE...

Scanning whole state FL...

THE FRIARY OF LAKEVIEW CENTER did not match :(
Address is 4400 HICKORY SHORES BLVD in GULF BREEZE,FL


FAIR OAKS PAVILION - PSYCHIATRIC HOSPITAL
Scanning city DELRAY BEACH...

5440 LINTON BLVD matched to 5352 LINTON BLVD!
Potential Match: DELRAY MEDICAL CENTER, INC. / DELRAY MEDICAL CENTER
---
Scanning whole state FL...

5440 LINTON BLVD matched to 5352 LINTON BLVD, DELRAY BEACH!
Potential Match: DELRAY MEDICAL CENTER, INC. / DELRAY MEDICAL CENTER
---
FAIR OAKS PAVILION - PSYCHIATRIC HOSPITAL did not match :(
Address is 5440 LINTON BLVD in DELRAY BEACH,FL


SHANDS PSYCHIATRIC HOSPITAL
Scanning city GAINESVILLE...

Scanning whole state FL...

KINDRED HOSPITAL - TARRANT COUNTY did not match :(
Address is 1000 NORTH COOPER STREET in ARLINGTON,TX


ALASKA VA HEALTHCARE SYSTEM
Scanning city ANCHORAGE...

1201 N MULDOON RD matched to 1201 N MULDOON RD!
Potential Match: ANCHORAGE VAMC / None
---
Best Match: ANCHORAGE VAMC / None


VA MEDICAL CENTER - NEWINGTON CAMPUS
Scanning city NEWINGTON...

Scanning whole state CT...

VA MEDICAL CENTER - NEWINGTON CAMPUS did not match :(
Address is 555 WILLARD AVE in NEWINGTON,CT


VA MEDICAL CENTER - ALVIN C. YORK CAMPUS
Scanning city MURFREESBORO...

Scanning whole state TN...

VA MEDICAL CENTER - ALVIN C. YORK CAMPUS did not match :(
Address is 3400 LEBANON PIKE in MURFREESBORO,TN


ST LUKE'S EAST HOSPITAL LEE'S SUMMIT
Scanning city LEE'S SUMMIT...

Scanning whole state MO...

100 NE ST LUKES BLVD matched to 100 NE SAINT LUKES BLVD, LEES SUMMIT!
Potential Match: SAINT LUKES EAST HOSPITAL / SAINT LUKE'S EAST LEE'S SUMMIT HOSPITAL
---
ST LUKE'S EAST HOSPITAL LEE'S SUMMIT did not match :(
Add

ROCK SPRINGS did not match :(
Address is 700 SOUTHEAST INNER LOOP in GEORGETOWN,TX


KULA HOSPITAL
Scanning city KULA...

Scanning whole state HI...

KULA HOSPITAL did not match :(
Address is 100 KEOKEA PLACE in KULA,HI


QUEEN'S MEDICAL CENTER WEST
Scanning city EWA BEACH...

91-2141  FORT WEAVER RD matched to 91-2141 FORT WEAVER RD!
Potential Match: HAWAII MEDICAL CENTER WEST / None
---
91-2141  FORT WEAVER RD matched to 91-2141 FORT WEAVER ROAD!
Potential Match: ST. FRANCIS MEDICAL CENTER - WEST / None
---
91-2141  FORT WEAVER RD matched to 91-2301 FORT WEAVER RD!
Potential Match: SUTTER HEALTH PACIFIC / KAHI MOHALA HOSPITAL
---
Scanning whole state HI...

91-2141  FORT WEAVER RD matched to 91-2301 FORT WEAVER RD, EWA BEACH!
Potential Match: SUTTER HEALTH PACIFIC / KAHI MOHALA HOSPITAL
---
91-2141  FORT WEAVER RD matched to 91-2141 FORT WEAVER ROAD, EWA BEACH!
Potential Match: ST. FRANCIS MEDICAL CENTER - WEST / None
---
91-2141  FORT WEAVER RD matched to 91-2141 FORT WEAVER RD, EWA

1815 SOUTH 31ST STREET matched to 1901 S 1ST ST, TEMPLE!
Potential Match: CENTAL TEXAS VETERANS HEALTH CARE SYSTEM / None
---
1815 SOUTH 31ST STREET matched to 1901 S 1ST ST, TEMPLE!
Potential Match: CTVHCS / None
---
1815 SOUTH 31ST STREET matched to 708 S 1ST ST, MULESHOE!
Potential Match: MULESHOE AREA HOSPITAL DISTRICT / MULESHOE AREA MEDICAL CENTER
---
1815 SOUTH 31ST STREET matched to 2401 S 31ST ST, TEMPLE!
Potential Match: SCOTT & WHITE MEMORIAL HOSPITAL / BAYLOR SCOTT & WHITE MEDICAL CENTER - TEMPLE
---
SCOTT & WHITE PAVILION did not match :(
Address is 1815 SOUTH 31ST STREET in TEMPLE,TX


BEACON CHILDREN'S HOSPITAL
Scanning city LUVERNE...

Scanning whole state AL...

150 HOSPITAL DRIVE matched to 220 HOSPITAL DR, JACKSON!
Potential Match: GILLIARD HEALTH SERVICES / JACKSON MEDICAL CENTER
---
150 HOSPITAL DRIVE matched to 1 HOSPITAL DR SW, HUNTSVILLE!
Potential Match: CRESTWOOD HEALTHCARE LP / CRESTWOOD MEDICAL CENTER
---
150 HOSPITAL DRIVE matched to 2700 HOSPITAL DR, NORTH

64030 HIGHWAY 434 matched to 64030 HIGHWAY 434 FL 2, LACOMBE!
Potential Match: PRESTIGE REHAB / ST. CATHERINE MEMORIAL HOSPITAL
---
LOUISIANA HEART HOSPITAL did not match :(
Address is 64030 HIGHWAY 434 in LACOMBE,LA


REGENCY HOSPITAL OF COVINGTON
Scanning city COVINGTON...

195 HIGHLAND PARK ENTRANCE matched to 195 HIGHLAND PARK ENTRANCE!
Potential Match: COVINGTON -AMG SPECIALTY HOSPITAL, LLC / None
---
Best Match: COVINGTON -AMG SPECIALTY HOSPITAL, LLC / None


OCEANS BEHAVIORAL HOSPITAL OF KENTWOOD
Scanning city KENTWOOD...

921 AVENUE G matched to 719 AVENUE G!
Potential Match: HOLY SPIRIT COMFORT AND HEALING CENTERS, INC. / SOUTHEAST REGIONAL MEDICAL CENTER, INC.
---
Scanning whole state LA...

921 AVENUE G matched to 719 AVENUE G, KENTWOOD!
Potential Match: HOLY SPIRIT COMFORT AND HEALING CENTERS, INC. / SOUTHEAST REGIONAL MEDICAL CENTER, INC.
---
OCEANS BEHAVIORAL HOSPITAL OF KENTWOOD did not match :(
Address is 921 AVENUE G in KENTWOOD,LA


PHYSICIANS BEHAVIORAL HOSPITAL
Scan

In [86]:
new_unmatched_count

2724

In [87]:
new_matched_count

652

In [89]:
ids = pd.read_csv('ID_NPI.csv')

In [98]:
test_1 = pd.merge(ids, npi_with_taxes,on='NPI')

In [93]:
id_npis = pd.DataFrame(dict_list)

In [106]:
all_stuff = pd.concat([test_1,test_2])
all_stuff.LAST_UPDATE_DATE = pd.to_datetime(all_stuff.LAST_UPDATE_DATE)

all_stuff_2 = all_stuff.sort_values('LAST_UPDATE_DATE', ascending=False).drop_duplicates('ID')

In [99]:
test_2 = pd.merge(id_npis, npi_with_taxes, on = 'NPI')

In [97]:
pd.merge(id_npis, ids, on =['NPI','ID'], how = 'right')

ID         NPI
0      12645123  1215960901
1       2543055  1568446755
2       5843311  1548254931
3       5544074  1801825997
4       2484648  1881658110
...         ...         ...
7021   75934239  1366556698
7022   81376905  1114987963
7023  155583642  1033562319
7024   71276504  1457314528
7025   26790250  1588739288

[7026 rows x 2 columns]

In [115]:
pd.merge(all_stuff_2, npi_hospitals, on='NPI', how='outer').drop_duplicates('NPI')

ID         NPI                  Taxonomies_x  \
0     15678840.0  1104830900                ['282N00000X']   
1      5681230.0  1932109048                ['282NC0060X']   
2      5656345.0  1780630939                ['282NC0060X']   
3      9854736.0  1194737817                ['282NC0060X']   
4      9217756.0  1609816198  ['261QA1903X', '282NC0060X']   
...          ...         ...                           ...   
7110         NaN  1427022078                           NaN   
7111         NaN  1801874771                           NaN   
7112         NaN  1285747519                           NaN   
7113         NaN  1356331425                           NaN   
7114         NaN  1164400131                           NaN   

                                                 NAME_x  \
0                        VAL VERDE HOSPITAL CORPORATION   
1                              GUNNISON VALLEY HOSPITAL   
2                               UNITY FAMILY HEALTHCARE   
3     CHIPPEWA VALLEY HOSPITAL & OAKVIEW CARE CENTER...   
4                                            UPMC MUNCY   
...                                                 ...   
7110                                                NaN   
7111                                                NaN   
7112                                                NaN   
7113                                                NaN   
7114                                                NaN   

                           OTHER_NAME_x              MAILING_ADDRESS_1_x  \
0     VAL VERDE REGIONAL MEDICAL CENTER                 801 N BEDELL AVE   
1                                  None                  711 N TAYLOR ST   
2                ST. GABRIEL'S HOSPITAL                    815 2ND ST SE   
3              CHIPPEWA VALLEY HOSPITAL                       PO BOX 224   
4                                  None  600 GRANT STREET US STEEL TOWER   
...                                 ...                              ...   
7110                                NaN                              NaN   
7111                                NaN                              NaN   
7112                                NaN                              NaN   
7113                                NaN                              NaN   
7114                                NaN                              NaN   

                MAILING_ADDRESS_2_x MAILING_CITY_x MAILING_STATE_x  \
0                              None        DEL RIO              TX   
1                              None       GUNNISON              CO   
2                              None   LITTLE FALLS              MN   
3                              None         DURAND              WI   
4     59TH FLOOR, C/O RENEE JOHNSON     PITTSBURGH              PA   
...                             ...            ...             ...   
7110                            NaN            NaN             NaN   
7111                            NaN            NaN             NaN   
7112                            NaN            NaN             NaN   
7113                            NaN            NaN             NaN   
7114                            NaN            NaN             NaN   

     MAIING_ZIP_x  ... MAILING_STATE_y MAIING_ZIP_y MAILING_PHONE_y  \
0       788404112  ...              TX    788404112      8307758566   
1       812302296  ...              CO    812302296      9706411456   
2       563453505  ...              MN    563453505      3206325441   
3       547360224  ...             NaN          NaN             NaN   
4       152192740  ...              PA    152192740      4126236303   
...           ...  ...             ...          ...             ...   
7110          NaN  ...              PA    168301232      8147655341   
7111          NaN  ...              CO    816413181      9708785047   
7112          NaN  ...              WI    547360224      7156724211   
7113          NaN  ...              CT    069023602      2032767463   
7114          NaN  ...   

In [119]:
npi_check = list(all_stuff_2.NPI)

In [123]:
not_in_match = npi_hospitals[npi_hospitals.NPI.isin(npi_check)==False]

In [128]:
pd.concat([all_stuff_2, not_in_match])

C:\Users\vigrose\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.


ID     LAST_UPDATE_DATE              LOCATION_ADDRESS_1  \
3319  15678840.0  2020-01-13 00:00:00                801 N BEDELL AVE   
2219   5681230.0  2020-01-13 00:00:00                 711 N TAYLOR ST   
1079   5656345.0  2020-01-10 00:00:00                   815 2ND ST SE   
2709   9854736.0  2020-01-10 00:00:00                  1220 3RD AVE W   
67     9217756.0  2020-01-09 00:00:00                  215 E WATER ST   
...          ...                  ...                             ...   
6773         NaN           2020-01-06                809 TURNPIKE AVE   
6781         NaN           2020-01-08  100 PIONEERS MEDICAL CENTER DR   
6790         NaN           2020-01-10                  1220 3RD AVE W   
6792         NaN           2020-01-13                  1 HOSPITAL PLZ   
6794         NaN           2020-01-13         1200 S CEDAR CREST BLVD   

     LOCATION_ADDRESS_2 LOCATION_CITY LOCATION_PHONE LOCATION_STATE  \
3319               None       DEL RIO     8307758566             TX   
2219               None      GUNNISON     9706411456             CO   
1079               None  LITTLE FALLS     3206325441             MN   
2709               None        DURAND     7156724211             WI   
67                 None         MUNCY     5705468282             PA   
...                 ...           ...            ...            ...   
6773               None    CLEARFIELD     8147655341             PA   
6781               None        MEEKER     9708785047             CO   
6790               None        DURAND     7156724211             WI   
6792               None      STAMFORD     2032767463             CT   
6794               None     ALLENTOWN     6104028000             PA   

     LOCATION_ZIP MAIING_ZIP                MAILING_ADDRESS_1  \
3319    788404112  788404112                 801 N BEDELL AVE   
2219    812302243  812302296                  711 N TAYLOR ST   
1079    563453505  563453505                    815 2ND ST SE   
2709    547361600  547360224                       PO BOX 224   
67      177568828  152192740  600 GRANT STREET US STEEL TOWER   
...           ...        ...                              ...   
6773    168301232  168301232                 809 TURNPIKE AVE   
6781        81641  816413181   100 PIONEERS MEDICAL CENTER DR   
6790    547361600  547360224                       PO BOX 224   
6792    069023602  069023602                   1 HOSPITAL PLZ   
6794    181036202  181054000                      PO BOX 4000   

                            MAILING_ADDRESS_2  MAILING_CITY MAILING_PHONE  \
3319                                     None       DEL RIO    8307758566   
2219                                     None      GUNNISON    9706411456   
1079                                     None  LITTLE FALLS    3206325441   
2709                                     None        DURAND    7156724211   
67              59TH FLOOR, C/O RENEE JOHNSON    PITTSBURGH    4126236303   
...                                       ...           ...           ...   
6773                                     None    CLEARFIELD    8147655341   
6781                                     None        MEEKER    9708785047   
6790                                     None        DURAND    7156724211   
6792                                     None      STAMFORD    2032767463   
6794  2100 MACK BOULEVARD - 4TH FLOOR FINANCE     ALLENTOWN    4848843025   

     MAILING_STATE                                               NAME  \
3319            TX                     VAL VERDE HOSPITAL CORPORATION   
2219            CO                           GUNNISON VALLEY HOSPITAL   
1079            MN                            UNITY FAMILY HEALTHCARE   
2709            WI  CHIPPEWA VALLEY HOSPITAL & OAKVIEW CARE CENTER...   
67              PA                                         UPMC MUNCY   
...            ...                                                ...   
6773            PA                                CLEARFIELD HOSPIT

In [131]:
list(not_in_match['NAME'])

['USAF 95MDOS',
 'MILWAUKEE VA',
 "CHILDREN'S HOSPITAL BOSTON",
 'SAINT VINCENT CATHOLIC MEDICAL CENTER',
 'V A MEDICAL CENTER - WILMINGTON, DELAWARE',
 'MINNEAPOLIS V A MEDICAL CENTER',
 'V.A. MED CENTER',
 'V.A.N.J.HEALTHCARE SYSTEM',
 'IMH PROFESSIONAL RAD',
 'VA CARRIBEAN HEALTHCARE SYSTEM',
 'MIRNA L. VALENCIA, M.D., P.A.',
 'VA CENTRAL IOWA',
 "CHILDREN'S HOSPITAL OF WISCONSIN",
 'INCARE LLC',
 'US ARMY',
 'US ARMY',
 'US ARMY WALTER REED ARMY MED CTR',
 'US NAVY',
 'US NAVY',
 'USA MEDDAC, EVANS ARMY COMMUNIT Y HOSPITAL',
 'USA MEDICAL CENTER',
 'USAF',
 'CHILDRENS HOSPITAL AND REGIONAL MEDICAL CENTER',
 'USAF',
 "CHILDREN'S MEMOMRIAL HOSPITAL",
 'VA HOSPITAL',
 'MONROE HOSPITAL, LLC',
 'MONSOUR MEDICAL CENTER',
 'VA MC LONG BEACH',
 'VA MEDICAL CENTER',
 'VA MEDICAL CENTER',
 'VA MEDICAL CENTER',
 'VA MEDICAL CENTER',
 'HAMPSHIRE MEMORIAL HOSPITAL, INC',
 'CENTRAL ARKANSAS VETERANS HEALTHCARE SYSTEM',
 'CENTRAL ARKANSAS VETERANS HEALTH CARE SYSTEM',
 'VA MEDICAL CENTER',
 "CENT

In [137]:
list(npi_hospitals.drop_duplicates(['NAME','LOCATION_CITY']).drop_duplicates('LOCATION_ADDRESS_1').NAME)

['USAF 95MDOS',
 'MILWAUKEE VA',
 "CHILDREN'S HOSPITAL BOSTON",
 'SAINT VINCENT CATHOLIC MEDICAL CENTER',
 'CHILD STUDY AND TREATMENT CENTER',
 'CHICOT MEMORIAL HOSPITAL',
 'V A MEDICAL CENTER - WILMINGTON, DELAWARE',
 'MINIMALLY INVASIVE SURGERY HOSPITAL',
 'MINNEAPOLIS V A MEDICAL CENTER',
 'V.A. MED CENTER',
 'V.A.N.J.HEALTHCARE SYSTEM',
 'IMH PROFESSIONAL RAD',
 'VA CARRIBEAN HEALTHCARE SYSTEM',
 'MIRNA L. VALENCIA, M.D., P.A.',
 'VA CENTRAL IOWA',
 "CHILDREN'S HOSPITAL OF WISCONSIN",
 'INCARE LLC',
 'MIDSTATE MEDICAL CENTER',
 'US ARMY',
 'US ARMY',
 'US ARMY WALTER REED ARMY MED CTR',
 'US NAVY',
 'US NAVY',
 'CHIPPENHAM & JOHNSTON-WILLIS HOSPITALS, INC.',
 'USA MEDDAC',
 'USA MEDDAC, EVANS ARMY COMMUNIT Y HOSPITAL',
 'USA MEDICAL CENTER',
 'USAF',
 'CHILDRENS HOSPITAL AND RESEARCH CENTER AT OAKLAND',
 'CHILDRENS HOSPITAL AND REGIONAL MEDICAL CENTER',
 'USAF',
 "CHILDREN'S MEMOMRIAL HOSPITAL",
 'CHRISTUS HEALTH ARK-LA-TEX',
 'VA GREATER LOS ANGELES MEDICAL CENTER',
 'MONROE HOSPI

In [140]:
sorted_hosp = npi_hospitals.sort_values('LOCATION_ADDRESS_1')

In [142]:
count = 0
matches_count = 1
while matches_count > 0:
    matches_list = []
    count += 1
    name = ''
    city = ''
    state = ''
    address = ''
    list_npi =[]

    for row in sorted_hosp.itertuples():
        match = False
        if state == row.LOCATION_STATE:
            if city == row.LOCATION_CITY:
                add_match = match_address(row.LOCATION_ADDRESS_1, address)
                if add_match ==True or add_match == 'Maybe':
                    if fuzz.ratio(name,row.NAME)>40 or fuzz.ratio(row.OTHER_NAME, name) > 40:
                        print(f'{row.NAME} / {row.OTHER_NAME} matches {name}')
                        print(f'{row.LOCATION_ADDRESS_1} matches {address}')
                        match = True
                        print('')
                        matches_list.append(name)

        if match ==False:
            name = row.NAME
            city = row.LOCATION_CITY
            state = row.LOCATION_STATE
            address = row.LOCATION_ADDRESS_1
            list_npi.append(row.NPI)
    
    matches_count = len(matches_list)
            
    print(f'{len(list_npi)} total hospitals')
    sorted_hosp = sorted_hosp[sorted_hosp['NPI'].isin(list_npi)].sort_values('LOCATION_ADDRESS_1')
    print(f'Round {count} complete!')

UNITED HEALTH SERVICES HOSPITALS, INC. / None matches UNITED HEALTH SERVICES HOSPITALS, INC
10-42 MITCHELL AVE matches 10-42 MITCHELL AVE

COUNTY OF LOS ANGELES / COUNTY OF LOS ANGELES HARBOR UCLA MEDICAL CENTER matches HARBOR UCLA MEDICAL CENTER
1000 W CARSON ST # 2 matches 1000 W CARSON ST

GREENE COUNTY MEDICAL CENTER / None matches GREENE COUNTY MEDICAL CENTER
1000 W LINCOLNWAY ST matches 1000 W LINCOLN WAY

BASSETT ARMY COMMUNITY HOSPITAL / ACH BASSETT-WAINWRIGHT matches BASSETT ARMY COMMUNITY HOSPITAL
1060 GAFFNEY RD # 7420 matches 1060 GAFFNEY RD

SEVENTH-DAY ADVENTISTS LOMA LINDA UNIVERSITY MEDICAL CENTER, INC. / None matches SEVENTH-DAY ADVENTISTS LOMA LINDA UNIVERSITY MEDICAL CENTER, INC.
11234 ANDERSON ST RM 1140 matches 11234 ANDERSON ST

MISSOULA COMMUNITY HEALTH SERVICES, INC. / MINERAL COMMUNITY HOSPITAL matches MISSOULA COMMUNITY HEALTH SERVICES, INC.
1208 6TH AVE E matches 1208 6TH AVE

JAMES A. HALEY VA HOSPITAL / None matches JAMES A HALEY VETERANS HOSPITAL
13000 BRU

In [143]:
sorted_hosp

NPI                                  Taxonomies  \
6278  1548246622                              ['282NC0060X']   
327   1740200757                              ['282N00000X']   
4374  1821082918                              ['282N00000X']   
1430  1972503647                              ['282N00000X']   
1536  1740261213                              ['281P00000X']   
...          ...                                         ...   
202   1700993326                              ['282N00000X']   
6040  1609822881                              ['282N00000X']   
714   1033159728                              ['282N00000X']   
2164  1942240122  ['273R00000X', '283Q00000X', '323P00000X']   
1551  1891763009                              ['286500000X']   

                                                   NAME  \
6278                BROADDUS HOSPITAL ASSOCIATION, INC.   
327                               LOUIS A. JOHNSON VAMC   
4374                                 METRO MAYAGUEZ INC   
1430    GOVERNOR JUAN F. LUIS HOSPITAL & MEDICAL CENTER   
1536                      HEBREW HOME AND HOSPITAL, INC   
...                                                 ...   
202                              VETERANS ADMINSTRATION   
6040  COMMUNITY MEMORIAL HOSPITAL OF MENOMONEE FALLS...   
714                              PENNINGTON GAP HMA INC   
2164           STATE OF NEBRASKA DEPT OF ADMIN SERVICES   
1551                           DFAS ATTN: DFASIN/ ADAMB   

                       OTHER_NAME                      MAILING_ADDRESS_1  \
6278                         None                    #1 HEALTHCARE DRIVE   
327                          None                             PO BOX 232   
4374               HOSPITAL PEREA                             PO BOX 170   
1430                         None              #4007 ESTATE DIAMOND RUBY   
1536                         None                         1 ABRAHMS BLVD   
...                           ...                                    ...   
202                          None                      5450 MOUNTAIN TRL   
6040                         None              N74 W12501 LEATHERWOOD CT   
714   LEE REGIONAL MEDICAL CENTER                        WEST MORGAN AVE   
2164      LINCOLN REGIONAL CENTER  WEST PROSPECTOR PLACE & FOLSOM STREET   
1551   WOMACK ARMY MEDICAL CENTER                WOMACK ARMY MEDICAL CTR   

                  MAILING_ADDRESS_2              MAILING_CITY MAILING_STATE  \
6278                   P.O. BOX 930                  PHILIPPI            WV   
327                            None                   GRAFTON            WV   
4374                           None                  MAYAGUEZ            PR   
1430                           None  CHRISTIANSTED, ST. CROIX            VI   
1536                           None             WEST HARTFORD            CT   
...                             ...                       ...           ...   
202                    DOUGLASVILLE              DOUGLASVILLE            GA   
6040  400 WOODLAND PRIME, SUITE 103           MENOMONEE FALLS            WI   
714                       PO BOX 70            PENNINGTON GAP            VA   
2164                   PO BOX 94949                   LINCOLN            NE   
1551         BLDG 4-2817 RILEY ROAD                FORT BRAGG            NC   

     MAIING_ZIP MAILING_PHONE                     LOCATION_ADDRESS_1  \
6278      26416    3044571760                    #1 HEALTHCARE DRIVE   
327   263540232    3042651132                #1 MEDICAL CENTER DRIVE   
4374  006810170    7878340101                   #15 DR BASORA STREET   
1430  008214421    3407786311              #4007 ESTATE DIAMOND RUBY   
1536  061171508    8605233800                         1 ABRAHMS BLVD   
...         ...           ...                                    ...   
202   301351246    4044171765                VETERANS ADMINISTRATION   
6040  530514490    4147770417                 W180N8085 TOWN HALL RD   
714       24277    276546

In [148]:
GOV_HOSPITAL

X          Y  OBJECTID         ID  \
0     -83.387732  39.348667      3001   12645123   
1     -81.919907  40.565095      3002   17244654   
2     -82.450635  40.048302      3003    2543055   
3     -83.755531  40.369542      3004    5843311   
4     -82.224713  41.295065      3005    5544074   
...          ...        ...       ...        ...   
7576  -87.447485  36.636641      7577  181742223   
7577  -85.941438  37.900353      7578  181840121   
7578 -117.388804  33.221316      7579  181992055   
7579  144.736612  13.475210      7580  182096919   
7580  -77.093590  39.001287      7581  182120889   

                                              NAME  \
0                  ADENA GREENFIELD MEDICAL CENTER   
1                                POMERENE HOSPITAL   
2                        LICKING MEMORIAL HOSPITAL   
3                              MARY RUTAN HOSPITAL   
4                             MERCY ALLEN HOSPITAL   
...                                            ...   
7576           BLANCHFIELD ARMY COMMUNITY HOSPITAL   
7577               IRELAND ARMY COMMUNITY HOSPITAL   
7578                 NAVAL HOSPITAL CAMP PENDLETON   
7579                           NAVAL HOSPITAL GUAM   
7580  WALTER REED NATIONAL MILITARY MEDICAL CENTER   

                                ADDRESS           CITY STATE    ZIP  \
0                   550 MIRABEAU STREET     GREENFIELD    OH  45123   
1                      981 WOOSTER ROAD    MILLERSBURG    OH  44654   
2                 1320 WEST MAIN STREET         NEWARK    OH  43055   
3                     205 PALMER AVENUE  BELLEFONTAINE    OH  43311   
4                200 WEST LORAIN STREET        OBERLIN    OH  44074   
...                                 ...            ...   ...    ...   
7576                     650 JOEL DRIVE  FORT CAMPBELL    KY  42223   
7577                   289 IRELAND AVE.      FORT KNOX    KY  40121   
7578  200 MERCY CIRCLE , CAMP PENDLETON      OCEANSIDE    CA  92055   
7579            FARENHOLT AVE., BLDG 50  AGANA HEIGHTS    GU  96919   
7580                8901 ROCKVILLE PIKE       BETHESDA    MD  20889   

               ZIP4  ...                  VAL_DATE  \
0     NOT AVAILABLE  ...  2014-02-10T00:00:00.000Z   
1     NOT AVAILABLE  ...  2014-01-31T00:00:00.000Z   
2     NOT AVAILABLE  ...  2014-02-10T00:00:00.000Z   
3     NOT AVAILABLE  ...  2014-02-10T00:00:00.000Z   
4     NOT AVAILABLE  ...  2014-02-10T00:00:00.000Z   
...             ...  ...                       ...   
7576  NOT AVAILABLE  ...  2019-05-16T00:00:00.000Z   
7577  NOT AVAILABLE  ...  2019-05-16T00:00:00.000Z   
7578  NOT AVAILABLE  ...  2019-05-16T00:00:00.000Z   
7579  NOT AVAILABLE  ...  2019-05-09T00:00:00.000Z   
7580  NOT AVAILABLE  ...  2019-05-16T00:00:00.000Z   

                                                WEBSITE       STATE_ID  \
0     http://www.adena.org/locations/detail.dT/adena...           1200   
1                       http://www.pomerenehospital.org           1202   
2                               http://www.lmhealth.org           1213   
3                              http://www.maryrutan.org           1214   
4     http://www.mercyonline.org/mercy_allen_hospita...           1219   
...                                                 ...            ...   
7576                                      NOT AVAILABLE  NOT AVAILABLE   
7577                                      NOT AVAILABLE  NOT AVAILABLE   
7578                                      NOT AVAILABLE  NOT AVAILABLE   
7579                                      NOT AVAILABLE  NOT AVAILABLE   
7580  https://www.wrnmmc.capmed.mil/SitePages/home.aspx  NOT AVAILABLE   

                      ALT_NAME ST_FIPS                 OWNER TTL_STAFF  BEDS  \
0                NOT AVAILABLE      39            NON-PROFIT      -999    25   
1                NOT AVAILABLE      39    GOVERNMENT - LOCAL      -999    69   
2                NOT AVAILABLE      39            NON-PROFIT      -999   213   
3                NOT AVAILABLE

In [152]:
gov_ids = list(all_stuff_2['ID'])

In [157]:
unmatched_still = GOV_HOSPITAL[GOV_HOSPITAL.ID.isin(gov_ids)==False]

In [193]:
npi_with_taxes.sort_values('LAST_UPDATE_DATE')

NPI                                         Taxonomies  \
143167  1124078985                                     ['174400000X']   
228971  1174547756                                     ['291U00000X']   
4016    1881604593                                     ['207NS0135X']   
33869   1538261318                                     ['261QD0000X']   
64048   1053404533                                     ['323P00000X']   
...            ...                                                ...   
236706  1972519379  ['207QG0300X', '207R00000X', '363A00000X', '36...   
190649  1083642581                                     ['152W00000X']   
190650  1619905114                                     ['213E00000X']   
164702  1598702862                                     ['314000000X']   
147524  1497707392                                     ['208600000X']   

                                    NAME  \
143167        ALPESH D. DESAI, D.O. P.A.   
228971           COMPU-MED SYSTEMS, INC.   
4016      SUZANNE SIROTA ROZENBERG DO,PC   
33869                AUSTIN SMILE CENTER   
64048             ED MURPHY & ASSOCIATES   
...                                  ...   
236706  BAYLOR UNIVERSITY MEDICAL CENTER   
190649          JEFFREY L. MORER, OD, PC   
190650    HEALTHDRIVE PODIATRY GROUP, PC   
164702   PETERSEN HEALTH PROPERTIES, LLC   
147524               UNIVERSITY OF MIAMI   

                                           OTHER_NAME    MAILING_ADDRESS_1  \
143167                                           None      2120 ASHLAND ST   
228971       PROFESSIONAL MEDICAL LABORATORY SERVICES    110 N LINCOLN AVE   
4016                                             None         11 IRVING PL   
33869                                            None       11521 N FM 620   
64048                                      FAIR WINDS        181 KINGS HWY   
...                                               ...                  ...   
236706                                           None        PO BOX 842022   
190649                     HEALTHDRIVE EYE CARE GROUP    100 CROSSING BLVD   
190650                     HEALTHDRIVE PODIATRY GROUP    100 CROSSING BLVD   
164702  JONESBORO REHABILITATION & HEALTH CARE CENTER  830 W TRAILCREEK DR   
147524                    UMIAMI MEDICINE - BURN UNIT     1611 NW 12TH AVE   

       MAILING_ADDRESS_2    MAILING_CITY MAILING_STATE MAIING_ZIP  \
143167              None         HOUSTON            TX      77008   
228971         SUITE 102          CORONA            CA  928821853   
4016                None        WOODMERE            NY  115981256   
33869          SUITE 700          AUSTIN            TX  787261139   
64048          SUITE 127  FREDERICKSBURG            VA  224052685   
...                  ...             ...           ...        ...   
236706              None          DALLAS            TX  752842022   
190649         SUITE 300      FRAMINGHAM            MA   17025555   
190650         SUITE 300      FRAMINGHAM            MA   17025555   
164702              None          PEORIA            IL  616141862   
147524   BOX 016960 M851           MIAMI            FL  331361005   

       MAILING_PHONE     LOCATION_ADDRESS_1 LOCATION_ADDRESS_2 LOCATION_CITY  \
143167    7138642659        2120 ASHLAND ST               None       HOUSTON   
228971    9512731055      110 N LINCOLN AVE          SUITE 102        CORONA   
4016      5162955570           11 IRVING PL               None      WOODMERE   
33869     5125069800         11521 N FM 620          SUITE 700        AUSTIN   
64048     5403683098          1410 DUSTY RD               None       BUMPASS   
...              ...                    ...                ...           ...   
236706    2148203151        3500 GASTON AVE               None        DALLAS   
190649    6179646681         12 PENNS TRAIL          SUITE 154       NEWTOWN   
190650    6179646681         12 PENNS TRAIL          SUITE 154       NEWTOWN   
164702    3096918113  995 STATE ROUTE 127 S

In [110]:
dict_list_11 =[]
UNMATCHED_LIST_11 =[]

for row in UNMATCHED_STILL.itertuples():
    new_df = npi_with_taxes[npi_with_taxes.LOCATION_STATE==row.STATE].sort_values('LAST_UPDATE_DATE')
    print(row.NAME)
    match =False
    add_match =False
        
    npi_number ='None'
        
    best_name_score = 0
    best_add_score = 80
    
    
    for line in new_df.itertuples():
        
        
        add_score = match_address_2(row.ADDRESS, line.LOCATION_ADDRESS_1)
        name_score = max([fuzz.ratio(row.NAME, line.OTHER_NAME),fuzz.ratio(row.NAME, line.NAME)])
        
        if add_score == 100 and name_score > 70:
            add_match = True
            match = True
            print('***********')
            print(f'{row.ADDRESS} matched to {line.LOCATION_ADDRESS_1}, {line.LOCATION_CITY}!')
            print(f'VERY GOOD MATCH: {line.NAME} / {line.OTHER_NAME}') 
            print('***********')
            break
            
        elif add_score>=best_add_score:
            if name_score >= best_name_score:
                match = True
                print(f'{row.ADDRESS} matched to {line.LOCATION_ADDRESS_1}, {line.LOCATION_CITY}!')
                print(f'Potential Match: {line.NAME} / {line.OTHER_NAME}')    
                print('---')
                NAME = line.NAME
                OTHER_NAME = line.OTHER_NAME
                best_name_score = name_score
                best_add_score = add_score
                npi_number = line.NPI
                
    if (add_match == False) & (match == True):
        print(f'BEST MATCH: {NAME} / {OTHER_NAME}')    
        print('---')
        
    if match == True:
        print('wtf')
        if npi_number == 'None':
            npi_number = line.NPI
        new_dict = {
            'ID': row.ID,
            'NPI': npi_number
            }
        dict_list_11.append(new_dict)
        
    if match == False:
        print(f'{row.NAME} did not match :(')
        print(f'Address is {row.ADDRESS} in {row.CITY},{row.STATE}')
        print('---')
        UNMATCHED_LIST_11.append(row.ID)
    print('')
            
        
        

GLENWOOD STATE HOSPITAL SCHOOL
GLENWOOD STATE HOSPITAL SCHOOL did not match :(
Address is 711 SOUTH VINE STREET in GLENWOOD,IA
---

HEALTHSOUTH EAST VALLEY REHABILITATION
5652 E BASELINE ROAD matched to 5652 EAST BASELINE ROAD, MESA!
Potential Match: ENCOMPASS HEALTH REHABILITATION HOSPITAL OF EAST VALLEY, LLC / ENCOMPASS HEALTH REHABILITATION HOSPITAL OF EAST VALLEY
---
BEST MATCH: ENCOMPASS HEALTH REHABILITATION HOSPITAL OF EAST VALLEY, LLC / ENCOMPASS HEALTH REHABILITATION HOSPITAL OF EAST VALLEY
---
wtf

HORIZON SPECIALTY HOSPITAL OF HENDERSON
***********
8550 S EASTERN AVE matched to 8550 S EASTERN AVENUE, LAS VEGAS!
VERY GOOD MATCH: THI OF NEVADA II AT DESERT LANE LLC / HORIZON SPECIALTY HOSPITAL OF HENDERSON
***********
wtf

UINTAH BASIN CARE AND REHABILITATION
UINTAH BASIN CARE AND REHABILITATION did not match :(
Address is 187 WEST LAGOON STREET in ROOSEVELT,UT
---

PERRY COUNTY MEMORIAL HOSPITAL
PERRY COUNTY MEMORIAL HOSPITAL did not match :(
Address is ONE HOSPITAL RD in TEL

BEST MATCH: LAKE HOSPITAL SYSTEM, INC / LAKE HEALTH
---
wtf

PROMEDICA WILDWOOD ORTHOPEDICA AND SPINE HOSPITAL
PROMEDICA WILDWOOD ORTHOPEDICA AND SPINE HOSPITAL did not match :(
Address is 2901 N REYNOLDS RD in TOLEDO,OH
---

COPPER HILLS YOUTH CENTER
COPPER HILLS YOUTH CENTER did not match :(
Address is 5899 WEST RIVENDELL DRIVE in WEST JORDAN,UT
---

REGIONS HOSPITAL
***********
640 JACKSON STREET matched to 640 JACKSON ST, SAINT PAUL!
VERY GOOD MATCH: REGIONS HOSPITAL / None
***********
wtf

HEBER VALLEY MEDICAL CENTER
1485 UNITED STATES HIGHWAY 40 matched to 1485 S HIGHWAY 40, HEBER CITY!
Potential Match: IHC HEALTH SERVICES INC / HEBER VALLEY HOSPITAL
---
BEST MATCH: IHC HEALTH SERVICES INC / HEBER VALLEY HOSPITAL
---
wtf

SANPETE VALLEY HOSPITAL
1100 SOUTH MEDICAL DRIVE matched to 100 N MEDICAL DR, SALT LAKE CITY!
Potential Match: INTERMOUNTAIN HEALTHCARE / PRIMARY CHILDREN'S MEDICAL CENTER
---
***********
1100 SOUTH MEDICAL DRIVE matched to 1100 S MEDICAL DR, MT PLEASANT!
VERY G

UNITY HEALING CENTER did not match :(
Address is 448 SEQUOYAH TRAIL DR in CHEROKEE,NC
---

AKRON CHILDREN'S HOSPITAL
AKRON CHILDREN'S HOSPITAL did not match :(
Address is 214 W BOWERY ST in AKRON,OH
---

CAVHCS EAST CAMPUS
CAVHCS EAST CAMPUS did not match :(
Address is 8105 VETERANS WAY in MONTGOMERY,AL
---

CONNECTICUT CHILDBIRTH & WOMEN'S CENTER
CONNECTICUT CHILDBIRTH & WOMEN'S CENTER did not match :(
Address is 94 LOCUST AVE in DANBURY,CT
---

ACADIA MONTANA
ACADIA MONTANA did not match :(
Address is 55 BASIN CREEK ROAD in BUTTE,MT
---

MPI CHEMICAL DEPENDENCY RECOVERY HOSPITAL
MPI CHEMICAL DEPENDENCY RECOVERY HOSPITAL did not match :(
Address is 3012 SUMMIT STREET, 5TH FLOOR in OAKLAND,CA
---

BHC FAIRFAX HOSPITAL NORTH
BHC FAIRFAX HOSPITAL NORTH did not match :(
Address is 916 PACIFIC AVE, FL 7 in EVERETT,WA
---

SUTTER COAST HOSPITAL
SUTTER COAST HOSPITAL did not match :(
Address is 555 5TH STREET, SUITE 2 in BROOKINGS,OR
---

TMC HEALTHCARE CENTER FOR GEROPSYCH
TMC HEALTHCARE CE

HUGHES SPALDING CHILDREN'S HOSPITAL did not match :(
Address is 1711 TULLIE CIRCLE NE in ATLANTA,GA
---

SHARP MCDONALD CENTER
SHARP MCDONALD CENTER did not match :(
Address is 7989 LINDA VISTA ROAD in SAN DIEGO,CA
---

SONORA REGIONAL MEDICAL CENTER - FAIRVIEW
SONORA REGIONAL MEDICAL CENTER - FAIRVIEW did not match :(
Address is 179 SOUTH FAIRVIEW LANE in SONORA,CA
---

ALTA BATES SUMMIT MED CTR-HERRICK CAMPUS
ALTA BATES SUMMIT MED CTR-HERRICK CAMPUS did not match :(
Address is 2001 DWIGHT WAY in BERKELEY,CA
---

AMERICAN RECOVERY CENTER
AMERICAN RECOVERY CENTER did not match :(
Address is 2180 WEST VALLEY BOULEVARD in POMONA,CA
---

TOM REDGATE MEMORIAL RECOVERY CENTER
TOM REDGATE MEMORIAL RECOVERY CENTER did not match :(
Address is 1775 CHESTNUT STREET in LONG BEACH,CA
---

GENERAL HOSPITAL, THE
GENERAL HOSPITAL, THE did not match :(
Address is 2200 HARRISON AVENUE in EUREKA,CA
---

SAINT JOSEPHS HOSPITAL OF ATLANTA
5665 PEACHTREE DUNWOODY RD NE matched to 5665 PEACHTREE DUNWOODY RD

MILESTONE FOUNDATION - EXTENDED CARE did not match :(
Address is 28 PORTLAND AVENUE in OLD ORCHARD BEACH,ME
---

METROWEST MEDICAL CENTER - LEONARD MORSE CAMPUS
METROWEST MEDICAL CENTER - LEONARD MORSE CAMPUS did not match :(
Address is 67 UNION STREET in NATICK,MA
---

REGIONAL REHABILITATION INSTITUTE
REGIONAL REHABILITATION INSTITUTE did not match :(
Address is 2908 5TH STREET in RAPID CITY,SD
---

GILLETTE CHILDRENS SPEC HOSP
***********
200 UNIVERSITY AVENUE EAST matched to 200 UNIVERSITY AVE E, SAINT PAUL!
VERY GOOD MATCH: GILLETTE CHILDREN'S SPECIALTY HEALTHCARE / None
***********
wtf

ST JOSEPHS HOSPITAL
45 W 10TH STREET matched to 45 10TH STREET WEST, SAINT PAUL!
Potential Match: HEALTHEAST ST JOSEPHS HOSPITAL / None
---
BEST MATCH: HEALTHEAST ST JOSEPHS HOSPITAL / None
---
wtf

ST CLOUD HOSPITAL
1406 SIXTH AVENUE NORTH matched to 1406 6TH AVE N, SAINT CLOUD!
Potential Match: CENTRACARE HEALTH SYSTEM / None
---
1406 SIXTH AVENUE NORTH matched to 1406 6TH AVE NORTH, SAINT CLOUD

...

FLORIDA HOSPITAL KISSIMMEE did not match :(
Address is 2450 N ORANGE BLOSSOM TRL in KISSIMMEE,FL
---

FLORIDA HOSPITAL WAUCHULA
FLORIDA HOSPITAL WAUCHULA did not match :(
Address is 533 W CARLTON ST in WAUCHULA,FL
---

SACRED HEART HOSPITAL ON THE GULF
***********
3801 E HWY 98 matched to 3801 E HIGHWAY 98, PORT ST JOE!
VERY GOOD MATCH: SACRED HEART ON THE GULF / None
***********
wtf

MEASE COUNTRYSIDE HOSPITAL
3231 MCMULLEN BOOTH RD matched to 3251 N MCMULLEN BOOTH RD, CLEARWATER!
Potential Match: BAYCARE HEALTH SYSTEM AGENT FOR TRUSTEES OF MEASE HOSPITAL / None
---
3231 MCMULLEN BOOTH RD matched to 3231 N MCMULLEN BOOTH RD, CLEARWATER!
Potential Match: TRUSTEES OF MEASE HOSPITAL INC / MEASE COUNTRYSIDE HOSPITAL
---
BEST MATCH: TRUSTEES OF MEASE HOSPITAL INC / MEASE COUNTRYSIDE HOSPITAL
---
wtf

ST ANTHONYS HOSPITAL
***********
1200 7TH AVE N matched to 1200 7TH AVE N, ST PETERSBURG!
VERY GOOD MATCH: ST ANTHONY'S HOSPITAL / None
***********
wtf

MEDICAL CENTER OF TRINITY WEST PASCO CA

RECEPTION AND MEDICAL CENTER HOSPITAL did not match :(
Address is 7765 S COUNTY RD 231 in LAKE BUTLER,FL
---

FLORIDA HOSPITAL OCEANSIDE
FLORIDA HOSPITAL OCEANSIDE did not match :(
Address is 264 S ATLANTIC AVE in ORMOND BEACH,FL
---

HALIFAX PSYCHIATRIC CENTER-NORTH
HALIFAX PSYCHIATRIC CENTER-NORTH did not match :(
Address is 841 JIMMY ANN DR in DAYTONA BEACH,FL
---

DEPOO HOSPITAL
DEPOO HOSPITAL did not match :(
Address is 1200 KENNEDY DR in KEY WEST,FL
---

WEST MARION COMMUNITY HOSPITAL
WEST MARION COMMUNITY HOSPITAL did not match :(
Address is 4600 SW 46TH CT in OCALA,FL
---

ST JOSEPH HOSPITAL MILFORD MED CTR
ST JOSEPH HOSPITAL MILFORD MED CTR did not match :(
Address is 442 NASHUA ROAD in MILFORD,NH
---

ST JOSEPH'S CHILDREN'S HOME
ST JOSEPH'S CHILDREN'S HOME did not match :(
Address is SOUTH 82240, 1419 MAIN ST in TORRINGTON,WY
---

HOSP UNIVERSITARIO DR RAMON RUIZ ARNAU
HOSP UNIVERSITARIO DR RAMON RUIZ ARNAU did not match :(
Address is AVE LAUREL - URB SANTA JUANITA in BAYAMON

EXODUS RECOVERY PHF did not match :(
Address is 9808 VENICE BLVD in CULVER CITY,CA
---

ST. HELENA HOSPITAL
***********
10 WOODLAND RD. matched to 10 WOODLAND RD, SAINT HELENA!
VERY GOOD MATCH: ST. HELENA HOSPITAL / ADVENTIST HEALTH ST. HELENA
***********
wtf

THUNDER ROAD CHEMICAL DEPENDENCY RECOVERY HOSPITAL
THUNDER ROAD CHEMICAL DEPENDENCY RECOVERY HOSPITAL did not match :(
Address is 390 40TH STREET in OAKLAND,CA
---

ARMC BEHAVIORAL HEALTH CENTER
ARMC BEHAVIORAL HEALTH CENTER did not match :(
Address is 230 DERONDA STREET in AMERY,WI
---

BALDWIN AREA MED CTR
BALDWIN AREA MED CTR did not match :(
Address is 730 10TH AVE in BALDWIN,WI
---

LOS ROBLES HOSPITAL & MEDICAL CENTER - EAST CAMPUS
LOS ROBLES HOSPITAL & MEDICAL CENTER - EAST CAMPUS did not match :(
Address is 150 VIA MERIDA in WESTLAKE VILAGE,CA
---

CORONA REGIONAL MEDICAL CENTER-MAGNOLIA
CORONA REGIONAL MEDICAL CENTER-MAGNOLIA did not match :(
Address is 730 MAGNOLIA AVENUE in CORONA,CA
---

SERENITY SPRINGS SPECIALTY HOS

UNION CORRECTIONAL INSTITUTE HOSPITAL did not match :(
Address is 7819 NW 228TH ST in RAIFORD,FL
---

MEMORIAL HOSPITAL
***********
1110 N SARAH DEWITT DRIVE matched to 1110 N SARAH DEWITT DR, GONZALES!
VERY GOOD MATCH: GONZALES HEALTHCARE SYSTEM / MEMORIAL HOSPITAL
***********
wtf

GRAHAM REGIONAL MEDICAL CENTER
***********
1301 MONTGOMERY ROAD matched to 1301 MONTGOMERY ROAD, GRAHAM!
VERY GOOD MATCH: GRAHAM REGIONAL MEDICAL CENTER / None
***********
wtf

LAVACA MEDICAL CENTER
1400 NORTH TEXANA STREET matched to 1400 N TEXANA, HALLETTSVILLE!
Potential Match: LAVACA HOSPITAL DISTRICT / LAVACA MEDICAL CENTER
---
BEST MATCH: LAVACA HOSPITAL DISTRICT / LAVACA MEDICAL CENTER
---
wtf

CHI ST LUKES HEALTH BAYLOR COLLEGE OF MEDICINE MEDICAL CENTER
***********
6720 BERTNER STREET matched to 6720 BERTNER STREET, HOUSTON!
VERY GOOD MATCH: CHI ST LUKE'S HEALTH BAYLOR ST. LUKE'S MEDICAL CENTER / None
***********
wtf

SAINT CLARE'S HOSPITAL
SAINT CLARE'S HOSPITAL did not match :(
Address is 915 EAS

BEST MATCH: HOSP. ONCOLOGICO DR. I. GONZALEZ MARTINEZ / None
---
wtf

AUXILIO MUTUO HOSPITAL
PONCE DE LEON AVENUE matched to PONCE DE LEON AVE, SAN JUAN!
Potential Match: HOSPITAL ESPANOL AUXILIO MUTUO DE PUERTO RICO, INC. / CIRUGIA AMBULATORIA
---
BEST MATCH: HOSPITAL ESPANOL AUXILIO MUTUO DE PUERTO RICO, INC. / CIRUGIA AMBULATORIA
---
wtf

HEALTH SOUTH REHABILITATION OF PR
HEALTH SOUTH REHABILITATION OF PR did not match :(
Address is 3ER PISO HOSP UNIVERSITARIO DE ADULTOS - CENTRO MEDICO in MONACILLO URBANO,PR
---

HOSP PSIQUIATRICO CORRECCIONAL
HOSP PSIQUIATRICO CORRECCIONAL did not match :(
Address is C/TENIENTE CESAR GONZALEZ 1106 in MONACILLO URBANO,PR
---

BELAU NATIONAL HOSPITAL
BELAU NATIONAL HOSPITAL did not match :(
Address is 1 HOSPITAL ROAD in KOROR,PW
---

LBJ TROPICAL MEDICAL CENTER
LBJ TROPICAL MEDICAL CENTER did not match :(
Address is FAGAALU VILLAGE in PAGO PAGO,AS
---

HEART HOSPITAL OF AUSTIN
HEART HOSPITAL OF AUSTIN did not match :(
Address is 3801 NORTH LAMAR in 

In [111]:
len(UNMATCHED_LIST_11)

359

In [107]:
len(UNMATCHED_LIST_10)

543

In [109]:
UNMATCHED_STILL = GOV_HOSPITAL[GOV_HOSPITAL.ID.isin(UNMATCHED_LIST_10)]

In [44]:
UNMATCHED_STILL.to_csv('unmatched_gov_final.csv', index=False)

In [40]:
match_address_2('1650 BRAGAW STREET','1650 COWLES ST')

81.0

In [195]:
len(UNMATCHED_LIST)

13

In [186]:
match_address_2('6900 NORTH DURANGO DRIVE','900 N RANCHO DR')

86.0

In [173]:
thng1='10819 S Drake'
thng2='10946 s drake'
match_address_2(thng1, thng2)

80.0

In [189]:
len(dict_list_3)

1254

In [198]:
new_matches = pd.DataFrame(dict_list_4)
old_matches = pd.DataFrame(dict_list_3)

In [218]:
all_matches = pd.concat([new_matches, old_matches])
all_matches = all_matches.drop_duplicates()
all_matches = pd.merge(all_matches, npi_with_taxes, on = 'NPI')
all_matches = pd.merge(all_matches, GOV_HOSPITAL, on='ID', suffixes = ['_NPI','_GOV'])
all_matches = all_matches.sort_values('ID')

id_dict = {}
for row in all_matches.itertuples():
    print('')
    print(row.NAME_GOV)
    ADD_SCORE = match_address_2(row.ADDRESS,row.LOCATION_ADDRESS_1)
    NAME_SCORE = max([fuzz.ratio(row.NAME_NPI, row.NAME_GOV), fuzz.ratio(row.OTHER_NAME, row.NAME_GOV)])
    
    if row.ID in id_dict.keys():
        if id_dict[row.ID]['ADD_SCORE'] >= ADD_SCORE and id_dict[row.ID]['NAME_SCORE'] > NAME_SCORE:
            id_dict[row.ID]['NAME'] = row.NAME_NPI
            id_dict[row.ID]['OTHER_NAME'] = row.OTHER_NAME
            id_dict[row.ID]['CITY'] = row.CITY
            id_dict[row.ID]['ADDRESS'] = row.LOCATION_ADDRESS_1
            id_dict[row.ID]['NPI'] = row.NPI
            
            id_dict[row.ID]['ADD_SCORE'] = ADD_SCORE
            id_dict[row.ID]['NAME_SCORE'] = NAME_SCORE
            print(f'{row.NAME_NPI} / {row.OTHER_NAME} is best match')
    else:
        id_dict[row.ID]={}
        id_dict[row.ID]['ID']=row.ID
        id_dict[row.ID]['NAME'] = row.NAME_NPI
        id_dict[row.ID]['OTHER_NAME'] = row.OTHER_NAME
        id_dict[row.ID]['CITY'] = row.LOCATION_CITY
        id_dict[row.ID]['ADDRESS'] = row.LOCATION_ADDRESS_1
        id_dict[row.ID]['NPI'] = row.NPI
        
        id_dict[row.ID]['ADD_SCORE'] = ADD_SCORE
        id_dict[row.ID]['NAME_SCORE'] = NAME_SCORE
        print(f'{row.NAME_NPI} / {row.OTHER_NAME} is match')



CARL R. DARNALL ARMY MEDICAL CENTER
BEARABLE DIAGNOSTIC CENTER, LLC / None is match

IRWIN ARMY COMMUNITY HOSPITAL
WILSON COUNTY HOSPITAL / WILSON MEDICAL CENTER is match

EISENHOWER ARMY MEDICAL CENTER
EISENHOWER ARMY MEDICAL CENTER / AMC EISENHOWER-GORDON is match

EISENHOWER ARMY MEDICAL CENTER

FORT BELVOIR COMMUNITY HOSPITAL
WASHINGTON DC VAMC / FT. BELVOIR VA CLINIC is match

WOMACK ARMY MEDICAL CENTER
WOMACK ARMY MEDICAL CENTER / WOMACK ARMY MEDICAL CENTER is match

THE CORPUS CHRISTI MEDICAL CENTER - DOCTORS REGIONAL
GHEP CORPUS CHRISTI PLLC / None is match

CHRISTUS SPOHN HOSPITAL CORPUS CHRISTI SOUTH
CHRISTUS TRINITY CLINIC / CHRISTUS TRINITY CLINIC is match

CHRISTUS SPOHN HOSPITAL CORPUS CHRISTI SOUTH

MCALLEN HEART HOSPITAL
H K A CORPORATION / AMERICAN HOME HEALTH & HOSPICE is match

MISSION TRAIL BAPTIST HOSPITAL-ER
WEBSTER SURGICAL SPECIALTY HOSPITAL, LTD / HOUSTON PHYSICIANS' HOSPITAL is match

NORTHEAST BAPTIST HOSPITAL
RIVER CITY NURSE MANAGEMENT LLC / None is match


LAHEY MEDICAL CENTER - PEABODY
PEABODY OBGYN, LLC / None is match

LAHEY MEDICAL CENTER - PEABODY

WINDHAM COMMUNITY MEMORIAL HOSPITAL
WINDHAM FAMILY MEDICAL SERVICES, PC / None is match

CANCER INSTITUTE OF NEW JERSEY
LIBERTY REHABILITATION ASSOCIATES / None is match

CANCER INSTITUTE OF NEW JERSEY

MEDSTAR GOOD SAMARITAN HOSPITAL
PRECISION IMAGING LLC / None is match

MEDSTAR GOOD SAMARITAN HOSPITAL

ST LUKES HOSPITAL
ST. LUKE'S HOSPITAL OF DULUTH / ST. LUKE'S ANESTHESIA ASSOCIATES is match

ST LUKES HOSPITAL

NELSON COUNTY HEALTH SYSTEM
MCKENZIE COUNTY HEALTHCARE SYSTEMS INC / MCHS CLINIC is match

JESSE BROWN VA MEDICAL CENTER - VA CHICAGO HEALTHCARE SYSTEM
JESSE BROWN VA MEDICAL CENTER / None is match

JESSE BROWN VA MEDICAL CENTER - VA CHICAGO HEALTHCARE SYSTEM
JESS BROWN VAMC / None is best match

BANNER IRONWOOD MEDICAL CENTER
DERMATOLOGY CENTER PC / None is match

ST. ROSE DOMINICAN HOSPITALS - ROSE DE LIMA CAMPUS
JOHN T GOODSELL DO PC GREGORY LINDERER MD LTD / ANESTHESIA ASSO

HAVASU REGIONAL MEDICAL CENTER
CLEARWATER CNTY MEM HOSP PHCY / None is best match

GILA REGIONAL MEDICAL CENTER
GABA LLC / None is match

GILA REGIONAL MEDICAL CENTER

PROVIDENCE PORTLAND MEDICAL CENTER
PROVIDENCE HEALTH & SERVICES - OREGON / PROVIDENCE CONSULTING PSYCHIATRY EAST is match

PROVIDENCE PORTLAND MEDICAL CENTER

SGT. JOHN L. LEVITOW VETERAN'S HEALTH CENTER
WESLEYAN UNIVERSITY - DAVISON HEALTH CENTER / None is match

PRINCETON HOUSE BEHAVIORAL HEALTH
BRIARWOOD CARE & REHABILITATION CENTER / CARRIAGE HOUSE MANOR is match

JANE TODD CRAWFORD MEMORIAL HOSPITAL
JANE TODD HOSPITAL RADIOLOGICAL ASSOCIATES,LLC / None is match

UNIVERSITY HOSPITALS CONNEAUT MEDICAL CENTER
ALEXIS INDUSTRIAL MEDICAL CENTER / None is match

FRANCISCAN ST ANTHONY HEALTH - MICHIGAN CITY
ST. ANTHONY HOME MEDICAL EQUIPMENT / None is match

FRANCISCAN ST ANTHONY HEALTH - MICHIGAN CITY
ST VINCENT PHYSICIAN SERVICES HOSPITAL AND HEALTH CARE CENTER / ST VINCENT PHYSICIAN SERVICES is best match

AVERA BEHAVIOR

COMMUNITY UNITED METHODIST HOSPITAL, INC. / METHODIST HOSPITAL PROFESSIONAL SERVICES is match

METHODIST HOSPITAL
KENTUCKY EMERGENCY MEDICINE PHYSICIANS PLLC / None is best match

METROSOUTH MEDICAL CENTER
MILRUD CHIROPRACTIC NATURAL CARE & REHAB, INC / MILRUD MEDICAL CENTER is match

METROSOUTH MEDICAL CENTER

ST. LUKE'S NORTHLAND HOSPITAL - SMITHVILLE
MERCY HOSPITALS EAST COMMUNITIES / MERCY HOSPITAL ST LOUIS is match

ST. LUKE'S NORTHLAND HOSPITAL - SMITHVILLE
LIBERTY EMERGENCY PHYSICIANS, INC. / None is best match

PENDER COMMUNITY HOSPITAL
ROCK COUNTY HOSPITAL / ROCK COUNTY HOSPITAL LONG TERM CARE is match

LONE PEAK HOSPITAL
SHOPKO STORES OPERATING CO LLC / SHOPKO PHARMACY 105 is match

VA SOUTHERN NEVADA HEALTHCARE SYSTEM
LAS VEGAS VAMC / LAS VEGAS VAMC PHARMACY is match

VA SOUTHERN NEVADA HEALTHCARE SYSTEM

SJ VETERANS ADMINISTRATION CARIBBEAN HEALTHCARE SYSTEM
RAQUEL ESPINOSA BARAJAS / WESTERN HEALTH & CARE AMBULANCE is match

CENTRAL FLORIDA BEHAVIORAL HOSPITAL
FLORIDA EM-I 

LEBONHEUR PATIENT TRANSPORTATION / None is match

SAINT JOSEPH EAST
WAL-MART STORES EAST LP / WALMART PHARMACY 10-0299 is match

SAINT JOSEPH EAST

CENTRACARE HEALTH SYSTEM
RAMSEY INTEGRATED HEALTH SERVICES / INTEGRATED HOME CARE is match

MADISON MEDICAL CENTER
OZARKS MEDICAL CENTER / RIVERWAYS HOSPICE OF OZARKS MEDICAL CENTER is match

COLORADO MENTAL HEALTH INSTITUTE AT PUEBLO-PSYCH
APRIA HEALTHCARE LLC / None is match

TMC HEALTHCARE
SWEA, P.C. / SOUTHWEST EMERGENCY ASSOCIATES, P.C. is match

TMC HEALTHCARE

CORONA REGIONAL MEDICAL CENTER-MAGNOLIA
RIVERSIDE MEDICAL CLINIC / None is match

CORONA REGIONAL MEDICAL CENTER-MAGNOLIA
STAR VIEW BEHAVIORAL HEALTH, INC. / STAR VIEW ADOLESCENT CENTER OP is best match

VA MEDICAL CENTER - MANCHESTER
MANCHESTER VAMC / MANCHESTER VAMC PHARMACY is match

VA MEDICAL CENTER - MANCHESTER

THE COOPER UNIVERSITY HOSPITAL
THE COOPER HEALTH SYSTEM / None is match

THE COOPER UNIVERSITY HOSPITAL

EMERALD COAST BEHAVIORAL HOSPITAL
BAY MEDICAL CENTER / BA

...


KAISER FND HOSP - FRESNO
FAMILY CARE PROVIDERS / None is match

KAISER FND HOSP - FRESNO

EL PASO LTAC HOSPITAL
PAN AMERICAN GENERAL HOSPITAL / SOUTHWESTERN GENERAL HOSPITAL is match

GRACIE SQUARE HOSPITAL
NEW YORK GRACIE SQUARE HOSPITAL INC / None is match

ASSURANCE HEALTH PSYCHIATRIC HOSPITAL
WOODLAWN HOSPITAL / GREENCROFT HEALTHCARE is match

BARNES-JEWISH HOSPITAL - PSYCHIATRIC SUPPORT CENTER
STATE OF MISSOURI / METROPOLITAN ST. LOUIS PSYCHIATRIC CENTER is match

ST. MARTIN HOSPITAL
SLIDELL MEMORIAL HOSPITAL / ST TAMMANY PARISH HOSPITAL SERVICE DISTRICT #2 is match

ST. MARTIN HOSPITAL

KAISER FND HOSP - IRVINE
STANDIFORD HELM II, M.D. INC. / PACIFIC COAST PAIN MANAGEMENT CENTER is match

HEALTHSOUTH HARMARVILLE REHABILITATION HOSPITAL
ENCOMPASS HEALTH REHABILITATION HOSPITAL OF HARMARVILLE, LLC / ENCOMPASS HEALTH REHABILITATION HOSPITAL OF HARMARVILLE is match

HAYMARKET MEDICAL CENTER
NAVAL MEDICAL CENTER PORTSMOUTH / PORTS VA BHC OCEANA is match

PARK CENTER, INC
PARKVIEW HOS

OCCUPATIONAL THERAPY SERVICES INC / FLORIDA REHABILITATION AND PAIN CENTER is match

HEALTHSOUTH REHABILITATION HOSPITAL AT MARTIN HEALTH
EGRET COVE REHABILITATION CENTER, LLC / EGRET COVE CENTER is match

SOUTH FLORIDA STATE HOSPITAL
FLORIDA DEPARTMENTOF CHILDREN AND FAMILIES / S FL STATE HOSP is match

CHI ST JOSEPH HEALTH MADISON HOSPITAL
AHM ACTION HOME HEALTH LP / ENCOMPASS HEALTH HOME HEALTH is match

QUEEN OF THE VALLEY HOSPITAL - NAPA
QUEEN OF THE VALLEY MEDICAL ASSOCIATION / ST JOSEPH HERITAGE HEALTH SYSTEM is match

QUEEN OF THE VALLEY HOSPITAL - NAPA

FLORIDA HOSPITAL WESLEY CHAPEL
DRS ANGEL MORALES KALTER RAMOS-SANTOS FONTENOT MDS PA / FLORIDA PERINATAL ASSOCIATES is match

SOUTH LAKE HOSPITAL
SOUTH LAKE ANESTHESIA SERVICES, P.A. / None is match

KINDRED HOSPITAL - MANSFIELD
CHILDRESS COUNTY HOSPITAL DISTRICT / CHILDRESS REGIONAL MEDICAL CENTER is match

NORTH TAMPA BEHAVIORAL HEALTH
CORA HEALTH SERVICES INC / CORA PHYSICAL THERAPY - DELAND is match

RADY CHILDREN'S HOSPITA

SCOTTSDALE HEALTHCARE HOSPITALS / SCOTTSDALE HEALTHCARE OSBORN MEDICAL CENTER is match

PALO VERDE BEHAVIORAL HEALTH
LABORATORY CORPORATION OF AMERICA / None is match

PALO VERDE BEHAVIORAL HEALTH

ARIZONA STATE FORENSIC HOSPITAL
SURGICAL SPECIALTY HOSPITAL OF ARIZONA, LLC / THE CORE INSTITUTE SPECIALTY HOSPITAL is match

CARONDELET ST. MARY'S HOSPITAL
SUNSET INTERNAL MEDICINE & GERIATRICS PC / None is match

CHANDLER REGIONAL MEDICAL CENTER
TERRY M. CLAYTON, M.D., P.C. / None is match

CHANDLER REGIONAL MEDICAL CENTER

ST JOSEPH'S WESTGATE MEDICAL CENTER
BIO-MEDICAL APPLICATIONS OF ARIZONA, LLC / PHOENIX ARTIFICIAL KIDNEY CENTER is match

BANNER-UNIVERSITY MEDICAL CENTER TUCSON CAMPUS
LANCASTER HMA PHYSICIAN MANAGEMENT INC. / HEART OF LANCASTER REGIONAL MEDICAL CENTER CRNAS is match

BANNER-UNIVERSITY MEDICAL CENTER TUCSON CAMPUS

BANNER-UNIVERSITY MEDICAL CENTER SOUTH CAMPUS
UNIVERSITY PHYSICIANS HEALTHCARE / UNIVERSITY PHYSICIANS HOSPITAL @ KINO is match

UNIVERSITY OF ARIZONA MEDIC

OHIOHEALTH REHABILITATION HOSPITAL

POMEGRANATE HEALTH SYSTEMS OF COLUMBUS
BEHAVIORAL HEALTHCARE PARTNERS OF CENTRAL OHIO INC / MOUNDBUILDERS GUIDANCE CENTER is match

RAINBOW BABIES AND CHILDRENS HOSPITAL
PATHOLOGY ASSOCIATES OF UNIVERSITY HOSPITALS,INC / None is match

RAINBOW BABIES AND CHILDRENS HOSPITAL
UNIVERSITY HOSPITALS LABORATORY SERVICES FOUNDATION / None is best match

REGENCY HOSPITAL OF CLEVELAND EAST
CITY OF GREEN / CITY OF GREEN FINANCE is match

REGENCY HOSPITAL OF TOLEDO
ST ANNE MERCY HOSPITAL / OTHER is match

RIDGEVIEW HOSPITAL
STRONGSVILLE DIALYSIS LLC / STRONGSVILLE DIALYSIS is match

ACCESS HOSPITAL DAYTON, LLC
PROFESSIONALS PRN LLC / NORTHSIDE HOME INFUSION is match

ACCESS HOSPITAL DAYTON, LLC

AKRON CHILDREN'S HOSPITAL
MAKO'S MARKET, INC. / MAKO'S PHARMACY is match

SELECT SPECIALTY HOSPITAL-COLUMBUS, INC
SELECT SPECIALTY HOSPITAL - COLUMBUS INC / None is match

ARROWHEAD BEHAVIORAL HEALTH
HHC TOLEDO, INC / FOCUS HEALTHCARE OF OHIO is match

ARROWHEAD BEHAVIOR

UNIVERSITY OF NORTH CAROLINA HOSPITALS AT CHAPEL HILL / UNC HOME HEALTH is match

BLACKBERRY CENTER
LABORATORY CORPORATION OF AMERICA / None is match

LANDMARK HOSPITAL OF SOUTHWEST FLORIDA
STERLING EMERGENCY SERVICES OF FLORIDA PA / None is match

OVIEDO MEDICAL CENTER
MOUNT SINAI MEDICAL CENTER / None is match

OVIEDO MEDICAL CENTER

LAGUNA TREATMENT HOSPITAL, LLC
AG LAGUNA HILLS, LLC / LAGUNA HILLS HEALTH & REHABILITATION CENTER is match

LAGUNA TREATMENT HOSPITAL, LLC

CLEAR VIEW BEHAVIORAL HEALTH
PROFESSIONAL PHARMACY SERVICES / GOOD DAY PHARMACY is match

CLEAR VIEW BEHAVIORAL HEALTH

VERITAS COLLABORATIVE NORTH CAROLINA LLC
BEAUFORT REGIONAL PHYSICIANS, LLC / SEABOARD SURGICAL ASSOCIATES is match

ACADIA MONTANA
MONTANA EYECARE LLP / None is match

WOMEN'S HOSPITAL
SNOWSHOE LTC GROUP, LLC / GREENHAVEN HEALTH AND REHABILITATION CENTER is match

HEALTHSOUTH REHABILITATION HOSPITAL OF GULFPORT
MEMORIAL HOSPITAL AT GULFPORT / None is match

ST LUKES HOSPITAL MONROE CAMPUS
ST. LUKE'S

In [219]:
newly_matched = pd.DataFrame(id_dict).transpose()

In [208]:
all_stuff_2

ID         NPI                    Taxonomies  \
3319   15678840  1104830900                ['282N00000X']   
2219    5681230  1932109048                ['282NC0060X']   
1079    5656345  1780630939                ['282NC0060X']   
2709    9854736  1194737817                ['282NC0060X']   
67      9217756  1609816198  ['261QA1903X', '282NC0060X']   
...         ...         ...                           ...   
2822    8665201  1255374377                ['282N00000X']   
3428  129744710  1760431530                ['207R00000X']   
3569    4557702  1790748226                ['282N00000X']   
1021     905819  1720021181                ['282NC0060X']   
232     8960617  1053391359                ['282N00000X']   

                                                   NAME  \
3319                     VAL VERDE HOSPITAL CORPORATION   
2219                           GUNNISON VALLEY HOSPITAL   
1079                            UNITY FAMILY HEALTHCARE   
2709  CHIPPEWA VALLEY HOSPITAL & OAKVIEW CARE CENTER...   
67                                           UPMC MUNCY   
...                                                 ...   
2822                                        VA HOSPITAL   
3428                             24 ON PHYSICIANS, P.C.   
3569                            RAPID CITY IHS HOSPITAL   
1021  NORTHEASTERN VERMONT REGIONAL HOSPITAL DIETARY...   
232                    SOUTH SHORE HOSPITAL CORPORATION   

                             OTHER_NAME                MAILING_ADDRESS_1  \
3319  VAL VERDE REGIONAL MEDICAL CENTER                 801 N BEDELL AVE   
2219                               None                  711 N TAYLOR ST   
1079             ST. GABRIEL'S HOSPITAL                    815 2ND ST SE   
2709           CHIPPEWA VALLEY HOSPITAL                       PO BOX 224   
67                                 None  600 GRANT STREET US STEEL TOWER   
...                                 ...                              ...   
2822                               None                  800 HOSPITAL DR   
3428                               None                  P.O. BOX 403631   
3569                               None              3200 CANYON LAKE DR   
1021                               None                 1315 HOSPITAL DR   
232                                None               8012 S CRANDON AVE   

                  MAILING_ADDRESS_2  MAILING_CITY MAILING_STATE MAIING_ZIP  \
3319                           None       DEL RIO            TX  788404112   
2219                           None      GUNNISON            CO  812302296   
1079                           None  LITTLE FALLS            MN  563453505   
2709                           None        DURAND            WI  547360224   
67    59TH FLOOR, C/O RENEE JOHNSON    PITTSBURGH            PA  152192740   
...                             ...           ...           ...        ...   
2822                        UNIT 2C      COLUMBIA            MO  652015275   
3428                           None       ATLANTA            GA  303843631   
3569                           None    RAPID CITY            SD  577028114   
1021                           None  ST JOHNSBURY            VT   58199210   
232              FINANCE DEPARTMENT       CHICAGO            IL  606171124   

     MAILING_PHONE       LOCATION_ADDRESS_1  LOCATION_ADDRESS_2 LOCATION_CITY  \
3319    8307758566         801 N BEDELL AVE                None       DEL RIO   
2219    9706411456          711 N TAYLOR ST                None      GUNNISON   
1079    3206325441            815 2ND ST SE                None  LITTLE FALLS   
2709    7156724211           1220 3RD AVE W                None        DURAND   
67      4126236303           215 E WATER ST                None         MUNCY   
...            ...                      ...                 ...           ...   
2822    5738146000          800 HOSPITAL DR             UNIT 2C      COLUMBIA   
3428    7707400895  2600 SIXTH STREET, S.W.                None        CA

In [231]:
THIS_LSIT = []
count = 0
for row in pd.merge(newly_matched, GOV_HOSPITAL, on='ID').itertuples():
    if row.CITY_x != row.CITY_y and row.ADD_SCORE < 80:
            print(f'{row.NAME_x}/{row.OTHER_NAME} maybe not {row.NAME_y}')
            count += 1
    else:
        print (f'{row.NAME_x}/{row.OTHER_NAME} probably {row.NAME_y}')
        new_dict = {
            'ID': row.ID,
            'NPI': row.NPI
            }
        THIS_LSIT.append(new_dict)
    print('-----')
print(count)

BEARABLE DIAGNOSTIC CENTER, LLC/None maybe not CARL R. DARNALL ARMY MEDICAL CENTER
-----
WILSON COUNTY HOSPITAL/WILSON MEDICAL CENTER maybe not IRWIN ARMY COMMUNITY HOSPITAL
-----
EISENHOWER ARMY MEDICAL CENTER/AMC EISENHOWER-GORDON probably EISENHOWER ARMY MEDICAL CENTER
-----
WASHINGTON DC VAMC/FT. BELVOIR VA CLINIC probably FORT BELVOIR COMMUNITY HOSPITAL
-----
WOMACK ARMY MEDICAL CENTER/WOMACK ARMY MEDICAL CENTER probably WOMACK ARMY MEDICAL CENTER
-----
GHEP CORPUS CHRISTI PLLC/None probably THE CORPUS CHRISTI MEDICAL CENTER - DOCTORS REGIONAL
-----
CHRISTUS TRINITY CLINIC/CHRISTUS TRINITY CLINIC maybe not CHRISTUS SPOHN HOSPITAL CORPUS CHRISTI SOUTH
-----
H K A CORPORATION/AMERICAN HOME HEALTH & HOSPICE probably MCALLEN HEART HOSPITAL
-----
WEBSTER SURGICAL SPECIALTY HOSPITAL, LTD/HOUSTON PHYSICIANS' HOSPITAL maybe not MISSION TRAIL BAPTIST HOSPITAL-ER
-----
RIVER CITY NURSE MANAGEMENT LLC/None probably NORTHEAST BAPTIST HOSPITAL
-----
SLP OVERTON LLC/OVERTON HEALTHCARE CENTER ma

ST ELIZABETH MEDICAL CENTER, INC/ST ELIZABETH GRANT maybe not THE MEDICAL CENTER AT ALBANY
-----
SUPERIOR WALK-IN CENTER, PC/None probably MUNISING MEMORIAL HOSPITAL
-----
DEAN RETAIL SERVICES INC/SSM HEALTH PRESCRIPITON CENTER probably ST MARYS HOSPITAL
-----
UNITY HOSPITAL/None probably MERCY HOSPITAL – UNITY CAMPUS
-----
TRINITY KENMARE HOSPITAL/KENMARE HEALTH CENTER probably KENMARE COMMUNITY HOSPITAL
-----
CHICAGO HEALTH AND PHYSICAL THERAPY CENTER SC/None maybe not CHICAGO BEHAVIORAL HOSPITAL
-----
LINCOLN SURGERY CENTER LLC/None probably LINCOLN SURGICAL HOSPITAL
-----
ENCOMPASS HEALTH REHABILITATION HOSPITAL OF ALBUQUERQUE, LLC/HEALTHSOUTH REHABILITATION HOSPITAL probably KINDRED HOSPITAL - ALBUQUERQUE
-----
KAISER PERMANENTE/None probably KAISER SUNNYSIDE MEDICAL CENTER
-----
IN HOME HEALTH LLC/HEARTLAND HOME HEALTH CARE maybe not HEALTHSOUTH REHABILITATION HOSPITAL OF MIDDLETOWN
-----
THOMAS M. CONNELLY L.L.C./FRIENDSHIP HEIGHTS CHIROPRACTIC probably BRIDGEPOINT HOSPITAL CAPI

DEPARTAMENTO DE SALUD OFICIAL/HOSPITAL UNIVERSITARIO DR RAMON RUIZ ARNAU probably HOSP UNIVERSITARIO DR RAMON RUIZ ARNAU
-----
TUFTS MEDICAL CENTER, INC./TUFTS MEDICAL CENTER maybe not NORTH SHORE MEDICAL CENTER  - UNION CAMPUS
-----
HEBREW HOME AND HOSPITAL INC/None probably HOSPITAL AT HEBREW HEALTH CARE
-----
PARKER'S LANE EMERGENCY PHYSICIANS LLC/None probably INOVA MOUNT VERNON HOSPITAL
-----
MISSISSIPPI METHODIST HOSPITAL & REHABILITATION CENTER, INC./METHODIST REHAB CENTER probably MS METHODIST REHABILITATION CENTER
-----
MENTAL HEALTH INSTITUTE/None probably CHEROKEE MENTAL HEALTH INSTITUTE
-----
CAVALIER COUNTY MEMORIAL HOSPITAL ASSOCIATION/CAVALIER COUNTY MEMORIAL HOSPITAL & CLINICS probably CCMH & CLINICS
-----
CATHOLIC HEALTH INITIATIVES COLORADO/CENTURA HOME OXYGEN probably COLORADO MENTAL HEALTH INSTITUTE AT FT LOGAN
-----
TUBA CITY REGIONAL HEALTH CARE CORPORATION/TUBA CITY INDIAN MEDICAL CENTER probably TUBA CITY REGIONAL HEALTH CARE
-----
LOURDES HOSPITAL LLC/LOURDES M

-----
TRINITY HEALTH/TRINITY REGIONAL EYECARE WILLIAMS CENTER probably TRINITY HOSPITALS
-----
HARRINGTON PHYSICAL THERAPY, PC/MANGER HARRINGTON, PT probably SHODAIR CHILDRENS HOSPITAL
-----
KIRBY MEDICAL CENTER/None maybe not OSF SAINT ELIZABETH MEDICAL CENTER
-----
STATE OF OKLAHOMA/GRIFFIN MEMORIAL HOSPITAL probably SAIN FRANCIS HOSPITAL MUSKOGEE EAST
-----
SOUTHEAST TEXAS NEPHROLOGY ASSOCIATES PA/None maybe not CHRISTUS SOUTHEAST TEXAS ORTHOPEDIC SPECIALTY CENTER
-----
SAN FRANCISCO HEALTH SYSTEM INC/HOSPITAL SAN FRANCISCO probably HOSP SAN FRANCISCO
-----
COORDINATED PRIMARY CARE, INC./MATERNAL FETAL MONITORING ASSOCIATES probably UMASS MEMORIAL MEDICAL CENTER - MEMORIAL CAMPUS
-----
SAINT JOSEPH MEDICAL CENTER, INC./None probably UNIVERSITY OF MARYLAND SAINT JOSEPH MEDICAL CENTER
-----
SOUTH CAROLINA CVS PHARMACY LLC/CVS PHARMACY #04385 maybe not SOUTH CAROLINA VOCATIONAL REHABILITATION EVALUATION CENTER
-----
MARSHALL COUNTY HOSP DISTRICT/MARSHALL COUNTY HOSPITAL PHARMACY probab

-----
HEART CENTER OF SOUTH FLORIDA LLC/None maybe not DEVEREUX HOSPITAL AND CHILDREN'S CENTER OF FLORIDA
-----
MAPLEWOOD PATHOLOGY PC/None probably PARKRIDGE VALLEY HOSPITAL
-----
PARAGON HEALTH PC/BRIGHT FUTURES PEDIATRICS maybe not MACKINAC STRAITS HOSPITAL AND HEALTH CENTER
-----
MCCAMEY CONVALESCENT CENTER/MCCAMEY HOSPITAL DISTRICT maybe not CEDAR CREST HOSPITAL
-----
LOVELACE SANDIA HEALTH SYSTEM/LOVELACE PHYSICIAN GROUP probably HAVEN BEHAVIORAL HOSPITAL OF ALBUQUERQUE
-----
OKANOGAN DOUGLAS COUNTY HOSPITAL DIST 1/THREE RIVERS HOSPITAL maybe not FORKS COMMUNITY HOSPITAL
-----
CENTRA HEALTH PROFESSIONAL SERVICES, LLC/ALTAVISTA MEDICAL CENTER maybe not DANVILLE REGIONAL MEDICAL CENTER
-----
OWENSBORO PATHOLOGY PSC/None probably OWENSBORO HEALTH REGIONAL HOSPITAL
-----
ONNURI HEALTHCARE LLC/PRANA PHARMACY AND HOMECARE maybe not FRANCISCAN HEALTHCARE RENSSLAER
-----
HENRY FORD MACOMB HOSPITAL CORPORATION/HENRY FORD MACOMB HOSPITAL probably HENRY FORD MACOMB HOSPITAL
-----
ASCENSION 

...

MERCY HOSPITAL, INC/CAROLINAS HEALTHCARE SYSTEM PINEVILLE probably CAROLINA CONTINUECARE AT PINEVILLE
-----
ATHENS ANESTHESIA ASSOCIATES, INC./None probably STARR REGIONAL MEDICAL CENTER
-----
MERCY HEALTH - ANDERSON HOSPITAL, LLC/MERCY HOSPITAL ANDERSON maybe not DUBLIN METHODIST HOSPITAL
-----
ST LOUIS UNIVERSITY/SLUCARE DEPARTMENT OF PEDIATRIC SURGERY probably SSM HEALTH CARDINAL GLENNON CHILDREN'S MEDICAL CENTER
-----
SELECT SPECIALTY HOSPITAL - SOUTH DALLAS INC/None probably METHODIST REHABILITATION HOSPITAL
-----
NORTHWEST CRITICAL CARE PHYSICIANS, P.S./None probably CASCADE BEHAVIORAL HOSPITAL
-----
ALTOONA VAMC/ALTOONA VAMC PHARMACY probably JAMES E VAN ZANDT VA MEDICAL CENTER
-----
HENRY FORD HEALTH SYSTEM/HENRY FORD MEDICAL CENTER PHARMACY probably HENRY FORD HOSPITAL
-----
FOX VALLEY PATHOLOGISTS SC/None probably CHILDRENS HSPTL OF WISCONSIN FOX VALLEY
-----
MITCHELL COUNTY HOSPITAL HEALTH SYSTEMS/None maybe not VIA CHRISTI HOSPITAL WICHITA ST TERESA INC
-----
MERCY HOSPITAL

-----
KAWEAH DELTA HEALTH CARE DISTRICT/KAWEAH DELTA REHABILITATION HOSPITAL probably KAWEAH DELTA REHABILITATION HOSPITAL
-----
TOTAL EYE CARE CENTERS PC/None maybe not ST JOHN VIANNEY CENTER
-----
LYLE FREEDMAN MD HUGULEY OPTICAL/None maybe not BAYLOR SCOTT & WHITE MEDICAL CENTER - GARLAND
-----
PROVIDENCE SAINT JOHN'S HEALTH CENTER/None maybe not KEDREN COMMUNITY MENTAL HEALTH CENTER
-----
LEHIGH VALLEY HOSPITAL/HEALTH SPECTRUM PHARMACY SERVICES probably LEHIGH VALLEY HOSPITAL
-----
LEESBURG REGIONAL MEDICAL CENTER D/B/A LRMC NURSING CENTER/LRMC NURSING CENTER probably LEESBURG REHABILITATION HOSPITAL
-----
LAWSON AND CROMER INC/LAWSON AND CROMER PHARMACY maybe not EMORY JOHNS CREEK HOSPITAL
-----
DALLAS COUNTY HOSPITAL DISTRICT/OAK WEST HEALTH CENTER maybe not SAGECREST HOSPITAL GRAPEVINE
-----
CHA HOLLYWOOD MEDICAL CENTER LP/HOLLYWOOD PRESBYTERIAN MEDICAL CENTER maybe not KERN MEDICAL CENTER
-----
PIH HEALTH HOSPITAL WHITTIER/PIH HEALTH HOME HEALTHCARE probably KINDRED HOSPITAL - 

AHMC WHITTIER HOSPITAL MEDICAL CENTER LP/WHITTIER HOSPITAL MEDICAL CENTER maybe not RIVERSIDE COUNTY REGIONAL MEDICAL CENTER - D/P APH
-----
RGV-NUECES REHABILITATION, INC./INNOVATIVE PHYSICAL THERAPY & SPORTS MEDICINE CENTERS maybe not MESQUITE REHABILITATION HOSPITAL
-----
SUNRAY OPERATING COMPANY LLC/SUNRAY HEALTHCARE CENTER maybe not SACRAMENTO COUNTY MENTAL HEALTH TREATMENT CENTER
-----
SENIOR CARE OF ST JOHNS OPERATOR LLC/ST JOHNS HEALTH CARE CENTER maybe not ST JOSEPH'S HOSPITAL BEHAVIORAL HEALTH CENTER
-----
COUNTY OF SAN DIEGO/SAN DIEGO COUNTY DEPARTMENT OF HEALTH SERVICES PHARMACY probably SAN DIEGO COUNTY PSYCHIATRIC HOSPITAL
-----
TOTAL RENAL CARE INC/NEW PORT RICHEY KIDNEY CENTER maybe not ST JOSEPH'S HOSPITAL NORTH
-----
IVOR GREEN M.D. A PROFESSIONAL CORPORATION/None probably SAN GABRIEL VALLEY MEDICAL CENTER
-----
COUNTY OF SAN JOAQUIN/SAN JOAQUIN COUNTY BEHAVIORAL HEALTH SERVICES probably SAN JOAQUIN COUNTY P.H.F.
-----
NORTH BROWARD HOSPITAL DISTRICT/NORTH BROWARD MED

-----
CONTINUECARE HOSPITAL OF TYLER, INC./TYLER CONTINUECARE HOSPITAL AT MOTHER FRANCES HOSPITAL maybe not KINDRED HOSPITAL THE HEIGHTS
-----
ALLIANCE HOSPITAL, LTD/None maybe not KINDRED HOSPITAL TOMBALL
-----
IFA MEDICAL CENTER INC/UNIVERSITY HEALTH CARE CENTER probably JACKSON MEMORIAL MENTAL HEALTH CENTER - INPATIENT
-----
INTRACARE HOSPITAL NORTH/INTRACARE NORTH HOSPITAL probably KINDRED HOSPITAL TOWN & COUNTRY
-----
TEXAS HILL COUNTRY ORTHOPAEDICS, P.A./None maybe not OCEANS BEHAVIORAL HOSPITAL OF KATY
-----
FOOT AND ANKLE CENTER OF NORTH HOUSTON P A/None probably PROVIDENCE HOSPITAL OF NORTH HOUSTON LLC
-----
CHILDRESS COUNTY HOSPITAL DISTRICT/CHILDRESS HEALTHCARE CENTER maybe not TEXAS CHILDREN'S HOSPITAL WEST CAMPUS
-----
TEXAN NURSING AND REHAB OF SAN MARCOS LLC/CARE INN OF SAN MARCOS, LLC probably WELLBRIDGE HOSPITAL OF SAN MARCOS
-----
THE UNIVERSITY OF TEXAS SOUTHWESTERN MEDICAL CENTER AT DALLAS/UTSW MONCRIEF RADIATION ONCOLOGY maybe not WARM SPRINGS REHABILITATION HOSPIT

REDOAK CARDIOVASCULAR CENTER, PA/None probably TEXIENNE HOSPITAL SYSTEMS
-----
RONALD E MEYER PLLC/None probably OCEANS BEHAVIORAL HOSPITAL OF THE PERMIAN BASIN
-----
IRVING COPPELL SURGICAL HOSPITAL/None probably BAYLOR SURGICAL HOSPITAL AT LAS COLINAS
-----
M DS CYBER CLINIC PA/NORTHWEST DIAGNOSTIC CLINIC probably BAYLOR SCOTT & WHITE EMERGENCY HOSPITAL AT CEDAR PARK
-----
DALLAS COUNTY HOSPITAL DISTRICT/HATCHER STATION PHARMACY maybe not BAYLOR SCOTT & WHITE CONTINUING CARE HOSPITAL
-----
KCI USA, INC./None maybe not MESA SPRINGS
-----
MATRIX REHABILITATION- TEXAS, INC./MATRIX REHABILITATION OF FRISCO maybe not NEW BRAUNFELS REGIONAL REHABILITATION HOSPITAL
-----
OCCUPATIONAL HEALTH CENTERS OF THE SOUTHWEST, P.A./CONCENTRA MEDICAL CENTER maybe not SETON MEDICAL CENTER HARKER HEIGHTS
-----
CORNERSTONE REGIONAL HOSPITAL, LP/None maybe not OCEANS BEHAVIORAL HOSPITAL OF LUFKIN
-----
HEALTHCARE CENTER OF HENDERSON/SOUTHWOOD NURSING & REHABILITATION maybe not HEALTHSOUTH REHABILITATION HO

In [222]:
pd.merge(newly_matched, GOV_HOSPITAL, on='ID')

ID                                    NAME_x  \
0             4           BEARABLE DIAGNOSTIC CENTER, LLC   
1             8                    WILSON COUNTY HOSPITAL   
2            26            EISENHOWER ARMY MEDICAL CENTER   
3            28                        WASHINGTON DC VAMC   
4            37                WOMACK ARMY MEDICAL CENTER   
...         ...                                       ...   
2383  181228719       MOUNTAIN AREA RECOVERY CENTER, INC.   
2384  181671459       BAYNE-JONES ARMY COMMUNITY HOSPITAL   
2385  181742223       BLANCHFIELD ARMY COMMUNITY HOSPITAL   
2386  181992055             NAVAL HOSPITAL CAMP PENDLETON   
2387  182120889  WALTER REED NATIONAL MILITARY MED CENTER   

                      OTHER_NAME          CITY_x  \
0                           None         MCALLEN   
1          WILSON MEDICAL CENTER        NEODESHA   
2          AMC EISENHOWER-GORDON     FORT GORDON   
3          FT. BELVOIR VA CLINIC      FT BELVOIR   
4     WOMACK ARMY MEDICAL CENTER      FORT BRAGG   
...                          ...             ...   
2383                        None           CLYDE   
2384                   POLK PHCY         FT POLK   
2385         CAMPB TOWN CTR PHCY   FORT CAMPBELL   
2386              CAMP PEND PHCY  CAMP PENDLETON   
2387       BETHESDA HEM ONC PHCY        BETHESDA   

                                  ADDRESS_x         NPI ADD_SCORE NAME_SCORE  \
0                          1305 NOLANA LOOP  1285610097        57         48   
1                            2600 OTTAWA RD  1760407407      64.5         75   
2                  300 W HOSPITAL RD BLDG W  1578660742        87        100   
3                          9300 DEWITT LOOP  1770533358       100         54   
4     2817 REILLY ROAD MCXC_COD CREDENTIALS  1487754958      75.5        100   
...                                     ...         ...       ...        ...   
2383                     414 HOSPITAL DRIVE  1508968975        60         47   
2384                       BLDG 1585 3RD ST  1033218441        86        100   
2385                    650 JOEL DR BLDG 98  1275630022      85.5        100   
2386                       200 MERCY CIRCLE  1659476901      79.5        100   
2387                     8901 WISCONSIN AVE  1982703393      63.5         95   

               X          Y  ...                  VAL_DATE  \
0     -97.774290  31.130906  ...  2015-07-28T00:00:00.000Z   
1     -96.772446  39.079192  ...  2015-07-25T00:00:00.000Z   
2     -82.125897  33.430333  ...  2015-07-24T00:00:00.000Z   
3     -77.143680  38.705603  ...  2015-07-29T00:00:00.000Z   
4     -79.002170  35.145626  ...  2015-07-28T00:00:00.000Z   
...          ...        ...  ...                       ...   
2383  -83.318550  35.482345  ...  2019-04-17T00:00:00.000Z   
2384  -93.213801  31.062456  ...  2019-05-16T00:00:00.000Z   
2385  -87.447485  36.636641  ...  2019-05-16T00:00:00.000Z   
2386 -117.388804  33.221316  ...  2019-05-16T00:00:00.000Z   
2387  -77.093590  39.001287  ...  2019-05-16T00:00:00.000Z   

                                                WEBSITE       STATE_ID  \
0                     http://www.crdamc.amedd.army.mil/  NOT AVAILABLE   
1                           http://iach.amedd.army.mil/  NOT AVAILABLE   
2                     http://www.ddeamc.amedd.army.mil/  NOT AVAILABLE   
3                                  www.fbch.capmed.mil/  NOT AVAILABLE   
4                       http://www.wamc.amedd.army.mil/  NOT AVAILABLE   
...                                                 ...            ...   
2383  http://www.ihs.gov/Nashville/index.cfm?module=...  NOT AVAILABLE   
2384                                      NOT AVAILABLE  NOT AVAILABLE   
2385                                      NOT AVAILABLE  NOT AVAILABLE   
2386                                      NOT AVAILABLE  NOT AVAILABLE   
2387  https://www.wrnmmc.capmed.mil/SitePages/home.aspx  NOT AVAILABLE   

           ALT_NAME ST_FIPS                 OWNER TTL_STAFF 

In [230]:
all_stuff_2

ID         NPI                    Taxonomies  \
3319   15678840  1104830900                ['282N00000X']   
2219    5681230  1932109048                ['282NC0060X']   
1079    5656345  1780630939                ['282NC0060X']   
2709    9854736  1194737817                ['282NC0060X']   
67      9217756  1609816198  ['261QA1903X', '282NC0060X']   
...         ...         ...                           ...   
2822    8665201  1255374377                ['282N00000X']   
3428  129744710  1760431530                ['207R00000X']   
3569    4557702  1790748226                ['282N00000X']   
1021     905819  1720021181                ['282NC0060X']   
232     8960617  1053391359                ['282N00000X']   

                                                   NAME  \
3319                     VAL VERDE HOSPITAL CORPORATION   
2219                           GUNNISON VALLEY HOSPITAL   
1079                            UNITY FAMILY HEALTHCARE   
2709  CHIPPEWA VALLEY HOSPITAL & OAKVIEW CARE CENTER...   
67                                           UPMC MUNCY   
...                                                 ...   
2822                                        VA HOSPITAL   
3428                             24 ON PHYSICIANS, P.C.   
3569                            RAPID CITY IHS HOSPITAL   
1021  NORTHEASTERN VERMONT REGIONAL HOSPITAL DIETARY...   
232                    SOUTH SHORE HOSPITAL CORPORATION   

                             OTHER_NAME                MAILING_ADDRESS_1  \
3319  VAL VERDE REGIONAL MEDICAL CENTER                 801 N BEDELL AVE   
2219                               None                  711 N TAYLOR ST   
1079             ST. GABRIEL'S HOSPITAL                    815 2ND ST SE   
2709           CHIPPEWA VALLEY HOSPITAL                       PO BOX 224   
67                                 None  600 GRANT STREET US STEEL TOWER   
...                                 ...                              ...   
2822                               None                  800 HOSPITAL DR   
3428                               None                  P.O. BOX 403631   
3569                               None              3200 CANYON LAKE DR   
1021                               None                 1315 HOSPITAL DR   
232                                None               8012 S CRANDON AVE   

                  MAILING_ADDRESS_2  MAILING_CITY MAILING_STATE MAIING_ZIP  \
3319                           None       DEL RIO            TX  788404112   
2219                           None      GUNNISON            CO  812302296   
1079                           None  LITTLE FALLS            MN  563453505   
2709                           None        DURAND            WI  547360224   
67    59TH FLOOR, C/O RENEE JOHNSON    PITTSBURGH            PA  152192740   
...                             ...           ...           ...        ...   
2822                        UNIT 2C      COLUMBIA            MO  652015275   
3428                           None       ATLANTA            GA  303843631   
3569                           None    RAPID CITY            SD  577028114   
1021                           None  ST JOHNSBURY            VT   58199210   
232              FINANCE DEPARTMENT       CHICAGO            IL  606171124   

     MAILING_PHONE       LOCATION_ADDRESS_1  LOCATION_ADDRESS_2 LOCATION_CITY  \
3319    8307758566         801 N BEDELL AVE                None       DEL RIO   
2219    9706411456          711 N TAYLOR ST                None      GUNNISON   
1079    3206325441            815 2ND ST SE                None  LITTLE FALLS   
2709    7156724211           1220 3RD AVE W                None        DURAND   
67      4126236303           215 E WATER ST                None         MUNCY   
...            ...                      ...                 ...           ...   
2822    5738146000          800 HOSPITAL DR             UNIT 2C      COLUMBIA   
3428    7707400895  2600 SIXTH STREET, S.W.                None        CA

In [239]:
this_list = pd.DataFrame(THIS_LSIT)
once_again = pd.merge(this_list, npi_with_taxes, on='NPI')

In [243]:
ALL_STUFF_3 = pd.concat([all_stuff_2,once_again])

In [247]:
CURRENT_STATUS = pd.merge(ALL_STUFF_3, GOV_HOSPITAL, on='ID', suffixes = ['_NPI','_GOV']).sort_values('NAME_NPI')

In [248]:
CURRENT_STATUS.to_csv('Almost_There.csv', index=False)

In [272]:
current_list_2 = list(CURRENT_STATUS['ID'])

In [268]:
# missing_npi = npi_hospitals[npi_hospitals['NPI'].isin(current_list)==False]
missing_gov = GOV_HOSPITAL[GOV_HOSPITAL['ID'].isin(current_list_2)==False]

In [265]:
MISSING_NPIS =[]
UNMATCHED_COUNT  = 0
for row in missing_npi.itertuples():
    match = False
    new_df = CURRENT_STATUS[CURRENT_STATUS['STATE'] == row.LOCATION_STATE]
    for line in new_df.itertuples():
        if max([match_address_2(line.LOCATION_ADDRESS_1,row.LOCATION_ADDRESS_1),match_address_2(line.ADDRESS,row.LOCATION_ADDRESS_1)]) >80:
            print(f'{row.NAME} potentially in list, matching to {line.NAME_GOV}')
            match =True
    if match == False:
        print(F'Potential missing: {row.NAME}')
        UNMATCHED_COUNT += 1
        MISSING_NPIS.append(row.NPI)
    print('---')
        

Potential missing: USAF 95MDOS
---
MILWAUKEE VA potentially in list, matching to CLEMENT J. ZABLOCKI VA MEDICAL CENTER
---
Potential missing: CHILDREN'S HOSPITAL BOSTON
---
SAINT VINCENT CATHOLIC MEDICAL CENTER potentially in list, matching to RICHMOND UNIVERSITY MEDICAL CENTER - MAIN CAMPUS
---
V A MEDICAL CENTER - WILMINGTON, DELAWARE potentially in list, matching to WILMINGTON VA MEDICAL CENTER
---
Potential missing: MINNEAPOLIS V A MEDICAL CENTER
---
V.A. MED CENTER potentially in list, matching to CINCINNATI VA MEDICAL CENTER
---
V.A.N.J.HEALTHCARE SYSTEM potentially in list, matching to VA MEDICAL CENTER - LYONS CAMPUS
---
IMH PROFESSIONAL RAD potentially in list, matching to IREDELL MEMORIAL HOSPITAL, INCORPORATED
---
Potential missing: VA CARRIBEAN HEALTHCARE SYSTEM
---
MIRNA L. VALENCIA, M.D., P.A. potentially in list, matching to PALMETTO GENERAL HOSPITAL
---
VA CENTRAL IOWA potentially in list, matching to METHODIST WEST HOSPITAL
VA CENTRAL IOWA potentially in list, matching

VANTXHCS potentially in list, matching to VA MEDICAL CENTER - DALLAS
---
BRIGHAM & WOMEN'S HOSPITAL potentially in list, matching to SIGNATURE HEALTHCARE BROCKTON HOSPITAL
---
ROBERT J DOLE VAMC potentially in list, matching to ROBERT J. DOLE VA MEDICAL CENTER
---
BRIDGEPORT ANESTHESIA ASSOCIATES,P.C potentially in list, matching to BRIDGEPORT HOSPITAL
---
Potential missing: ROBERT BELANGER,D.O.
---
Potential missing: ROBERT BELANGER
---
VETERAN ADMINISTRATION potentially in list, matching to SPOKANE VA MEDICAL CENTER
---
VETERAN AFFAIRS MEDICAL CENTER potentially in list, matching to W. G. (BILL) HEFNER VA MEDICAL CENTER
---
VETERAN AFFAIRS MEDICAL CENTER potentially in list, matching to OSCAR G. JOHNSON VA MEDICAL CENTER
---
BRAINTREE HOSPITAL LLC. potentially in list, matching to KINDRED HOSPITAL NORTHEAST - STOUGHTON
---
VETERAN HOSPITAL potentially in list, matching to VA MEDICAL CENTER - LYONS CAMPUS
---
VANTHCS potentially in list, matching to VA MEDICAL CENTER - DALLAS
---
Pote

---
Potential missing: MULTICARE HEALTH SYSTEM
---
ST JOSEPHS HOSPITAL potentially in list, matching to SAINT JOSEPHS HOSPITAL AND MEDICAL CENTER
---
Potential missing: ROSWELL PARK CANCER INSTITUTE
---
ROSEBURG VA HEALTHCARE SYSTEM potentially in list, matching to ROSEBURG VA MEDICAL CENTER
---
ROSEBURG VA HEALTH CARE SYSTEM potentially in list, matching to ROSEBURG VA MEDICAL CENTER
---
Potential missing: RONALD T PURCELL
---
Potential missing: VA SANDIEGO HEALTH CARE SYSTEM
---
Potential missing: CAMBRIDGE HEALTH ALLIANCE
---
Potential missing: CARITAS SAINT ELIZABETH'S MEDICAL CENTER
---
Potential missing: IDAHO FALLS RECOVERY CENTER
---
Potential missing: CAPITAL REGION GERIATRIC CENTER, INC.
---
MT VERNON HOSPITAL potentially in list, matching to MONTEFIORE MOUNT VERNON HOSPITAL
---
ST LUKE'S REGIONAL MEDICAL CENTER potentially in list, matching to ST. LUKE'S REGIONAL MEDICAL CENTER
---
VA NORTH TEXAS HEALTH CARE SYSTEM potentially in list, matching to VA MEDICAL CENTER - DALLAS


MD ANDERSON CANCER CENTER potentially in list, matching to UNIVERSITY OF TEXAS M.D. ANDERSON CANCER CENTER
---
Potential missing: MEDDAC-WACH
---
Potential missing: MEDICAL ACCOUNT SERVICES
---
GOOD SAMARITAN HOSPITAL potentially in list, matching to GOOD SAMARITAN HOSPITAL-BAKERSFIELD
---
MEDICAL MATRIX potentially in list, matching to DOCTORS' COMMUNITY HOSPITAL
---
Potential missing: COUNTY OF TUOLUMNE
---
JEFFERSON REGIONAL MEDICAL CENTER potentially in list, matching to JEFFERSON REGIONAL MEDICAL CENTER
---
Potential missing: MEDICAL UNIVESRSITY OF SOUTH CAROLINA
---
Potential missing: JEFFERSON COUNTY COMMISSION
---
MEDVAMC potentially in list, matching to MICHAEL E. DEBAKEY VA MEDICAL CENTER
---
Potential missing: UNITED STATES AIR FORCE
---
UNION HOSPITAL INC potentially in list, matching to HANCOCK REGIONAL HOSPITAL
UNION HOSPITAL INC potentially in list, matching to UNION HOSPITAL CLINTON
---
Potential missing: MEMORIAL BEHAVIORAL HEALTH
---
Potential missing: JOHN H STROGER 

---
PARAGON LONG TERM ACUTE CARE HOSPITAL potentially in list, matching to BATON ROUGE BEHAVIORAL HOSPITAL
---
WILLIAM JENNINGS BRYAN DORN VETERANS HOSPITAL potentially in list, matching to WILLIAM JENNINGS BRYAN DORN VA MEDICAL CENTER
---
Potential missing: BARNES-JEWISH HOSPITAL
---
Potential missing: PARIS REGIONAL MEDICAL CENTER
---
Potential missing: WILLMAR REGIONAL TREATMENT CENTER
---
WALTER REED ARMY MEDICAL CENTER potentially in list, matching to HOWARD UNIVERSITY HOSPITAL
---
ALLENTOWN SPECIALTY HOSPITAL potentially in list, matching to LEHIGH VALLEY HOSPITAL-MUHLENBERG
ALLENTOWN SPECIALTY HOSPITAL potentially in list, matching to GOOD SHEPHERD SPECIALTY HOSPITAL
---
WALTER REED ARMY MEDICAL CENTER potentially in list, matching to HOWARD UNIVERSITY HOSPITAL
---
Potential missing: REGENCY HOSPITAL OF HATTIESBURG, LLC
---
Potential missing: NORTHEAST JOINT VENTURE, LLC
---
Potential missing: HILL TOP CENTER
---
WASHINGTON COUNTY HOSPITAL potentially in list, matching to FREDER

...

PRESCOTT VAMC potentially in list, matching to VALLEY VIEW MEDICAL CENTER
---
Potential missing: PALO ALTO VAMC
---
LONG BEACH VAMC potentially in list, matching to NEWPORT BAY HOSPITAL
LONG BEACH VAMC potentially in list, matching to SOUTHERN INYO HOSPITAL
LONG BEACH VAMC potentially in list, matching to VA LONG BEACH HEALTHCARE SYSTEM
---
PORTLAND VAMC potentially in list, matching to PORTLAND VA MEDICAL CENTER
---
PALO ALTO VAMC potentially in list, matching to VA MEDICAL CENTER - PALO ALTO DIVISION
---
PALO ALTO VAMC potentially in list, matching to VA MEDICAL CENTER - LIVERMORE DIVISION
---
Potential missing: MARTINEZ VAMC
---
Potential missing: DAVIE MEDICAL CENTER
---
Potential missing: HOSPITAL SERVICE DISTRICT NO1 PARISH OF AVOYELLES STATE OF LOUISIANA
---
Potential missing: UNIVERSITY OF KANSAS HOSPITAL AUTHORITY
---
NAVAL MEDICAL CENTER PORTSMOUTH potentially in list, matching to NAVAL MEDICAL CENTER PORTSMOUTH
---
Potential missing: NAVAL HOSPITAL YOKOSUKA
---
Potential mis

---
Potential missing: CYPRESS GROVE BEHAVIORAL HEALTH LLC
---
PUBLIC HOSPITAL DISTRICT NO. 2, KLICKITAT COUNTY, WASHINGTON potentially in list, matching to SKYLINE HOSPITAL
---
Potential missing: MAJOR HOSPITAL
---
Potential missing: THE MIRIAM HOSPITAL
---
UNIVERSITY OF ALABAMA AT BIRMINGHAM potentially in list, matching to UNIVERSITY OF ALABAMA HOSPITAL
---
ATLANTA VAMC potentially in list, matching to ATLANTA VA HEALTH MEDICAL CENTER
---
OCHSNER MEDICAL CENTER - HANCOCK LLC potentially in list, matching to HANCOCK MEDICAL CENTER
---
Potential missing: CHARLESTON AREA MEDICAL CENTER INC
---
ST. CHARLES HEALTH SYSTEM, INC. potentially in list, matching to ST CHARLES MEDICAL CENTER  BEND
---
SAINT FRANCIS MEDICAL CENTER potentially in list, matching to SAINT FRANCIS MEDICAL CENTER
---
Potential missing: SOUTHWEST HEALTH SYSTEM, INC.
---
AURORA HEALTH CARE METRO, INC. potentially in list, matching to SELECT SPEC HOSPITAL LUKES CAMPUS
AURORA HEALTH CARE METRO, INC. potentially in list, 

RHSC EL PASO, INC. potentially in list, matching to KINDRED HOSPITAL EL PASO
---
BETHESDA REHABILITATION HOSPITAL, INC. potentially in list, matching to APOLLO BEHAVIORAL HEALTH HOSPITAL
---
ST. MICHAEL'S HOSPITAL, INC. potentially in list, matching to SAINT MICHAELS HOSPITAL
---
Potential missing: ADMINISTRACION DE SERVICIOS DE SALUD MENTAL Y CONTRA LA ADICCION
---
TENET HEALTHSYSTEM GRADUATE, LLC potentially in list, matching to GEISINGER COMMUNITY MEDICAL CENTER
TENET HEALTHSYSTEM GRADUATE, LLC potentially in list, matching to GOOD SHEPHERD PENN PARTNERS SPECIALTY HOSPITAL AT RITTENHOUSE
---
Potential missing: ADVENTIST HEALTH SYSTEM-SUNBELT INC
---
Potential missing: TENET HEALTH SYSTEM HAHNEMANN, LLC
---
Potential missing: FRYE REGIONAL MEDICAL CENTER, INC.
---
Potential missing: TH HEALTHCARE, LTD.
---
GOOD SAMARITAN MEDICAL CENTER, INC. potentially in list, matching to GOOD SAMARITAN MEDICAL CENTER
---
FMC HOSPITAL, LTD. potentially in list, matching to NORTH SHORE MEDICAL CENTE

---
PHELPS MEMORIAL HEALTH CENTER potentially in list, matching to PHELPS MEMORIAL HEALTH CENTER
---
Potential missing: BON SECOURS HOSPITAL BALTIMORE INC
---
Potential missing: MERIDIAN HEALTH SERVICES CORP
---
Potential missing: HMIH CEDAR CREST, LLC
---
ASCENSION GENESYS HOSPITAL potentially in list, matching to GENESYS REGIONAL MEDICAL CENTER - HEALTH PARK
---
Potential missing: ALTERNATIVES IN TREATMENT, LLC
---
PRISMA HEALTH TUOMEY potentially in list, matching to PALMETTO HEALTH TUOMEY
---
Potential missing: SAINT FRANCIS MEDICAL CENTER
---
ST FRANCIS HOSPITAL INC potentially in list, matching to REGENCY HOSPITAL OF GREENVILLE
ST FRANCIS HOSPITAL INC potentially in list, matching to ST FRANCIS-DOWNTOWN
---
ST FRANCIS HOSPITAL, INC. potentially in list, matching to ST FRANCIS-EASTSIDE
---
UNIVERSITY OF TEXAS HEALTH SCIENCE CENTER AT TYLER potentially in list, matching to UNIVERSITY OF TEXAS HEALTH CENTER - TYLER
---
ST CLAIRE MEDIAL CENTER potentially in list, matching to ST. CLA

---
CHIPPEWA VALLEY HOSPITAL & OAKVIEW CARE CENTER, INC. potentially in list, matching to CHIPPEWA VALLEY HSPTL
---
Potential missing: STAMFORD HOSPITAL
---
LEHIGH VALLEY HOSPITAL potentially in list, matching to LEHIGH VALLEY HOSPITAL
---


In [264]:
UNMATCHED_COUNT

980

In [279]:
missing_gov.to_csv('missing_gov.csv', index=False)

In [275]:
CURRENT_STATUS

ID         NPI  \
841    22694914  1760424261   
836     9642104  1295789295   
4741  129744710  1760431530   
2817   60099702  1902867229   
1444   12402745  1164477055   
...         ...         ...   
2720    1003909  1376528398   
1966   10280759  1629074182   
2020   10485364  1194706655   
1091   10585364  1295709954   
2650   11849464  1275536344   

                                             Taxonomies  \
841                                      ['282E00000X']   
836                                      ['283X00000X']   
4741                                     ['207R00000X']   
2817         ['261QM1100X', '261QM1101X', '332000000X']   
1444                                     ['282E00000X']   
...                                                 ...   
2720  ['207PE0005X', '207Q00000X', '207RE0101X', '20...   
1966                                     ['282NC0060X']   
2020                                     ['282N00000X']   
1091                                     ['283X00000X']   
2650         ['282N00000X', '333600000X', '3336I0012X']   

                                               NAME_NPI  \
841   1125 SIR FRANCIS DRAKE BOULEVARD OPERATING COM...   
836            1300 CAMPBELL LANE OPERATING COMPANY LLC   
4741                             24 ON PHYSICIANS, P.C.   
2817                                354TH MEDICAL GROUP   
1444        4499 ACUSHNET AVENUE OPERATING COMPANY, LLC   
...                                                 ...   
2720                                      YORK HOSPITAL   
1966                             YUMA DISTRICT HOSPITAL   
2020                       YUMA REGIONAL MEDICAL CENTER   
1091               YUMA REHABILITATION HOSPITAL, L.L.C.   
2650                         ZEELAND COMMUNITY HOSPITAL   

                                             OTHER_NAME  \
841       KENTFIELD REHABILITATION & SPECIALTY HOSPITAL   
836           SOUTHERN KENTUCKY REHABILITATION HOSPITAL   
4741                                               None   
2817                                    EIELSON AFB MTF   
1444       VIBRA HOSPITAL OF SOUTHEASTERN MASSACHUSETTS   
...                                                 ...   
2720                                               None   
1966                                               None   
2020                                               None   
1091  YUMA REHABILITATION HOSPITAL, AN AFFILIATION O...   
2650         SPECTRUM HEALTH ZEELAND COMMUNITY HOSPITAL   

                   MAILING_ADDRESS_1 MAILING_ADDRESS_2 MAILING_CITY  \
841   5 EAST RIVER PARK PLACE E #460              None       FRESNO   
836   5 EAST RIVER PARK PLACE E #460              None       FRESNO   
4741                 P.O. BOX 403631              None      ATLANTA   
2817                2630 CENTRAL AVE        SUITE 1M07  EIELSON AFB   
1444            4499 ACUSHNET AVENUE              None  NEW BEDFORD   
...                              ...               ...          ...   
2720                  15 HOSPITAL DR              None         YORK   
1966                  1000 W 8TH AVE              None         YUMA   
2020                 2400 S AVENUE A              None         YUMA   
1091               9001 LIBERTY PKWY              None   BIRMINGHAM   
2650                   8333 FELCH ST              None      ZEELAND   

     MAILING_STATE MAIING_ZIP  ...                  VAL_DATE  \
841             CA  937201560  ...  2014-02-10T00:00:00.000Z   
836             CA  937201560  ...  2013-12-17T00:00:00.000Z   
4741            GA  303843631  ...  2015-03-12T00:00:00.000Z   
2817            AK  997022325  ...  2014-02-13T00:00:00.000Z   
1444            MA   27454707  ...  2016-08-01T00:00:00.000Z   
...            ...        ...  ...                       ...   
2720            ME  039091099  ...  2014-02-10T00:00:00.000Z   
1966            CO  807592641  ...  2014-03-12T00:00:00.000Z   
2020            AZ  853647127  ...  2014-03-12T00:00:00.000Z   
1091            AL  

In [277]:
GOV_HOSPITAL

X          Y  OBJECTID         ID  \
0     -83.387732  39.348667      3001   12645123   
1     -81.919907  40.565095      3002   17244654   
2     -82.450635  40.048302      3003    2543055   
3     -83.755531  40.369542      3004    5843311   
4     -82.224713  41.295065      3005    5544074   
...          ...        ...       ...        ...   
7576  -87.447485  36.636641      7577  181742223   
7577  -85.941438  37.900353      7578  181840121   
7578 -117.388804  33.221316      7579  181992055   
7579  144.736612  13.475210      7580  182096919   
7580  -77.093590  39.001287      7581  182120889   

                                              NAME  \
0                  ADENA GREENFIELD MEDICAL CENTER   
1                                POMERENE HOSPITAL   
2                        LICKING MEMORIAL HOSPITAL   
3                              MARY RUTAN HOSPITAL   
4                             MERCY ALLEN HOSPITAL   
...                                            ...   
7576           BLANCHFIELD ARMY COMMUNITY HOSPITAL   
7577               IRELAND ARMY COMMUNITY HOSPITAL   
7578                 NAVAL HOSPITAL CAMP PENDLETON   
7579                           NAVAL HOSPITAL GUAM   
7580  WALTER REED NATIONAL MILITARY MEDICAL CENTER   

                                ADDRESS           CITY STATE    ZIP  \
0                   550 MIRABEAU STREET     GREENFIELD    OH  45123   
1                      981 WOOSTER ROAD    MILLERSBURG    OH  44654   
2                 1320 WEST MAIN STREET         NEWARK    OH  43055   
3                     205 PALMER AVENUE  BELLEFONTAINE    OH  43311   
4                200 WEST LORAIN STREET        OBERLIN    OH  44074   
...                                 ...            ...   ...    ...   
7576                     650 JOEL DRIVE  FORT CAMPBELL    KY  42223   
7577                   289 IRELAND AVE.      FORT KNOX    KY  40121   
7578  200 MERCY CIRCLE , CAMP PENDLETON      OCEANSIDE    CA  92055   
7579            FARENHOLT AVE., BLDG 50  AGANA HEIGHTS    GU  96919   
7580                8901 ROCKVILLE PIKE       BETHESDA    MD  20889   

               ZIP4  ...                  VAL_DATE  \
0     NOT AVAILABLE  ...  2014-02-10T00:00:00.000Z   
1     NOT AVAILABLE  ...  2014-01-31T00:00:00.000Z   
2     NOT AVAILABLE  ...  2014-02-10T00:00:00.000Z   
3     NOT AVAILABLE  ...  2014-02-10T00:00:00.000Z   
4     NOT AVAILABLE  ...  2014-02-10T00:00:00.000Z   
...             ...  ...                       ...   
7576  NOT AVAILABLE  ...  2019-05-16T00:00:00.000Z   
7577  NOT AVAILABLE  ...  2019-05-16T00:00:00.000Z   
7578  NOT AVAILABLE  ...  2019-05-16T00:00:00.000Z   
7579  NOT AVAILABLE  ...  2019-05-09T00:00:00.000Z   
7580  NOT AVAILABLE  ...  2019-05-16T00:00:00.000Z   

                                                WEBSITE       STATE_ID  \
0     http://www.adena.org/locations/detail.dT/adena...           1200   
1                       http://www.pomerenehospital.org           1202   
2                               http://www.lmhealth.org           1213   
3                              http://www.maryrutan.org           1214   
4     http://www.mercyonline.org/mercy_allen_hospita...           1219   
...                                                 ...            ...   
7576                                      NOT AVAILABLE  NOT AVAILABLE   
7577                                      NOT AVAILABLE  NOT AVAILABLE   
7578                                      NOT AVAILABLE  NOT AVAILABLE   
7579                                      NOT AVAILABLE  NOT AVAILABLE   
7580  https://www.wrnmmc.capmed.mil/SitePages/home.aspx  NOT AVAILABLE   

                      ALT_NAME ST_FIPS                 OWNER TTL_STAFF  BEDS  \
0                NOT AVAILABLE      39            NON-PROFIT      -999    25   
1                NOT AVAILABLE      39    GOVERNMENT - LOCAL      -999    69   
2                NOT AVAILABLE      39            NON-PROFIT      -999   213   
3                NOT AVAILABLE

In [286]:
pd.merge(missing_gov, npi_with_taxes, left_on=['NAME','CITY','STATE'], right_on=['NAME','LOCATION_CITY','LOCATION_STATE']).sort_values('LAST_UPDATE_DATE').drop_duplicates('ID', keep='last')

X          Y  OBJECTID         ID  \
31  -82.484209  28.532936      1249   37734609   
22 -104.548494  45.887996      2184     659324   
38 -134.465153  58.329080      1718    1799801   
7   -84.556007  35.888605      3189   17237748   
42  -87.881899  41.125087       336    9360901   
29 -102.820550  46.889076      5108    6058601   
11  -73.944228  40.654842      3388  119111203   
21  -95.046092  45.120138      6824    2556201   
9   -87.821539  36.866340      3358   11342211   
33  -85.632088  31.451577      1303     836360   
26 -103.299035  48.906693      2221    3458730   
18  -77.921285  34.205464      4687    1128401   
20 -117.321814  34.131364      4764    8492411   
16  -73.937368  40.678233      3833   17111213   
44  -78.864887  42.899205      7081    3414263   
30  -90.884555  32.904739      5689    6439159   
39  -96.772446  39.079192      1725          8   
37  -93.436913  42.005062      1622   93450201   
28  -83.081022  43.332719      2886   13448453   
40  -97.774290  31.130906      1786          4   
41  -76.605256  40.968145       275    6017822   
17 -119.252134  34.277350      4658   51793003   
15 -115.167457  36.159624      3730    4089102   
25  -83.323384  35.484855      2216    2328719   
27  -96.647011  40.790183      2227  104868506   
13 -100.782338  46.807946      3528     458506   
0   -86.758542  37.927861      3027   10947586   

                                            NAME  \
31                          SPRINGBROOK HOSPITAL   
22          DAHL MEMORIAL HEALTHCARE ASSOCIATION   
38                    BARTLETT REGIONAL HOSPITAL   
7                           ROANE MEDICAL CENTER   
42                      RIVERSIDE MEDICAL CENTER   
29        ST JOSEPH'S HOSPITAL AND HEALTH CENTER   
11               UNIVERSITY HOSPITAL OF BROOKLYN   
21                        RICE MEMORIAL HOSPITAL   
9                     TRIGG COUNTY HOSPITAL INC.   
33                           DALE MEDICAL CENTER   
26                            ST LUKE'S HOSPITAL   
18           NEW HANOVER REGIONAL MEDICAL CENTER   
20          COMMUNITY HOSPITAL OF SAN BERNARDINO   
16                     INTERFAITH MEDICAL CENTER   
44                 ROSWELL PARK CANCER INSTITUTE   
30          SHARKEY-ISSAQUENA COMMUNITY HOSPITAL   
39                 IRWIN ARMY COMMUNITY HOSPITAL   
37                         STORY COUNTY HOSPITAL   
28                    MARLETTE REGIONAL HOSPITAL   
40           CARL R. DARNALL ARMY MEDICAL CENTER   
41                      GEISINGER MEDICAL CENTER   
17                 VENTURA COUNTY MEDICAL CENTER   
15  UNIVERSITY MEDICAL CENTER OF SOUTHERN NEVADA   
25            CHEROKEE INDIAN HOSPITAL AUTHORITY   
27               MADONNA REHABILITATION HOSPITAL   
13                              SANFORD BISMARCK   
0                 PERRY COUNTY MEMORIAL HOSPITAL   

                                ADDRESS            CITY STATE    ZIP  \
31                        7007 GROVE RD     BROOKSVILLE    FL  34609   
22                     215 SANDY STREET         EKALAKA    MT  59324   
38                  3260 HOSPITAL DRIVE          JUNEAU    AK  99801   
7       8045 ROANE MEDICAL CENTER DRIVE        HARRIMAN    TN  37748   
42                        350 N WALL ST        KANKAKEE    IL  60901   
29                  2500 FAIRWAY STREET       DICKINSON    ND  58601   
11                       445 LENOX ROAD        BROOKLYN    NY  11203   
21          301 BECKER AVENUE SOUTHWEST         WILLMAR    MN  56201   
9                       254 MAIN STREET           CADIZ    KY  42211   
33                  126 HOSPITAL AVENUE           OZARK    AL  36360   
26                        702 1ST ST SW          CROSBY    ND  58730   
18  2228 S. 17TH STREET/FISCAL SERVICES      WILMINGTON    NC  28401   
20            1805 MEDICAL CENTER DRIVE  SAN BERNARDINO    CA  92411   
16                    1545 ATLANTIC AVE        BROOKLYN    NY  11213   
44                          666 ELM STR         BUFFALO    NY  14263   
30 

In [283]:
npi_with_taxes.LAST_UPDATE_DATE=pd.to_datetime(npi_with_taxes.LAST_UPDATE_DATE)

In [302]:
MOAR = pd.merge(missing_gov, npi_with_taxes, left_on=['ADDRESS','STATE'], right_on=['LOCATION_ADDRESS_1', 'LOCATION_STATE']).sort_values('LAST_UPDATE_DATE')[['ID','NPI']]

In [303]:
MOARR = pd.merge(missing_gov, npi_with_taxes, left_on=['NAME','CITY','STATE'], right_on=['OTHER_NAME','LOCATION_CITY','LOCATION_STATE']).sort_values('LAST_UPDATE_DATE').drop_duplicates('ID', keep='last')[['ID','NPI']]

In [304]:
MOARRR = pd.merge(missing_gov, npi_with_taxes, left_on=['NAME','ADDRESS'], right_on=['OTHER_NAME','LOCATION_ADDRESS_1']).sort_values('LAST_UPDATE_DATE').drop_duplicates('ID', keep='last')[['ID','NPI']]

In [305]:
MOARRRR = pd.merge(missing_gov, npi_with_taxes, left_on=['NAME','ADDRESS'], right_on=['NAME','LOCATION_ADDRESS_1']).sort_values('LAST_UPDATE_DATE').drop_duplicates('ID', keep='last')[['ID','NPI']]

In [309]:
moar = pd.concat([MOAR,MOARR,MOARRR,MOARRRR])

In [308]:
CURRENT_STATUS

ID         NPI  \
841    22694914  1760424261   
836     9642104  1295789295   
4741  129744710  1760431530   
2817   60099702  1902867229   
1444   12402745  1164477055   
...         ...         ...   
2720    1003909  1376528398   
1966   10280759  1629074182   
2020   10485364  1194706655   
1091   10585364  1295709954   
2650   11849464  1275536344   

                                             Taxonomies  \
841                                      ['282E00000X']   
836                                      ['283X00000X']   
4741                                     ['207R00000X']   
2817         ['261QM1100X', '261QM1101X', '332000000X']   
1444                                     ['282E00000X']   
...                                                 ...   
2720  ['207PE0005X', '207Q00000X', '207RE0101X', '20...   
1966                                     ['282NC0060X']   
2020                                     ['282N00000X']   
1091                                     ['283X00000X']   
2650         ['282N00000X', '333600000X', '3336I0012X']   

                                               NAME_NPI  \
841   1125 SIR FRANCIS DRAKE BOULEVARD OPERATING COM...   
836            1300 CAMPBELL LANE OPERATING COMPANY LLC   
4741                             24 ON PHYSICIANS, P.C.   
2817                                354TH MEDICAL GROUP   
1444        4499 ACUSHNET AVENUE OPERATING COMPANY, LLC   
...                                                 ...   
2720                                      YORK HOSPITAL   
1966                             YUMA DISTRICT HOSPITAL   
2020                       YUMA REGIONAL MEDICAL CENTER   
1091               YUMA REHABILITATION HOSPITAL, L.L.C.   
2650                         ZEELAND COMMUNITY HOSPITAL   

                                             OTHER_NAME  \
841       KENTFIELD REHABILITATION & SPECIALTY HOSPITAL   
836           SOUTHERN KENTUCKY REHABILITATION HOSPITAL   
4741                                               None   
2817                                    EIELSON AFB MTF   
1444       VIBRA HOSPITAL OF SOUTHEASTERN MASSACHUSETTS   
...                                                 ...   
2720                                               None   
1966                                               None   
2020                                               None   
1091  YUMA REHABILITATION HOSPITAL, AN AFFILIATION O...   
2650         SPECTRUM HEALTH ZEELAND COMMUNITY HOSPITAL   

                   MAILING_ADDRESS_1 MAILING_ADDRESS_2 MAILING_CITY  \
841   5 EAST RIVER PARK PLACE E #460              None       FRESNO   
836   5 EAST RIVER PARK PLACE E #460              None       FRESNO   
4741                 P.O. BOX 403631              None      ATLANTA   
2817                2630 CENTRAL AVE        SUITE 1M07  EIELSON AFB   
1444            4499 ACUSHNET AVENUE              None  NEW BEDFORD   
...                              ...               ...          ...   
2720                  15 HOSPITAL DR              None         YORK   
1966                  1000 W 8TH AVE              None         YUMA   
2020                 2400 S AVENUE A              None         YUMA   
1091               9001 LIBERTY PKWY              None   BIRMINGHAM   
2650                   8333 FELCH ST              None      ZEELAND   

     MAILING_STATE MAIING_ZIP  ...                  VAL_DATE  \
841             CA  937201560  ...  2014-02-10T00:00:00.000Z   
836             CA  937201560  ...  2013-12-17T00:00:00.000Z   
4741            GA  303843631  ...  2015-03-12T00:00:00.000Z   
2817            AK  997022325  ...  2014-02-13T00:00:00.000Z   
1444            MA   27454707  ...  2016-08-01T00:00:00.000Z   
...            ...        ...  ...                       ...   
2720            ME  039091099  ...  2014-02-10T00:00:00.000Z   
1966            CO  807592641  ...  2014-03-12T00:00:00.000Z   
2020            AZ  853647127  ...  2014-03-12T00:00:00.000Z   
1091            AL  

In [310]:
moar = pd.merge(moar, npi_with_taxes, on='NPI')
CURRENT_STATUS_2 = pd.merge(moar, GOV_HOSPITAL, on='ID', suffixes = ['_NPI','_GOV']).sort_values('NAME_NPI')

In [340]:
GO_TIME = pd.concat([CURRENT_STATUS, CURRENT_STATUS_2])

In [327]:
miss_npi = list(missing_npi['NAME'])
good_words = ['CENTER','HOSPITAL','SYSTEM','UNIVERSITY','HEALTH','VAMC','MERCY','MEDIC']

In [332]:
new_npis = []
count =0
for row in missing_npi.itertuples():
    keep = False
    for word in good_words:
        if word in row.NAME:
            keep=True
    if keep ==True:
        print(row.NAME)
        count +=1 
        new_npis.append(row.NPI)
print(count)

CHILDREN'S HOSPITAL BOSTON
SAINT VINCENT CATHOLIC MEDICAL CENTER
V A MEDICAL CENTER - WILMINGTON, DELAWARE
MINNEAPOLIS V A MEDICAL CENTER
V.A. MED CENTER
V.A.N.J.HEALTHCARE SYSTEM
VA CARRIBEAN HEALTHCARE SYSTEM
CHILDREN'S HOSPITAL OF WISCONSIN
USA MEDDAC, EVANS ARMY COMMUNIT Y HOSPITAL
USA MEDICAL CENTER
CHILDRENS HOSPITAL AND REGIONAL MEDICAL CENTER
CHILDREN'S MEMOMRIAL HOSPITAL
VA HOSPITAL
MONROE HOSPITAL, LLC
MONSOUR MEDICAL CENTER
VA MEDICAL CENTER
VA MEDICAL CENTER
VA MEDICAL CENTER
VA MEDICAL CENTER
HAMPSHIRE MEMORIAL HOSPITAL, INC
CENTRAL ARKANSAS VETERANS HEALTH CARE SYSTEM
VA MEDICAL CENTER
CENTRAL TEXAS VETERAN'S HEALTH CARE SYSTEM
VA HEALTH CARE SYSTEM, SALT LAKE CITY, UT
VA HOSPITAL
VA HOSPITAL
VA HOSPITAL
CHARLESTON VAMC
VA HOSPITAL
VA HOSPITAL SAN DIEGO
CHARLESTON AREA MEDICAL CENTER
VA LOMA LINDA HEALTH CARE SYSTEM (112G)
VA LONG BEACH HEALTHCARE SYSTEM
VA LONG BEACH HEALTHCARE SYSTEM
ST JAMES HOSPITAL AND HEALTH CENTER
VA MARYLAND HEALTH CARE SYSTEM
UNIVERSITY OF CHICAG

ABRAHAM LINCOLN MEMORIAL HOSPITAL
BETH ISRAEL HOSPITAL ASSOCIATION
BETH ISRAEL DEACONESS MEDICAL CENTER
YALE-NEW HAVEN HOSPITAL
YALE UNIVERSITY SCHOOL OF MEDICINE
ABINGTON MEMORIAL HOSPITAL
HOSPITAL ESPANOL DE AUXILIO MUTUO DE PUERTO RICO, INC.
BERNICE COMMUNITY REHAB HOSPITAL
HOSPITAL ESPANOL AUXILIO MUTUO DE PUERTO RICO, INC.
WRIGHT PATTERSON MEDICAL CENTER
PINNACLE HEALTH HOSPITALS
PEDIATRIX MEDICAL GROUP
PEDIATRIX MEDICAL GROUP
PEDIATRIX MEDICAL GROUP
PEDIATRIX MEDICAL GROUP
BAYSTATE MEDICAL SURGICAL INC
BIG SPRING VAMC
PENINSULA HOSPITAL CENTER
PEDIATRIX MEDICAL GROUP OF CALIFORNIA
18TH MEDICAL GROUP
HOLY INFANT HOSPITAL
MEADOWCREST HOSPITAL, LLC
CHILDREN'S HOSPITAL MEDICAL CENTER OF AKRON
TENET MID-CITY MEDICAL, LLC
CHILDREN'S HOSPITAL OF PHILADELPHIA
ST BERNARDS HOSPITAL INC
SAVOY MEDICAL CENTER
NORTHLAKE MEDICAL CENTER, LLC
DASSEE COMMUNITY HEALTH SYSTEMS
MISSION HOSPITAL, INC
DASSEE COMMUNITY HEALTH SYSTEMS
SAINT JOSEPH MERCY SALINE HOSPITAL
DARDANELLE HOSPITAL YELL COUNTY
MER

RIVER PARISHES HOSPITAL LLC
NORTHWEST TEXAS SURGICAL HOSPITAL, LLC
HODGEMAN COUNTY HEALTH CENTER
FRANK T RUTHERFORD MEMORIAL HOSPITAL, INC
ANNE ARUNDEL MEDICAL CENTER, INC
HOSPITAL SERVICE DISTRICT NO. 2
LAKESIDE MEMORIAL HOSPITAL INC.
ST FRANCIS HOSPITAL, INC
MEMORIAL HOSPITAL
HOSPITAL DISTRICT NO 1 MARION CO
CONCHO COUNTY HOSPITAL
CAPE COD HEALTHCARE INC
CHARLESTON HOSPITAL, INC.
SINAI HOSPITAL OF BALTIMORE INC
NORTHERN ARIZONA VETERANS HEALTH CARE SYSTEM
CONTINUOUS CARE CENTER OF BARTLESVILLE INC
CLEVELAND COUNTY HEALTHCARE SYSTEM
ST. JOSEPH REGIONAL HEALTH NETWORK
ST. JOSEPH REGIONAL HEALTH NETWORK
COMMONWEALTH OF VIRGINIA WESTERN STATE HOSPITAL
COMMONWEALTH OF VIRGINIA WESTERN STATE HOSPITAL
OTTUMWA REGIONAL HEALTH CENTER INC
MERIDIAN HOSPITALS CORPORATION
MERIDIAN HOSPITALS CORPORATION
MERIDIAN HOSPITALS CORPORATION
CAMDEN COUNTY HEALTH SERVICES CENTER
ST JOHNS REGIONAL MEDICAL CENTER
HARPER COUNTY COM. HOSPITAL
ST. THERESA SPECIALTY HOSPITAL, LLC
NOR-LEA HOSPITAL DISTRICT
MT. SI

UMASS MEMORIAL MEDICAL CENTER, INC.
NASSAU HEALTHCARE CORPORATION
CARILION MEDICAL CENTER
INTERMEDICAL HOSPITAL OF SOUTH CAROLINA INC
PIPESTONE COUNTY MEDICAL CENTER
MEMORIAL HOSPITAL FOR CANCER & ALLIED DISEASES
PINCKNEYVILLE COMMUNITY HOSPITAL
UNIVERSITY OF NORTH CAROLINA HEALTH CARE SYSTEM
FIRELANDS REGIONAL MEDICAL CENTER
IHC HEALTH SERVICES INC.
PASADERA BEHAVIORAL HEALTH NETWORK, INC.
ST. LUKE'S HOSPITAL OF DULUTH
MENA HOSPITAL COMMISSION
THE REGIONAL HEALTH SYSTEM OF ACADIANA, LLC
TRANSYLVANIA COMMUNITY HOSPITAL, INC
ANN & ROBERT H LURIE CHILDRENS HOSPITAL OF CHICAGO
ST. LUKE'S HOSPITAL OF DULUTH
JOHNS HOPKINS BAYVIEW MEDICAL CENTER, INC.
MCNAIRY HOSPITAL CORPORATION
RED BUD ILLINOIS HOSPITAL COMPANY LLC
LOYOLA UNIVERSITY MEDICAL CENTER
10TH MEDICAL GROUP
CAMDEN GENERAL HOSPITAL, INC.
ST. BARNABAS HOSPITAL
IHC HEALTH SERVICES INC.
NORTHSHORE REGIONAL MEDICAL CENTER, LLC
ROSEBUD INDIAN HEALTH SERVICE
YAVAPAI COMMUNITY HOSPITAL ASSOCIATION
COFFEE COUNTY HOSPITAL GROUP, INC
ST. DAV

In [336]:
test = npi_with_taxes[npi_with_taxes.NPI.isin(new_npis)]

In [378]:
test = test.rename(columns = {'NAME':'NAME_NPI'})

In [379]:
xtra_plus = pd.concat([test, GO_TIME])

C:\Users\vigrose\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.


In [342]:
GO_TIME

ID         NPI  \
841    22694914  1760424261   
836     9642104  1295789295   
4741  129744710  1760431530   
2817   60099702  1902867229   
1444   12402745  1164477055   
...         ...         ...   
57     10214215  1528076155   
190     2282701  1518050947   
123    58575218  1629189733   
51      7035565  1558383554   
146     7314120  1124075908   

                                             Taxonomies  \
841                                      ['282E00000X']   
836                                      ['283X00000X']   
4741                                     ['207R00000X']   
2817         ['261QM1100X', '261QM1101X', '332000000X']   
1444                                     ['282E00000X']   
...                                                 ...   
57                                       ['282N00000X']   
190   ['333600000X', '3336I0012X', '3336L0003X', '33...   
123                                      ['207L00000X']   
51           ['207P00000X', '363AM0700X', '363L00000X']   
146                                      ['207R00000X']   

                                               NAME_NPI  \
841   1125 SIR FRANCIS DRAKE BOULEVARD OPERATING COM...   
836            1300 CAMPBELL LANE OPERATING COMPANY LLC   
4741                             24 ON PHYSICIANS, P.C.   
2817                                354TH MEDICAL GROUP   
1444        4499 ACUSHNET AVENUE OPERATING COMPANY, LLC   
...                                                 ...   
57                                               VHAWNY   
190                     WESTON COUNTY HOSPITAL DISTRICT   
123                WHITEROCK ANESTHESIA CONSULTANTS, PA   
51                          WINSTON EMERGENCY GROUP LLC   
146                          WNY INTERNAL MEDICINE P.C.   

                                         OTHER_NAME  \
841   KENTFIELD REHABILITATION & SPECIALTY HOSPITAL   
836       SOUTHERN KENTUCKY REHABILITATION HOSPITAL   
4741                                           None   
2817                                EIELSON AFB MTF   
1444   VIBRA HOSPITAL OF SOUTHEASTERN MASSACHUSETTS   
...                                             ...   
57                                             None   
190          WESTON COUNTY HEALTH SERVICES PHARMACY   
123                                            None   
51                                             None   
146                       WNY PRIMARY CARE MEDICINE   

                   MAILING_ADDRESS_1 MAILING_ADDRESS_2     MAILING_CITY  \
841   5 EAST RIVER PARK PLACE E #460              None           FRESNO   
836   5 EAST RIVER PARK PLACE E #460              None           FRESNO   
4741                 P.O. BOX 403631              None          ATLANTA   
2817                2630 CENTRAL AVE        SUITE 1M07      EIELSON AFB   
1444            4499 ACUSHNET AVENUE              None      NEW BEDFORD   
...                              ...               ...              ...   
57                 314 WOOD ACRES DR              None     EAST AMHERST   
190             1124 WASHINGTON BLVD              None        NEWCASTLE   
123                    PO BOX 870638              None         MESQUITE   
51                200 CORPORATE BLVD         SUITE 201        LAFAYETTE   
146                   445 TREMONT ST              None  NORTH TONAWANDA   

     MAILING_STATE MAIING_ZIP  ...                  VAL_DATE  \
841             CA  937201560  ...  2014-02-10T00:00:00.000Z   
836             CA  937201560  ...  2013-12-17T00:00:00.000Z   
4741            GA  303843631  ...  2015-03-12T00:00:00.000Z   
2817            AK  997022325  ...  2014-02-13T00:00:00.000Z   
1444            MA   27454707  ...  2016-08-01T00:00:00.000Z   
...            ...        ...  ...                       ...   
57              NY  140511654  ...  2015-05-22T00:00:00.000Z   
190             WY  827012972  ...  2013-12-05T00:00:00.000Z   
123             TX  751870638  ...  2014-02-07T00:00:00.000Z   
51              LA  

In [343]:
test

NPI                    Taxonomies  \
319     1659389518                ['286500000X']   
726     1245248939                ['282N00000X']   
879     1083622120                ['282N00000X']   
880     1417965559                ['282N00000X']   
882     1871501916                ['282N00000X']   
...            ...                           ...   
240609  1245248624                ['282NR1301X']   
240880  1598773079                ['282NC2000X']   
240908  1528075108                ['282N00000X']   
240990  1619985942  ['261QE0002X', '282N00000X']   
241401  1992713564  ['3336I0012X', '282E00000X']   

                                                  NAME  \
319                         SYRACUSE VA MEDICAL CENTER   
726                               MOUNT SINAI HOSPITAL   
879             PRIME HEALTHCARE HUNTINGTON BEACH, LLC   
880                     PRIME HEALTHCARE LA PALMA, LLC   
882                      PRIME HEALTHCARE ANAHEIM, LLC   
...                                                ...   
240609                  HOSPITAL AUTHORITY OF BEN HILL   
240880                     ARKANSAS CHILDRENS HOSPITAL   
240908                               FRANKLIN HOSPITAL   
240990            CATHOLIC HEALTH INITIATIVES COLORADO   
241401  NEW YORK CITY HEALTH AND HOSPITALS CORPORATION   

                                OTHER_NAME              MAILING_ADDRESS_1  \
319                                   None                123 W CAYUGA ST   
726                  MOUNT SINAI OF QUEENS  1 GUSTAVE L LEVY PL, BOX 6000   
879                                   None               3300 E GUASTI RD   
880       LA PALMA INTERCOMMUNITY HOSPITAL            3300 E. GUASTI ROAD   
882            WEST ANAHEIM MEDICAL CENTER               3300 E GUASTI RD   
...                                    ...                            ...   
240609              DORMINY MEDICAL CENTER             200 PERRY HOUSE RD   
240880        ACH PHYSICIANS BILLING GROUP                    PO BOX 8088   
240908                                None            972 BRUSH HOLLOW RD   
240990                                None                  PO BOX 910126   
241401  HENRY J. CARTER SPECIALTY HOSPITAL                   160 WATER ST   

                               MAILING_ADDRESS_2 MAILING_CITY MAILING_STATE  \
319                                         None       OSWEGO            NY   
726                                         None     NEW YORK            NY   
879                                    3RD FLOOR      ONTARIO            CA   
880                                         None      ONTARIO            CA   
882                                    3RD FLOOR      ONTARIO            CA   
...                                          ...          ...           ...   
240609                               PO BOX 1447   FITZGERALD            GA   
240880                                      None  LITTLE ROCK            AR   
240908  5TH FLOOR FINANCE ATTN: WILLIAM J. FUCHS     WESTBURY            NY   
240990                                      None       DENVER            CO   
241401                                  ROOM 736     NEW YORK            NY   

       MAIING_ZIP MAILING_PHONE  LOCATION_ADDRESS_1 LOCATION_ADDRESS_2  \
319     131261449    3153425369      800 IRVING AVE               None   
726     100296500    2122562904       2510 30TH AVE               None   
879     917618655    9092354400    17772 BEACH BLVD               None   
880     917618654    9092354400  7901 WALKER STREET               None   
882     917618655    9092354400   3033 W ORANGE AVE               None   
...           ...           ...                 ...                ...   
240609  317508857    2294247100  200 PERRY HOUSE RD               None   
240880  722038088          None     800 MARSHALL ST               None   
240908  115901740    5168766000    900 FRANKLIN AVE               None   
240990  802910126    3037656008  14300 ORCHARD PKWY               None   
24140

In [350]:
MO = pd.merge(missing_gov, npi_with_taxes, left_on=['ALT_NAME','ADDRESS'], right_on=['OTHER_NAME','LOCATION_ADDRESS_1']).sort_values('LAST_UPDATE_DATE').drop_duplicates('ID', keep='last')[['ID','NPI']]

In [351]:
MOO = pd.merge(missing_gov, npi_with_taxes, left_on=['ALT_NAME','ADDRESS'], right_on=['NAME','LOCATION_ADDRESS_1']).sort_values('LAST_UPDATE_DATE').drop_duplicates('ID', keep='last')[['ID','NPI']]

In [352]:
MOOO = pd.merge(missing_gov, npi_with_taxes, left_on=['ALT_NAME','CITY','STATE'], right_on=['OTHER_NAME','LOCATION_CITY','LOCATION_STATE']).sort_values('LAST_UPDATE_DATE').drop_duplicates('ID', keep='last')[['ID','NPI']]

In [353]:
MOOOO = pd.merge(missing_gov, npi_with_taxes, left_on=['ALT_NAME','CITY','STATE'], right_on=['NAME','LOCATION_CITY','LOCATION_STATE']).sort_values('LAST_UPDATE_DATE').drop_duplicates('ID', keep='last')[['ID','NPI']]

In [356]:
MM = pd.concat([MO,MOO,MOOO,MOOOO])

In [357]:
moo = pd.merge(MM, npi_with_taxes, on='NPI')
moom = pd.merge(moo, GOV_HOSPITAL, on='ID', suffixes = ['_NPI','_GOV']).sort_values('NAME_NPI')

In [360]:
pd.concat([xtra_plus,moom]).to_csv('XTRA_STATUS.csv',index =False)

C:\Users\vigrose\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.


In [415]:
finality

ADDRESS  \
319                                    NaN   
726                                    NaN   
879                                    NaN   
880                                    NaN   
882                                    NaN   
..                                     ...   
3                        1901 S. UNION AVE   
16   STATE ROUTE 264 SOUTH 191, PO BOX 457   
12                       301 YADKIN STREET   
6                         9440 POPPY DRIVE   
13                   15248 ELEVENTH STREET   

                                ALT_NAME   BEDS         CITY COUNTRY  \
319                                  NaN    NaN          NaN     NaN   
726                                  NaN    NaN          NaN     NaN   
879                                  NaN    NaN          NaN     NaN   
880                                  NaN    NaN          NaN     NaN   
882                                  NaN    NaN          NaN     NaN   
..                                   ...    ...          ...     ...   
3               TACOMA GENERAL ALLENMORE  130.0       TACOMA     USA   
16              NAVAJO HEALTH FOUNDATION   25.0       GANADO     USA   
12        STANLY REGIONAL MEDICAL CENTER  109.0    ALBEMARLE     USA   
6    DOCTORS HOSPITAL AT WHITE ROCK LAKE  218.0       DALLAS     USA   
13      VICTOR VALLEY COMMUNITY HOSPITAL  101.0  VICTORVILLE     USA   

             COUNTY COUNTYFIPS HELIPAD          ID     LAST_UPDATE_DATE  ...  \
319             NaN        NaN     NaN         NaN  2007-07-08 00:00:00  ...   
726             NaN        NaN     NaN         NaN  2016-06-03 00:00:00  ...   
879             NaN        NaN     NaN         NaN  2013-12-17 00:00:00  ...   
880             NaN        NaN     NaN         NaN  2014-12-23 00:00:00  ...   
882             NaN        NaN     NaN         NaN  2014-02-25 00:00:00  ...   
..              ...        ...     ...         ...                  ...  ...   
3            PIERCE      53053       N  11798411.0  2008-04-17 00:00:00  ...   
16           APACHE       4001       N  69386505.0  2019-12-05 00:00:00  ...   
12           STANLY      37167       Y  10428002.0  2008-02-13 00:00:00  ...   
6            DALLAS      48113       N  58575218.0  2016-04-28 00:00:00  ...   
13   SAN BERNARDINO       6071       Y  52192392.0  2008-04-20 00:00:00  ...   

     TTL_STAFF                TYPE      Taxonomies                  VAL_DATE  \
319        NaN                 NaN  ['286500000X']                       NaN   
726        NaN                 NaN  ['282N00000X']                       NaN   
879        NaN                 NaN  ['282N00000X']                       NaN   
880        NaN                 NaN  ['282N00000X']                       NaN   
882        NaN                 NaN  ['282N00000X']                       NaN   
..         ...                 ...             ...                       ...   
3       -999.0  GENERAL ACUTE CARE  ['282N00000X']  2014-02-10T00:00:00.000Z   
16      -999.0     CRITICAL ACCESS  ['261QC0050X']  2015-01-12T00:00:00.000Z   
12      -999.0  GENERAL ACUTE CARE  ['273Y00000X']  2014-02-10T00:00:00.000Z   
6       -999.0  GENERAL ACUTE CARE  ['282N00000X']  2014-02-07T00:00:00.000Z   
13      -999.0  GENERAL ACUTE CARE  ['282N00000X']  2014-02-10T00:00:00.000Z   

        VAL_METHOD                                            WEBSITE  \
319            NaN                                                NaN   
726            NaN                                                NaN   
879            NaN                                                NaN   
880            NaN                                                NaN   
882            NaN                                                NaN   
..             ...                                                ...   
3          IMAGERY                http://www.multicare.org/allenmore/   
16   IMAGERY/OTHER                            http://sagememorial.org   
12         IMAGERY                    

In [410]:
finality = pd.concat([xtra_plus,moom])

C:\Users\vigrose\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.


In [411]:
FINALITY = finality.sort_values(['LOCATION_CITY','LOCATION_STATE'])

In [398]:
FINALITY.sort_values('NAME_GOV').dtypes

ADDRESS                object
ALT_NAME               object
BEDS                  float64
CITY                   object
COUNTRY                object
COUNTY                 object
COUNTYFIPS             object
HELIPAD                object
ID                    float64
LAST_UPDATE_DATE       object
LATITUDE              float64
LOCATION_ADDRESS_1     object
LOCATION_ADDRESS_2     object
LOCATION_CITY          object
LOCATION_PHONE         object
LOCATION_STATE         object
LOCATION_ZIP           object
LONGITUDE             float64
MAIING_ZIP             object
MAILING_ADDRESS_1      object
MAILING_ADDRESS_2      object
MAILING_CITY           object
MAILING_PHONE          object
MAILING_STATE          object
NAICS_CODE            float64
NAICS_DESC             object
NAME                   object
NAME_GOV               object
NAME_NPI               object
NPI                     int64
OBJECTID              float64
OTHER_NAME             object
OWNER                  object
POPULATION

In [405]:
FINALITY_2 = FINALITY.sort_values('NAME_GOV').drop_duplicates('NPI', keep='first')
FINALITY_2 = FINALITY_2.sort_values(['LOCATION_ADDRESS_1','LOCATION_CITY','LOCATION_STATE'])

In [412]:
FINALITY_2 = FINALITY_2.fillna('None')

In [409]:
matches_list = []
count += 1
name = ''
city = ''
state = ''
address = ''
list_npi =[]

for row in FINALITY_2.itertuples():
    match = False
    if row.NAME_GOV == 'None':
        if state == row.LOCATION_STATE:
            if city == row.LOCATION_CITY:
                add_match = match_address(row.LOCATION_ADDRESS_1, address)
                if add_match ==True or add_match == 'Maybe':
                    print(f'{row.NAME_NPI} / {row.OTHER_NAME} matches {name}')
                    print(f'{row.LOCATION_ADDRESS_1} matches {address}')
                    match = True
                    print('')
                    matches_list.append(name)

    if match ==False:
        name = row.NAME_NPI
        city = row.LOCATION_CITY
        state = row.LOCATION_STATE
        address = row.LOCATION_ADDRESS_1
        list_npi.append(row.NPI)
    
    matches_count = len(matches_list)

1 total hospitals
2 total hospitals
3 total hospitals
4 total hospitals
5 total hospitals
6 total hospitals
7 total hospitals
8 total hospitals
9 total hospitals
10 total hospitals
11 total hospitals
12 total hospitals
13 total hospitals
14 total hospitals
15 total hospitals
16 total hospitals
17 total hospitals
18 total hospitals
19 total hospitals
20 total hospitals
21 total hospitals
22 total hospitals
23 total hospitals
24 total hospitals
25 total hospitals
26 total hospitals
27 total hospitals
28 total hospitals
29 total hospitals
30 total hospitals
31 total hospitals
32 total hospitals
KINDRED HOSPITAL / None matches HORIZONS WOMEN'S HEALTHCARE, LLC
1 ELIZABETH PL matches 1 ELIZABETH PL

32 total hospitals
MEDICAL CENTER AT ELIZABETH PLACE LLC / None matches HORIZONS WOMEN'S HEALTHCARE, LLC
1 ELIZABETH PLACE matches 1 ELIZABETH PL

32 total hospitals
33 total hospitals
34 total hospitals
35 total hospitals
36 total hospitals
37 total hospitals
38 total hospitals
39 total hospital

390 total hospitals
391 total hospitals
392 total hospitals
393 total hospitals
394 total hospitals
395 total hospitals
396 total hospitals
397 total hospitals
398 total hospitals
399 total hospitals
400 total hospitals
401 total hospitals
402 total hospitals
403 total hospitals
404 total hospitals
405 total hospitals
406 total hospitals
407 total hospitals
408 total hospitals
409 total hospitals
410 total hospitals
411 total hospitals
412 total hospitals
413 total hospitals
414 total hospitals
415 total hospitals
416 total hospitals
417 total hospitals
418 total hospitals
419 total hospitals
420 total hospitals
421 total hospitals
422 total hospitals
423 total hospitals
424 total hospitals
425 total hospitals
426 total hospitals
427 total hospitals
428 total hospitals
429 total hospitals
430 total hospitals
431 total hospitals
432 total hospitals
RENOWN SOUTH MEADOWS MEDICAL CENTER / None matches LIFECARE HOSPITALS OF NORTHERN NEVADA, INC
10101 DOUBLE R BLVD matches 10101 DOUBLE R BLV

776 total hospitals
777 total hospitals
778 total hospitals
779 total hospitals
780 total hospitals
781 total hospitals
782 total hospitals
783 total hospitals
784 total hospitals
785 total hospitals
786 total hospitals
787 total hospitals
788 total hospitals
789 total hospitals
790 total hospitals
791 total hospitals
792 total hospitals
793 total hospitals
794 total hospitals
795 total hospitals
796 total hospitals
797 total hospitals
798 total hospitals
799 total hospitals
800 total hospitals
801 total hospitals
802 total hospitals
803 total hospitals
804 total hospitals
805 total hospitals
806 total hospitals
807 total hospitals
808 total hospitals
809 total hospitals
810 total hospitals
811 total hospitals
812 total hospitals
813 total hospitals
814 total hospitals
815 total hospitals
816 total hospitals
817 total hospitals
818 total hospitals
819 total hospitals
820 total hospitals
821 total hospitals
822 total hospitals
823 total hospitals
824 total hospitals
825 total hospitals


1203 total hospitals
1204 total hospitals
1205 total hospitals
1206 total hospitals
1207 total hospitals
1208 total hospitals
1209 total hospitals
1210 total hospitals
1211 total hospitals
1212 total hospitals
1213 total hospitals
1214 total hospitals
1215 total hospitals
1216 total hospitals
1217 total hospitals
1218 total hospitals
1219 total hospitals
1220 total hospitals
1221 total hospitals
1222 total hospitals
1223 total hospitals
1224 total hospitals
1225 total hospitals
JAMES PETERS VETERAN MEDICAL CENTER / None matches BRONX VAMC
130 W KINGSBRIDGE RD matches 130 W KINGSBRIDGE RD

1225 total hospitals
1226 total hospitals
1227 total hospitals
1228 total hospitals
1229 total hospitals
1230 total hospitals
1231 total hospitals
1232 total hospitals
1233 total hospitals
1234 total hospitals
1235 total hospitals
1236 total hospitals
1237 total hospitals
1238 total hospitals
1239 total hospitals
1240 total hospitals
1241 total hospitals
1242 total hospitals
1243 total hospitals
1244 

1624 total hospitals
1625 total hospitals
1626 total hospitals
1627 total hospitals
1628 total hospitals
1629 total hospitals
1630 total hospitals
1631 total hospitals
1632 total hospitals
1633 total hospitals
1634 total hospitals
1635 total hospitals
1636 total hospitals
1637 total hospitals
1638 total hospitals
1639 total hospitals
1640 total hospitals
1641 total hospitals
1642 total hospitals
1643 total hospitals
1644 total hospitals
1645 total hospitals
1646 total hospitals
1647 total hospitals
1648 total hospitals
1649 total hospitals
1650 total hospitals
1651 total hospitals
1652 total hospitals
1653 total hospitals
1654 total hospitals
1655 total hospitals
SONNY MONTGOMERY V A M EDICAL CENTER / None matches JACKSON VAMC
1500 E WOODROW WILSON AVE matches 1500 E WOODROW WILSON AVE

1655 total hospitals
1656 total hospitals
1657 total hospitals
1658 total hospitals
1659 total hospitals
1660 total hospitals
1661 total hospitals
1662 total hospitals
1663 total hospitals
1664 total ho

...

5378 total hospitals
5379 total hospitals
5380 total hospitals
5381 total hospitals
5382 total hospitals
5383 total hospitals
5384 total hospitals
5385 total hospitals
5386 total hospitals
5387 total hospitals
5388 total hospitals
5389 total hospitals
5390 total hospitals
5391 total hospitals
5392 total hospitals
5393 total hospitals
5394 total hospitals
5395 total hospitals
5396 total hospitals
5397 total hospitals
5398 total hospitals
5399 total hospitals
MIDWEST DIVISION - MMC, LLC / MENORAH MEDICAL CENTER matches KC REHABILITATION HOSPITAL INC
5721 W 119TH ST matches 5701 W 110TH ST

5399 total hospitals
5400 total hospitals
5401 total hospitals
5402 total hospitals
5403 total hospitals
5404 total hospitals
5405 total hospitals
5406 total hospitals
5407 total hospitals
5408 total hospitals
5409 total hospitals
5410 total hospitals
5411 total hospitals
5412 total hospitals
5413 total hospitals
5414 total hospitals
5415 total hospitals
5416 total hospitals
5417 total hospitals
5418 t

5696 total hospitals
5697 total hospitals
5698 total hospitals
5699 total hospitals
5700 total hospitals
5701 total hospitals
5702 total hospitals
5703 total hospitals
5704 total hospitals
5705 total hospitals
5706 total hospitals
5707 total hospitals
5708 total hospitals
5709 total hospitals
5710 total hospitals
5711 total hospitals
5712 total hospitals
5713 total hospitals
5714 total hospitals
5715 total hospitals
5716 total hospitals
5717 total hospitals
5718 total hospitals
5719 total hospitals
5720 total hospitals
LANE REGIONAL MEDICAL CENTER / None matches HOSPITAL SERVICE DISTRICT 1 OF EAST BATON ROUGE PARISH
6300 MAIN STREET matches 6300 MAIN ST

5720 total hospitals
5721 total hospitals
5722 total hospitals
5723 total hospitals
5724 total hospitals
5725 total hospitals
5726 total hospitals
5727 total hospitals
5728 total hospitals
5729 total hospitals
5730 total hospitals
5731 total hospitals
5732 total hospitals
5733 total hospitals
5734 total hospitals
5735 total hospitals
5

6029 total hospitals
6030 total hospitals
6031 total hospitals
6032 total hospitals
6033 total hospitals
6034 total hospitals
6035 total hospitals
6036 total hospitals
6037 total hospitals
6038 total hospitals
6039 total hospitals
6040 total hospitals
6041 total hospitals
6042 total hospitals
6043 total hospitals
6044 total hospitals
6045 total hospitals
6046 total hospitals
6047 total hospitals
6048 total hospitals
6049 total hospitals
6050 total hospitals
6051 total hospitals
6052 total hospitals
6053 total hospitals
6054 total hospitals
6055 total hospitals
6056 total hospitals
6057 total hospitals
6058 total hospitals
6059 total hospitals
6060 total hospitals
6061 total hospitals
6062 total hospitals
6063 total hospitals
6064 total hospitals
6065 total hospitals
6066 total hospitals
6067 total hospitals
6068 total hospitals
6069 total hospitals
6070 total hospitals
6071 total hospitals
6072 total hospitals
6073 total hospitals
6074 total hospitals
6075 total hospitals
6076 total ho

6357 total hospitals
6358 total hospitals
6359 total hospitals
6360 total hospitals
6361 total hospitals
6362 total hospitals
6363 total hospitals
6364 total hospitals
6365 total hospitals
6366 total hospitals
6367 total hospitals
6368 total hospitals
6369 total hospitals
6370 total hospitals
6371 total hospitals
6372 total hospitals
6373 total hospitals
6374 total hospitals
6375 total hospitals
6376 total hospitals
6377 total hospitals
6378 total hospitals
6379 total hospitals
6380 total hospitals
6381 total hospitals
6382 total hospitals
6383 total hospitals
6384 total hospitals
6385 total hospitals
6386 total hospitals
6387 total hospitals
6388 total hospitals
6389 total hospitals
6390 total hospitals
6391 total hospitals
6392 total hospitals
6393 total hospitals
6394 total hospitals
6395 total hospitals
6396 total hospitals
6397 total hospitals
6398 total hospitals
6399 total hospitals
6400 total hospitals
6401 total hospitals
6402 total hospitals
6403 total hospitals
6404 total ho

6745 total hospitals
6746 total hospitals
6747 total hospitals
6748 total hospitals
6749 total hospitals
6750 total hospitals
6751 total hospitals
6752 total hospitals
6753 total hospitals
6754 total hospitals
6755 total hospitals
6756 total hospitals
6757 total hospitals
6758 total hospitals
6759 total hospitals
6760 total hospitals
6761 total hospitals
6762 total hospitals
6763 total hospitals
6764 total hospitals
6765 total hospitals
6766 total hospitals
6767 total hospitals
6768 total hospitals
6769 total hospitals
6770 total hospitals
6771 total hospitals
6772 total hospitals
6773 total hospitals
6774 total hospitals
6775 total hospitals
PROVIDENCE EVERETT MEDICAL CENTER / INPATIENT REHABILITATION FACILITY matches BETHANY OF THE NORTHWEST
916 PACIFIC AVENUE matches 916 PACIFIC AVENUE

6775 total hospitals
6776 total hospitals
6777 total hospitals
6778 total hospitals
6779 total hospitals
6780 total hospitals
6781 total hospitals
6782 total hospitals
6783 total hospitals
6784 total

In [408]:
FINALITY_2.to_csv('CURRENT_STATUS_FINAL.csv', index=False)

In [413]:
FINALITY_2

ADDRESS                             ALT_NAME  BEDS      CITY  \
444  1 HEALTHCARE DRIVE  BROADDUS HOSPITAL ASSOCIATION, INC.  72.0  PHILIPPI   

    COUNTRY   COUNTY COUNTYFIPS HELIPAD         ID LAST_UPDATE_DATE  ...  \
444     USA  BARBOUR      54001       N  5226416.0       2019-07-09  ...   

     TTL_STAFF             TYPE      Taxonomies                  VAL_DATE  \
444     -999.0  CRITICAL ACCESS  ['282NC0060X']  2019-04-16T00:00:00.000Z   

        VAL_METHOD                            WEBSITE          X          Y  \
444  IMAGERY/OTHER  http://www.davishealthsystem.org/ -80.061793  39.143249   

         ZIP           ZIP4  
444  26416.0  NOT AVAILABLE  

[1 rows x 51 columns]

In [417]:
finality.to_csv('Ye_Gads.csv', index=False)

In [69]:
T = pd.merge(UNMATCHED_STILL, npi_hospitals, left_on = ['NAME','CITY'], right_on=['NAME','LOCATION_CITY'])

In [49]:
UNMATCHED_STILL.TELEPHONE.replace('(','')

14      (712) 527-4811
24      (435) 722-2497
26      (812) 547-7011
28      (937) 534-4600
34      (812) 298-8888
             ...      
7481    (254) 519-8328
7521    (319) 244-5555
7527    (970) 887-5800
7556     NOT AVAILABLE
7578    (760) 725-4357
Name: TELEPHONE, Length: 369, dtype: object

In [68]:
U = pd.merge(UNMATCHED_STILL, npi_hospitals, left_on = ['ADDRESS'], right_on=['LOCATION_ADDRESS_1'])

In [67]:
V = pd.merge(UNMATCHED_STILL, npi_hospitals, left_on = ['NAME','STATE'], right_on=['NAME','LOCATION_STATE'])

In [66]:
W = pd.merge(UNMATCHED_STILL, npi_hospitals, left_on = ['NAME','STATE'], right_on=['OTHER_NAME','LOCATION_STATE'])

In [65]:
Z = pd.merge(UNMATCHED_STILL, npi_hospitals, left_on = ['ALT_NAME','STATE'], right_on=['NAME','LOCATION_STATE'])

In [64]:
Y = pd.merge(UNMATCHED_STILL, npi_hospitals, left_on = ['ALT_NAME','STATE'], right_on=['OTHER_NAME','LOCATION_STATE'])

In [58]:
nums= []
for num in list(UNMATCHED_STILL.TELEPHONE):
    new_phone = num.replace('(','').replace(')','').replace(' ','').replace('-','')
    nums.append(new_phone)

In [60]:
UNMATCHED_STILL['PHONE']=nums

C:\Users\vigrose\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [73]:
X = pd.merge(UNMATCHED_STILL, npi_hospitals, left_on = ['PHONE'], right_on=['LOCATION_PHONE'])

In [82]:
matchy  = pd.concat([T,U,V,W,X,Y,Z]).drop_duplicates('ID')

C:\Users\vigrose\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.


In [76]:
len(dict_list_4)

1417

In [77]:
len(dict_list_5)

6603

In [78]:
len(dict_list_6)

174

In [80]:
len(UNMATCHED_STILL)

369

In [81]:
len(GOV_HOSPITAL)

7146

In [85]:
UNMATCHED_STILL[UNMATCHED_STILL.ID.isin(matchy.ID)==False].to_csv('testing.csv', index=False)

In [112]:
dict_list_7 = dict_list_10 + dict_list_11

In [113]:
ALL = pd.merge(pd.DataFrame(dict_list_7),npi_hospitals,on='NPI')

In [114]:
ALL = pd.merge(ALL,GOV_HOSPITAL,on='ID')

In [116]:
ALL.to_csv('all_cuurent_matches.csv', index=False)

In [95]:
dict_list_5

[{'ID': 12645123, 'NPI': 1639127509},
 {'ID': 17244654, 'NPI': 1639127509},
 {'ID': 2543055, 'NPI': 1639127509},
 {'ID': 5843311, 'NPI': 1639127509},
 {'ID': 5544074, 'NPI': 1639127509},
 {'ID': 11844501, 'NPI': 1194983098},
 {'ID': 1084721, 'NPI': 1538178801},
 {'ID': 2484648, 'NPI': 1538178801},
 {'ID': 2887901, 'NPI': 1760446009},
 {'ID': 2188240, 'NPI': 1760446009},
 {'ID': 5146140, 'NPI': 1760446009},
 {'ID': 4188435, 'NPI': 1760446009},
 {'ID': 3788061, 'NPI': 1760446009},
 {'ID': 188008, 'NPI': 1760446009},
 {'ID': 5488011, 'NPI': 1760446009},
 {'ID': 1687301, 'NPI': 1548439268},
 {'ID': 1887313, 'NPI': 1740404151},
 {'ID': 887102, 'NPI': 1417927021},
 {'ID': 4387109, 'NPI': 1982799375},
 {'ID': 2789149, 'NPI': 1578850962},
 {'ID': 130345408, 'NPI': 1598099814},
 {'ID': 1784010, 'NPI': 1407832249},
 {'ID': 3884606, 'NPI': 1407832249},
 {'ID': 4289027, 'NPI': 1407832249},
 {'ID': 3284094, 'NPI': 1962412486},
 {'ID': 112789106, 'NPI': 1093981672},
 {'ID': 8132425, 'NPI': 109398167

In [101]:
ALL.head(50)['NAME_y']

0                       ADENA GREENFIELD MEDICAL CENTER
1                                     POMERENE HOSPITAL
2                             LICKING MEMORIAL HOSPITAL
3                                   MARY RUTAN HOSPITAL
4                                  MERCY ALLEN HOSPITAL
5                                   NAVAL HOSPITAL GUAM
6                              NORTHSIDE MEDICAL CENTER
7                            VALLEY VIEW MEDICAL CENTER
8                         CENTRAL VALLEY MEDICAL CENTER
9                                 SIERRA VISTA HOSPITAL
10                          LEA REGIONAL MEDICAL CENTER
11                            HANCOCK REGIONAL HOSPITAL
12                            GUADALUPE COUNTY HOSPITAL
13                         GILA REGIONAL MEDICAL CENTER
14                      PEAK BEHAVIORAL HEALTH SERVICES
15                MOUNTAIN VIEW REGIONAL MEDICAL CENTER
16     REHOBOTH MCKINLEY CHRISTIAN HEALTH CARE SERVICES
17    CROWNPOINT PUBLIC HEALTH SERVICES INDIAN H

In [141]:
bad_ids = []
for row in matchy.itertuples():
    unmatch =False
    #     add_dict = {
#         'ADDRESS':
#         'CITY':
#         'STATE':
#         'ZIP':
    if fuzz.ratio(translate_addr(row.LOCATION_ADDRESS_1),translate_addr(row.ADDRESS))<50:
        print(translate_addr(row.LOCATION_ADDRESS_1))
        print(translate_addr(row.ADDRESS))
        print('')
        unmatch = True
#     if row.CITY != row.LOCATION_CITY:
#         print(row.LOCATION_CITY)
#         print(row.CITY)
#         print('')
#         unmatch = True
#     if row.STATE != row.LOCATION_STATE:
#         print(row.STATE)
#         print(row.LOCATION_STATE)
#         print('')
#         unmatch = True
#     if row.LOCATION_ZIP[0:5] != str(row.ZIP):
#         print(row.LOCATION_ZIP[0:5])
#         print(row.ZIP)
#         print('')
    if unmatch == True:
        bad_ids.append(row.ID)
#     print('---')

1 PERKINS SQUARE
214 WEST BOWERY STREET

CORNER OF ROUTE 7 AND ROUTE 12
HIGHWAY 12 & BONITO DR, BLDG FD 3002

128 NORTH FM 3167
2573 HOSPITAL COURT

1380 EAST MEDICAL CENTER DRIVE
544 SOUTH 400 EAST (FLOOD ST)

6TH STREET AND FRANKLIN STREET
621 NORTH FRANKLIN ST, PO BOX 465

606 NORTH JEFFERSON STREET
78 HOSPITAL ROAD

802 2ND STREET NW
14 6TH AVENUE SW

911 EAST BRADY STREET
ONE HOSPITAL WAY

RR 1 BOX 11
UPPER COURT STREET

HC 65 BOX 8A
202 SOUTH FRISCO AVENUE

2200 WEST ILLINOIS AVENUE
400 ROSALIND REDFERN GROVER PARKWAY

ROSWELL PARK CANCER INSTITUTE DEPT OF
666 ELM STR

1454 LAKE SIDE AVENUE
400 CELEBRATION PLACE

H100 SANTA MARGARITA ROAD
200 MERCY CIRCLE , CAMP PENDLETON

224 NW CRANE AVENUE
309 NE MARION STREET

18302 HIGHWOODS PRESERVE PARKWAY
2550 SE WALTON ROAD

20480 MARKET STREET
9507 HOSPITAL AVENUE

HIGHWAY 8 EAST
1002 EAST MADISON STREET

200 WEST HOSPITAL DRIVE
HIGHWAY 73 MILE POST 342

5262 WOODS ROAD
POST OFFICE BOX 800

160 MAIN STREET
PO BOX 300

115 SUMMERS HOSPIT

In [142]:
len(bad_ids)

78

In [134]:
ALL[ALL.ID.isin(bad_ids)].to_csv('broken.csv', index=False)

In [ ]:
addr_translate_2 = {
    '1ST': 'FIRST',
    '2ND':'SECOND',
    '3RD': 'THIRD',
    '4TH': 'FOURTH',
    '5TH': 'FIFTH',
    '6TH': 'SIXTH',
    '7TH': 'SEVENTH',
    '8TH': 'EIGHTH',
    '9TH':'NINTH',
    'ONE': '1',
    

    
}


def translate_addr_2(addr_string):
    addr_string = addr_string.replace('.','')
    addr_string = addr_string.upper()
    new_addr = []
    
    tokens = addr_string.split()
    
    for t in tokens:
        if t in addr_translate_2:
            new_addr.append(addr_translate[t])
        else:
            new_addr.append(t)
    
    return ' '.join(new_addr)

In [ ]:
.replace(' ','')